In [1]:
# -*- coding: utf-8 -*-
from django.shortcuts import render
from django.http import HttpResponse
import string
import random
from django.utils import timezone
from django.contrib.auth.views import login as auth_login
from allauth.socialaccount.models import SocialApp
from allauth.socialaccount.templatetags.socialaccount import get_providers
from django.conf import settings
from django.shortcuts import get_object_or_404, redirect
from django.contrib.auth.decorators import login_required
from django.contrib.auth.decorators import user_passes_test
from django.dispatch import receiver
from allauth.account.signals import user_signed_up
from allauth.socialaccount.signals import social_account_added, pre_social_login

from django.utils import timezone
from django.db.models import Q
from django.contrib.auth import login, authenticate, logout
import inspect
from django.contrib.auth.models import User
from django.contrib.auth import update_session_auth_hash
from django.core.files.uploadedfile import SimpleUploadedFile
import pdfkit
import datetime
from datetime import timedelta
from django.http import JsonResponse, HttpResponseRedirect
from django.forms.models import model_to_dict
import json
from django.core import serializers
from celery import shared_task
from supporting_business.tasks import *
import xlwt
import io
import urllib
from django.contrib.sites.shortcuts import get_current_site
from django.core.mail import EmailMessage
from django.template.loader import render_to_string
from django.core.mail import send_mail, EmailMessage
from django.db import connection
from django.contrib import messages
import copy
from django.views.decorators.csrf import csrf_exempt
import itertools
from zipfile import ZipFile
import ffmpeg
import requests
import urllib.request

### for auth
try:
     # Django versions >= 1.9

    from django.utils.module_loading import import_module
except ImportError:
    # Django versions < 1.9
    from django.utils.importlib import import_module

from django.conf import settings
from django.contrib.auth import get_user
from django.contrib.auth.models import AnonymousUser
from django.contrib.auth import SESSION_KEY, BACKEND_SESSION_KEY, load_backend
from django.contrib.sessions.models import Session
from django.contrib.auth.models import User
from datetime import datetime
from django.db import reset_queries
import time
from django.db import connection
def my_timer(original_function):
    def wrapper(*args, **kwargs):
        t1 = time.time()
        reset_queries()
        result = original_function(*args, **kwargs)
        t2 = time.time() - t1
        time_sql=0.0
        for q in connection.queries:
            time_sql = float(q["time"]) + time_sql
            print(q)
        print(original_function.__name__)
        print( '총 쿼리수: {}'.format(len(connection.queries) ))
        print( '실행된 총 시간: {} 초'.format( t2))
        print('db 쿼리 시간 :  {} 초'.format(time_sql))
        print('쿼리 제외한 연산 시간 :  {} 초'.format(t2 - time_sql))
        return result
    return wrapper

def sql_sense():
    print("sql sensing")
    reset_queries()
    for q in connection.queries:
        print(q)
        
@my_timer
def test():
    start_index = int(0)
    size = int(10)
    support_business = SupportBusiness.objects.exclude(support_business_status=1).exclude(support_business_status=None)
    total = len(support_business)
    try:
        support_business_result = support_business[start_index:start_index+size]
    except Exception as e :
        print(e)
        support_business_result = ""
    k = 0
    result = {}
    result["result_set"] = []
    for s in support_business_result:
        temp = {}
        temp["mng_id"] = s.id
        temp["mng_index"] = k
        k = k + 1
        temp["mng_support_business_name"] = s.support_business_name
        temp["mng_support_business_apply_start_ymd"] = s.support_business_apply_start_ymd
        temp["mng_author"] = s.support_business_author.mng_name
        temp["mng_mng_team"] = s.support_business_author.mng_team
        temp["mng_mng_kikwan"] = s.support_business_author.mng_kikwan
        temp["mng_mng_tel"] = s.support_business_author.mng_tel
        temp["mng_apply_num"] = len(Appliance.objects.all().filter(support_business=s).filter(is_submit=True))
        temp["mng_award_num"] = len(Award.objects.all().filter(support_business=s))
        try:
            if s.support_business_status == "1":
                mng_status = "작성중"
            elif s.support_business_status == "2":
                mng_status = "승인대기중"
            elif s.support_business_status == "3":
                mng_status = "공고중"
            elif s.support_business_status == "4":
                mng_status = "모집종료"
            elif s.support_business_status == "5":
                mng_status = "공고종료"
            elif s.support_business_status == "6":
                mng_status = "블라인드중"
        except:
            print("error")
            mng_status = ""
        temp["mng_status"] = mng_status
        result["result_set"].append(copy.deepcopy(temp))
    result["total"] =total
    
test()

{'sql': 'SELECT @@SQL_AUTO_IS_NULL', 'time': '0.016'}
{'sql': 'SELECT VERSION()', 'time': '0.000'}
{'sql': "SELECT `supporting_business_supportbusiness`.`id`, `supporting_business_supportbusiness`.`support_business_author_id`, `supporting_business_supportbusiness`.`support_business_created_at_ymdt`, `supporting_business_supportbusiness`.`support_business_name`, `supporting_business_supportbusiness`.`support_business_name_tag`, `supporting_business_supportbusiness`.`support_business_name_sub`, `supporting_business_supportbusiness`.`support_business_poster`, `supporting_business_supportbusiness`.`support_business_relate_support_business_id`, `supporting_business_supportbusiness`.`support_business_short_desc`, `supporting_business_supportbusiness`.`support_business_subject`, `supporting_business_supportbusiness`.`support_business_detail`, `supporting_business_supportbusiness`.`support_business_apply_start_ymd`, `supporting_business_supportbusiness`.`support_business_apply_end_ymdt`, `supp

In [2]:
@my_timer
def test_2():
    start_index = int(0)
    size = int(10)
    support_business = SupportBusiness.objects.exclude(support_business_status__in=[1,None]).select_related("support_business_author")
    total = len(support_business)
    try:
        support_business_result = support_business[start_index:start_index+size]
    except Exception as e :
        print(e)
        support_business_result = ""
    k = 0
    result = {}
    result["result_set"] = []
    for s in support_business_result:
        temp = {}
        temp["mng_id"] = s.id
        temp["mng_index"] = k
        k = k + 1
        temp["mng_support_business_name"] = s.support_business_name
        temp["mng_support_business_apply_start_ymd"] = s.support_business_apply_start_ymd
        temp["mng_author"] = s.support_business_author.mng_name
        temp["mng_mng_team"] = s.support_business_author.mng_team
        temp["mng_mng_kikwan"] = s.support_business_author.mng_kikwan
        temp["mng_mng_tel"] = s.support_business_author.mng_tel
        temp["mng_apply_num"] = (Appliance.objects.filter(support_business=s,is_submit=True)).count()
        temp["mng_award_num"] = (Award.objects.filter(support_business=s)).count()
        mng_status = ""
        try:
            if s.support_business_status == "1":
                mng_status = "작성중"
            elif s.support_business_status == "2":
                mng_status = "승인대기중"
            elif s.support_business_status == "3":
                mng_status = "공고중"
            elif s.support_business_status == "4":
                mng_status = "모집종료"
            elif s.support_business_status == "5":
                mng_status = "공고종료"
            elif s.support_business_status == "6":
                mng_status = "블라인드중"
        except:
            print("error")
            mng_status = ""
        temp["mng_status"] = mng_status
        result["result_set"].append(copy.deepcopy(temp))
    result["total"] =total
    
test_2()

{'sql': "SELECT `supporting_business_supportbusiness`.`id`, `supporting_business_supportbusiness`.`support_business_author_id`, `supporting_business_supportbusiness`.`support_business_created_at_ymdt`, `supporting_business_supportbusiness`.`support_business_name`, `supporting_business_supportbusiness`.`support_business_name_tag`, `supporting_business_supportbusiness`.`support_business_name_sub`, `supporting_business_supportbusiness`.`support_business_poster`, `supporting_business_supportbusiness`.`support_business_relate_support_business_id`, `supporting_business_supportbusiness`.`support_business_short_desc`, `supporting_business_supportbusiness`.`support_business_subject`, `supporting_business_supportbusiness`.`support_business_detail`, `supporting_business_supportbusiness`.`support_business_apply_start_ymd`, `supporting_business_supportbusiness`.`support_business_apply_end_ymdt`, `supporting_business_supportbusiness`.`support_business_object`, `supporting_business_supportbusiness`.`

In [3]:
import re
@my_timer
def startup_list_by_or():
    filter_list = ["출판","일러스트","스타트업","VR","3년 이내","15명 이하"]
    result = Startup.objects.all().exclude(company_name="").exclude(company_name=None)
    startup_set =[]
    startup_list = []
    for filter in filter_list:
        if filter == "구성원 제한없음":
            pass
        elif "명 이하" in filter or "명 이상" in filter:
            # x 명이 있는 경우에는 구성원을 입력하지 않은 스타트업을 추가해주어야함
            num = int(re.findall('\d+', filter)[0])
            if (num != 0):
                result = copy.deepcopy(result.filter(company_total_employee__lte=num).exclude(company_name="").exclude(
                    company_name=None)) | Startup.objects.all().filter(company_total_employee=None)
        elif filter != None and filter != "":
            for s in result.filter(selected_company_filter_list__filter_name__in=filter_list):
                if s not in startup_list:
                    startup_list.append(s)

    for s in startup_list:
        temp_obj = {}
        temp_obj["company_name"] = s.company_name
        temp_obj["logo"] = s.logo
        temp_obj["company_short_desc"] = s.company_short_desc
        try:
            temp_obj["is_favored"] = is_in_favor_list("startup", s.id, request.POST.get("id"))
        except:
            temp_obj["is_favored"] = False
        temp_obj["filter"] = []
        temp_obj["id"] = s.id
        temp_obj["sim"]=0
        for t in s.selected_company_filter_list.all():
            if t.filter_name != "" and t.filter_name != None and t.cat_0 != "지원형태" and t.cat_1 != "기업형태":
                temp_obj["filter"].append(t.filter_name)
        for f in filter_list:
            for f_s in s.selected_company_filter_list.all():
                if f == f_s.filter_name:
                    temp_obj["sim"] = temp_obj["sim"] + 1

        startup_set.append(copy.deepcopy(temp_obj))

    return JsonResponse(startup_set, safe=False)
startup_list_by_or()

{'sql': "SELECT `supporting_business_startup`.`id`, `supporting_business_startup`.`user_id`, `supporting_business_startup`.`company_name`, `supporting_business_startup`.`established_date`, `supporting_business_startup`.`logo`, `supporting_business_startup`.`back_img`, `supporting_business_startup`.`company_short_desc`, `supporting_business_startup`.`company_intro`, `supporting_business_startup`.`company_youtube`, `supporting_business_startup`.`company_facebook`, `supporting_business_startup`.`company_instagram`, `supporting_business_startup`.`company_website`, `supporting_business_startup`.`address_0`, `supporting_business_startup`.`address_1`, `supporting_business_startup`.`repre_name`, `supporting_business_startup`.`repre_email`, `supporting_business_startup`.`repre_tel`, `supporting_business_startup`.`mark_name`, `supporting_business_startup`.`mark_email`, `supporting_business_startup`.`mark_tel`, `supporting_business_startup`.`company_keyword`, `supporting_business_startup`.`compan

<JsonResponse status_code=200, "application/json">

In [4]:
@my_timer
def startup_list_by_or():
    filter_list = ["출판","일러스트","스타트업","VR","3년 이내","15명 이하"]
    result = Startup.objects.exclude(company_name__in=["",None])
    startup_set =[]
    startup_list = []
    for filter in filter_list:
        if filter == "구성원 제한없음":
            pass
        elif "명 이하" in filter or "명 이상" in filter:
            # x 명이 있는 경우에는 구성원을 입력하지 않은 스타트업을 추가해주어야함
            num = int(re.findall('\d+', filter)[0])
            if (num != 0):
                result = copy.deepcopy(result.filter(company_total_employee__lte=num)) | \
                Startup.objects.filter(company_total_employee=None)
        elif filter != None and filter != "":
            for s in result.filter(selected_company_filter_list__filter_name__in=filter_list):
                if s not in startup_list:
                    startup_list.append(s)

    for s in startup_list:
        temp_obj = {}
        temp_obj["company_name"] = s.company_name
        temp_obj["logo"] = s.logo
        temp_obj["company_short_desc"] = s.company_short_desc
        try:
            temp_obj["is_favored"] = is_in_favor_list("startup", s.id, request.POST.get("id"))
        except:
            temp_obj["is_favored"] = False
        temp_obj["filter"] = []
        temp_obj["id"] = s.id
        temp_obj["sim"]=0
        for t in s.selected_company_filter_list.exclude(cat_0="지원형태",cat_1 = "기업형태" ):
            temp_obj["filter"].append(t.filter_name)
        temp_obj["sim"] = s.selected_company_filter_list.filter(filter_name__in=filter_list).count()
        startup_set.append(copy.deepcopy(temp_obj))
    return JsonResponse(startup_set, safe=False)
startup_list_by_or()

{'sql': "SELECT `supporting_business_startup`.`id`, `supporting_business_startup`.`user_id`, `supporting_business_startup`.`company_name`, `supporting_business_startup`.`established_date`, `supporting_business_startup`.`logo`, `supporting_business_startup`.`back_img`, `supporting_business_startup`.`company_short_desc`, `supporting_business_startup`.`company_intro`, `supporting_business_startup`.`company_youtube`, `supporting_business_startup`.`company_facebook`, `supporting_business_startup`.`company_instagram`, `supporting_business_startup`.`company_website`, `supporting_business_startup`.`address_0`, `supporting_business_startup`.`address_1`, `supporting_business_startup`.`repre_name`, `supporting_business_startup`.`repre_email`, `supporting_business_startup`.`repre_tel`, `supporting_business_startup`.`mark_name`, `supporting_business_startup`.`mark_email`, `supporting_business_startup`.`mark_tel`, `supporting_business_startup`.`company_keyword`, `supporting_business_startup`.`compan

<JsonResponse status_code=200, "application/json">

In [5]:
@my_timer
def vue_get_startup_detail():
   
    startup = Startup.objects.get(user=AdditionalUserInfo.objects.get(id=74).user)
    result = {}
    result["back_img"] = startup.back_img
    result["logo"] = startup.logo
    result["company_website"] = startup.company_website
    result["company_youtube"] = startup.company_youtube
    result["company_instagram"] = startup.company_instagram
    result["company_facebook"] = startup.company_facebook
    result["company_keyword"] = startup.company_keyword
    result["established_date"]= startup.established_date
    result["company_short_desc"] = startup.company_short_desc
    result["company_intro"] = startup.company_intro
    result["select_tag"]= []
    for f in startup.selected_company_filter_list.all():
        result["select_tag"].append(f.filter_name)
    result["startup_id"] = startup.id
    result["mark_tel"]=startup.mark_tel
    result["company_name"] = startup.company_name
    result["company_kind"] = startup.company_kind
    result["mark_name"] = startup.mark_name
    result["mark_email"] = startup.mark_email
    result["intro_tag"] = []
    result["select_tag"] = []
    for f in startup.selected_company_filter_list.all():
        if f.cat_0 != "지원형태" and f.cat_1!="기업형태":
            result["intro_tag"].append(f.filter_name)
            result["select_tag"].append(f.filter_name)
    if startup.company_total_employee != "":
        result["intro_tag"].append(startup.company_total_employee + "명 이하")
    result["information"] = {}
    result["information"]["id"] = startup.id
    result["information"]["tag"] = []
    result["support_business_tag"]=[]
    for f in startup.selected_company_filter_list.all():
        if f.cat_0=="지원형태":
            result["support_business_tag"].append(f.filter_name)
    result["select_tag"]= []
    for f in startup.selected_company_filter_list.all():
        result["information"]["tag"].append(f.filter_name)
    for t in startup.selected_company_filter_list.all():
        if t.filter_name != "" and t.filter_name != None:
            result["information"]["tag"].append(t.filter_name)
    result['information']["company_website"] = startup.company_website
    result["information"]["repre_email"] =  startup.user.username
    result["address_0"] = startup.address_0
    result["address_1"] = startup.address_1
    result["ip_chk"] = startup.ip_chk
    result["revenue_chk"] = startup.revenue_chk
    result["export_chk"] = startup.export_chk
    result["company_invest_chk"] = startup.company_invest_chk
    result["service"] = []
    result["tag"] = []
    result["pub_tag"]=[]
    for f in startup.selected_company_filter_list.all():
        result["tag"].append(f.filter_name)
    if startup.company_total_employee != "" :
        result["pub_tag"].append( startup.company_total_employee +"명 이하")
        result["tag"].append( startup.company_total_employee +"명 이하")
    for f in startup.selected_company_filter_list.all():
        if f.cat_0!='조건' and f.cat_1 != '기업형태':
            result["pub_tag"].append(f.filter_name)
    for service  in startup.service_set.all():
        obj = {}
        obj["service_intro"] = service.service_intro
        obj["service_file"] = service.service_file
        obj["file_name"] = service.service_file.split("/")[-1]
        obj["service_name"] = service.service_name
        obj["service_img"] = service.service_img
        obj["img_name"] = service.service_img.split("/")[-1]
        obj["id"] = service.id
        result["service"].append(copy.deepcopy(obj))
    result["company_history"] = []
    for history in startup.history_set.all():
        obj = {}
        obj["company_history_year"] = history.company_history_year
        obj["company_history_month"] = history.company_history_month
        obj["company_history_content"] = history.company_history_content
        obj["id"] = history.id
        result["company_history"].append(copy.deepcopy(obj))
    result["revenue_before_year_0"] = startup.revenue_before_year_0
    result["revenue_before_year_1"] = startup.revenue_before_year_1
    result["revenue_before_year_2"] = startup.revenue_before_year_2
    result["revenue_before_0"] = startup.revenue_before_0
    result["revenue_before_1"] = startup.revenue_before_1
    result["revenue_before_2"] = startup.revenue_before_2
    result["export_before_year_0"] = startup.export_before_year_0
    result["export_before_year_1"] = startup.export_before_year_1
    result["export_before_year_2"] = startup.export_before_year_2
    result["export_before_0"] = startup.export_before_0
    result["export_before_1"] = startup.export_before_1
    result["export_before_2"] = startup.export_before_2
    result["export_before_nation_0"] = startup.export_before_nation_0
    result["export_before_nation_1"] = startup.export_before_nation_1
    result["export_before_nation_2"] = startup.export_before_nation_2
    result["attached_cert_file"]= startup.attached_cert_file
    result["attached_ip_file"] = startup.attached_ip_file
    result["invest"] = []
    for invest in startup.companyinvest_set.all():
        obj = {}
        obj["company_invest_year"] = invest.company_invest_year
        obj["company_invest_size"] = invest.company_invest_size
        obj["company_invest_agency"] = invest.company_invest_agency
        result["invest"].append(copy.deepcopy(obj))
    result["news"] = []
    for news in startup.activity_set.order_by("-company_activity_created_at").all():
        obj = {}
        obj["company_activity_created_at"] = news.company_activity_created_at
        obj["company_activity_text"] = news.company_activity_text
        obj["company_activity_img"] = news.company_activity_img
        obj["company_activity_youtube"] = news.company_activity_youtube
        obj["like_num"] = (news.activitylike_set.all()).count()
        obj["rep_num"] = (news.reply_set.all()).count()
        obj["id"] = news.id
        obj["rep"] = []
        for rep in news.reply_set.all():
            temp = {}
            # temp["logo"] = rep.activity.startup.clip_thumbnail
            temp["company_activity_text"] = rep.company_activity_text
            temp["company_activity_created_at"] = rep.company_activity_created_at
            temp["rep_author"] = rep.company_activity_author.user.username
            temp["id"] = rep.id
            obj["rep"].append(copy.deepcopy(temp))
        result["news"].append(copy.deepcopy(obj))
    print("end")
    return JsonResponse(result)
vue_get_startup_detail()

end
{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_bu

<JsonResponse status_code=200, "application/json">

In [6]:
@my_timer
def vue_get_startup_detail():
   
    startup = Startup.objects.filter(user=AdditionalUserInfo.objects.get(id=74).user)\
    .prefetch_related("selected_company_filter_list").prefetch_related("service_set").prefetch_related("history_set")\
    .prefetch_related("companyinvest_set").prefetch_related("activity_set").select_related("user").last()
    result = {}
    result["information"] = {}
    result["information"]["id"] = startup.id
    result["information"]["tag"] = []
    result["tag"] = []
    result["back_img"] = startup.back_img
    result["logo"] = startup.logo
    result["company_website"] = startup.company_website
    result["company_youtube"] = startup.company_youtube
    result["company_instagram"] = startup.company_instagram
    result["company_facebook"] = startup.company_facebook
    result["company_keyword"] = startup.company_keyword
    result["established_date"]= startup.established_date
    result["company_short_desc"] = startup.company_short_desc
    result["company_intro"] = startup.company_intro
    result["select_tag"]= []
    for f in startup.selected_company_filter_list.all():
        result["select_tag"].append(f.filter_name)
        result["information"]["tag"].append(f.filter_name)
        result["tag"].append(f.filter_name)
    result["startup_id"] = startup.id
    result["mark_tel"]=startup.mark_tel
    result["company_name"] = startup.company_name
    result["company_kind"] = startup.company_kind
    result["mark_name"] = startup.mark_name
    result["mark_email"] = startup.mark_email
    result["intro_tag"] = []
    result["select_tag"] = []
    for f in startup.selected_company_filter_list.exclude(cat_0 = "지원형태",cat_1="기업형태"):
        result["intro_tag"].append(f.filter_name)
        result["select_tag"].append(f.filter_name)
    if startup.company_total_employee != "":
        result["intro_tag"].append(startup.company_total_employee + "명 이하")       
    result["support_business_tag"]=[]
    for f in startup.selected_company_filter_list.filter(cat_0="지원형태"):
        result["support_business_tag"].append(f.filter_name)
    result["select_tag"]= []
    result['information']["company_website"] = startup.company_website
    result["information"]["repre_email"] =  startup.user.username
    result["address_0"] = startup.address_0
    result["address_1"] = startup.address_1
    result["ip_chk"] = startup.ip_chk
    result["revenue_chk"] = startup.revenue_chk
    result["export_chk"] = startup.export_chk
    result["company_invest_chk"] = startup.company_invest_chk
    result["service"] = []
   
    result["pub_tag"]=[]
 
   
    if startup.company_total_employee != "" :
        result["pub_tag"].append( startup.company_total_employee +"명 이하")
        result["tag"].append( startup.company_total_employee +"명 이하")
    for f in startup.selected_company_filter_list.exclude(cat_0='조건',cat_1 = '기업형태' ):
        result["pub_tag"].append(f.filter_name)
    for service  in startup.service_set.all():
        obj = {}
        obj["service_intro"] = service.service_intro
        obj["service_file"] = service.service_file
        obj["file_name"] = service.service_file.split("/")[-1]
        obj["service_name"] = service.service_name
        obj["service_img"] = service.service_img
        obj["img_name"] = service.service_img.split("/")[-1]
        obj["id"] = service.id
        result["service"].append(copy.deepcopy(obj))
    result["company_history"] = []
    for history in startup.history_set.all():
        obj = {}
        obj["company_history_year"] = history.company_history_year
        obj["company_history_month"] = history.company_history_month
        obj["company_history_content"] = history.company_history_content
        obj["id"] = history.id
        result["company_history"].append(copy.deepcopy(obj))
    result["revenue_before_year_0"] = startup.revenue_before_year_0
    result["revenue_before_year_1"] = startup.revenue_before_year_1
    result["revenue_before_year_2"] = startup.revenue_before_year_2
    result["revenue_before_0"] = startup.revenue_before_0
    result["revenue_before_1"] = startup.revenue_before_1
    result["revenue_before_2"] = startup.revenue_before_2
    result["export_before_year_0"] = startup.export_before_year_0
    result["export_before_year_1"] = startup.export_before_year_1
    result["export_before_year_2"] = startup.export_before_year_2
    result["export_before_0"] = startup.export_before_0
    result["export_before_1"] = startup.export_before_1
    result["export_before_2"] = startup.export_before_2
    result["export_before_nation_0"] = startup.export_before_nation_0
    result["export_before_nation_1"] = startup.export_before_nation_1
    result["export_before_nation_2"] = startup.export_before_nation_2
    result["attached_cert_file"]= startup.attached_cert_file
    result["attached_ip_file"] = startup.attached_ip_file
    result["invest"] = []
    for invest in startup.companyinvest_set.all():
        obj = {}
        obj["company_invest_year"] = invest.company_invest_year
        obj["company_invest_size"] = invest.company_invest_size
        obj["company_invest_agency"] = invest.company_invest_agency
        result["invest"].append(copy.deepcopy(obj))
    result["news"] = []
    for news in startup.activity_set.order_by("-company_activity_created_at").all()\
    .prefetch_related("activitylike_set").prefetch_related("reply_set"):
        obj = {}
        obj["company_activity_created_at"] = news.company_activity_created_at
        obj["company_activity_text"] = news.company_activity_text
        obj["company_activity_img"] = news.company_activity_img
        obj["company_activity_youtube"] = news.company_activity_youtube
        obj["like_num"] = (news.activitylike_set).count()
        obj["rep_num"] = (news.reply_set).count()
        obj["id"] = news.id
        obj["rep"] = []
        for rep in news.reply_set.select_related("company_activity_author__user"):
            temp = {}
            # temp["logo"] = rep.activity.startup.clip_thumbnail
            temp["company_activity_text"] = rep.company_activity_text
            temp["company_activity_created_at"] = rep.company_activity_created_at
            temp["rep_author"] = rep.company_activity_author.user.username
            temp["id"] = rep.id
            obj["rep"].append(copy.deepcopy(temp))
        result["news"].append(copy.deepcopy(obj))
    print("end")
    return JsonResponse(result)
vue_get_startup_detail()

end
{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_bu

<JsonResponse status_code=200, "application/json">

In [7]:
@my_timer
def vue_get_support_business_appliance():
  
    support_business = SupportBusiness.objects.get(id=161)
    ap = Appliance.objects.filter(support_business=support_business).filter(is_submit=True)
    k=1
    result = []
    for a in ap :
        temp={}
        temp["index"] = k
        k=k+1
        temp["company_name"] = a.startup.company_name
        temp["company_kind"] = a.startup.company_kind
        temp["company_id"] = a.startup.id
        temp["id"] = a.id
        temp["mark_name"] = a.startup.mark_name
        temp["mark_email"] = a.startup.mark_email
        temp["mark_tel"] = a.startup.mark_tel
        temp["appliance_update_at_ymdt"] = a.appliance_update_at_ymdt
        temp["down_path"] = a.id
        result.append(copy.deepcopy(temp))
     
    return JsonResponse(result,safe=False)
vue_get_support_business_appliance()

{'sql': 'SELECT `supporting_business_supportbusiness`.`id`, `supporting_business_supportbusiness`.`support_business_author_id`, `supporting_business_supportbusiness`.`support_business_created_at_ymdt`, `supporting_business_supportbusiness`.`support_business_name`, `supporting_business_supportbusiness`.`support_business_name_tag`, `supporting_business_supportbusiness`.`support_business_name_sub`, `supporting_business_supportbusiness`.`support_business_poster`, `supporting_business_supportbusiness`.`support_business_relate_support_business_id`, `supporting_business_supportbusiness`.`support_business_short_desc`, `supporting_business_supportbusiness`.`support_business_subject`, `supporting_business_supportbusiness`.`support_business_detail`, `supporting_business_supportbusiness`.`support_business_apply_start_ymd`, `supporting_business_supportbusiness`.`support_business_apply_end_ymdt`, `supporting_business_supportbusiness`.`support_business_object`, `supporting_business_supportbusiness`.`

<JsonResponse status_code=200, "application/json">

In [8]:
@my_timer
def vue_get_support_business_appliance():
  
    support_business = SupportBusiness.objects.get(id=161)
    ap = Appliance.objects.filter(support_business=support_business,is_submit=True).select_related("startup")
    k=1
    result = []
    for a in ap :
        temp={}
        temp["index"] = k
        k=k+1
        temp["company_name"] = a.startup.company_name
        temp["company_kind"] = a.startup.company_kind
        temp["company_id"] = a.startup.id
        temp["id"] = a.id
        temp["mark_name"] = a.startup.mark_name
        temp["mark_email"] = a.startup.mark_email
        temp["mark_tel"] = a.startup.mark_tel
        temp["appliance_update_at_ymdt"] = a.appliance_update_at_ymdt
        temp["down_path"] = a.id
        result.append(copy.deepcopy(temp))
     
    return JsonResponse(result,safe=False)
vue_get_support_business_appliance()

{'sql': 'SELECT `supporting_business_supportbusiness`.`id`, `supporting_business_supportbusiness`.`support_business_author_id`, `supporting_business_supportbusiness`.`support_business_created_at_ymdt`, `supporting_business_supportbusiness`.`support_business_name`, `supporting_business_supportbusiness`.`support_business_name_tag`, `supporting_business_supportbusiness`.`support_business_name_sub`, `supporting_business_supportbusiness`.`support_business_poster`, `supporting_business_supportbusiness`.`support_business_relate_support_business_id`, `supporting_business_supportbusiness`.`support_business_short_desc`, `supporting_business_supportbusiness`.`support_business_subject`, `supporting_business_supportbusiness`.`support_business_detail`, `supporting_business_supportbusiness`.`support_business_apply_start_ymd`, `supporting_business_supportbusiness`.`support_business_apply_end_ymdt`, `supporting_business_supportbusiness`.`support_business_object`, `supporting_business_supportbusiness`.`

<JsonResponse status_code=200, "application/json">

In [9]:
from django.utils import timezone
@my_timer
def vue_get_support_business_select_name_by_kikwan_1():

    support_business_list = []
    for sp in SupportBusiness.objects.filter( Q(support_business_status="3") ).filter(support_business_apply_end_ymdt__gte=timezone.now()):
        support_business_list.append({
            "author": sp.support_business_author.mng_name,
            "author_id": sp.support_business_author.id,
            "name": sp.support_business_name,
            "support_business_id": sp.id,
            "support_business_status": sp.support_business_status
        })
    return JsonResponse(support_business_list, safe=False)
vue_get_support_business_select_name_by_kikwan_1()

{'sql': "SELECT `supporting_business_supportbusiness`.`id`, `supporting_business_supportbusiness`.`support_business_author_id`, `supporting_business_supportbusiness`.`support_business_created_at_ymdt`, `supporting_business_supportbusiness`.`support_business_name`, `supporting_business_supportbusiness`.`support_business_name_tag`, `supporting_business_supportbusiness`.`support_business_name_sub`, `supporting_business_supportbusiness`.`support_business_poster`, `supporting_business_supportbusiness`.`support_business_relate_support_business_id`, `supporting_business_supportbusiness`.`support_business_short_desc`, `supporting_business_supportbusiness`.`support_business_subject`, `supporting_business_supportbusiness`.`support_business_detail`, `supporting_business_supportbusiness`.`support_business_apply_start_ymd`, `supporting_business_supportbusiness`.`support_business_apply_end_ymdt`, `supporting_business_supportbusiness`.`support_business_object`, `supporting_business_supportbusiness`.`

<JsonResponse status_code=200, "application/json">

In [10]:
from django.utils import timezone
@my_timer
def vue_get_support_business_select_name_by_kikwan_1():

    support_business_list = []
    for sp in SupportBusiness.objects.filter(support_business_status="3",support_business_apply_end_ymdt__gte=timezone.now()).select_related("support_business_author"):
        support_business_list.append({
            "author": sp.support_business_author.mng_name,
            "author_id": sp.support_business_author.id,
            "name": sp.support_business_name,
            "support_business_id": sp.id,
            "support_business_status": sp.support_business_status
        })
    return JsonResponse(support_business_list, safe=False)
vue_get_support_business_select_name_by_kikwan_1()

{'sql': "SELECT `supporting_business_supportbusiness`.`id`, `supporting_business_supportbusiness`.`support_business_author_id`, `supporting_business_supportbusiness`.`support_business_created_at_ymdt`, `supporting_business_supportbusiness`.`support_business_name`, `supporting_business_supportbusiness`.`support_business_name_tag`, `supporting_business_supportbusiness`.`support_business_name_sub`, `supporting_business_supportbusiness`.`support_business_poster`, `supporting_business_supportbusiness`.`support_business_relate_support_business_id`, `supporting_business_supportbusiness`.`support_business_short_desc`, `supporting_business_supportbusiness`.`support_business_subject`, `supporting_business_supportbusiness`.`support_business_detail`, `supporting_business_supportbusiness`.`support_business_apply_start_ymd`, `supporting_business_supportbusiness`.`support_business_apply_end_ymdt`, `supporting_business_supportbusiness`.`support_business_object`, `supporting_business_supportbusiness`.`

<JsonResponse status_code=200, "application/json">

In [11]:
@my_timer
def vue_get_startup_public_detail():
    startup = Startup.objects.get(id=74)
    result = {}
    result["back_img"] = startup.back_img
    result["logo"] = startup.logo
    result["company_website"] = startup.company_website
    result["company_id"] = startup.id
    try:
        result["is_favored"]= is_in_favor_list("startup", startup.id, user_auth_id)
    except:
        result["is_favored"] = False
    result["company_youtube"] = startup.company_youtube
    result["company_instagram"] = startup.company_instagram
    result["company_facebook"] = startup.company_facebook
    result["company_keyword"] = startup.company_keyword
    result["established_date"] = startup.established_date
    result["company_short_desc"] = startup.company_short_desc
    result["company_intro"] = startup.company_intro
    result["select_tag"] = []
    for f in startup.selected_company_filter_list.all():
        result["select_tag"].append(f.filter_name)
    result["startup_id"] = startup.id
    result["mark_tel"] = startup.mark_tel
    result["company_name"] = startup.company_name
    result["company_kind"] = startup.company_kind


    result["mark_name"] = startup.mark_name
    result["mark_email"] = startup.mark_email if startup.mark_email != "" else startup.user.username

    # result["logo"] = startup.clip_thumbnail_selected_company_filter_list

    result["information"] = {}
    result["information"]["id"] = startup.id
    result["information"]["tag"] = []
    result["support_business_tag"] = []
    for f in startup.selected_company_filter_list.all():
        if f.cat_0 == "지원형태":
            result["support_business_tag"].append(f.filter_name)
    result["select_tag"] = []

    for f in startup.selected_company_filter_list.all():
        result["information"]["tag"].append(f.filter_name)

    for t in startup.selected_company_filter_list.all():
        if t.filter_name != "" and t.filter_name != None:
            result["information"]["tag"].append(t.filter_name)
    result['information']["company_website"] = startup.company_website
    result["information"]["mark_email"] = startup.mark_email if startup.mark_email != "" else startup.user.username
    result["address_0"] = startup.address_0
    result["address_1"] = startup.address_1
    result["ip_chk"] = startup.ip_chk
    result["revenue_chk"] = startup.revenue_chk
    result["export_chk"] = startup.export_chk
    result["company_invest_chk"] = startup.company_invest_chk
    result["service"] = []

    result["tag"] = []
    result["pub_tag"] = []
    for f in startup.selected_company_filter_list.all():
        result["tag"].append(f.filter_name)
    for f in startup.selected_company_filter_list.all():
        if f.cat_0!="지원조건" and f.cat_1!="기업형태":
            result["pub_tag"].append(f.filter_name)

    for service in startup.service_set.all():
        obj = {}
        obj["service_intro"] = service.service_intro
        obj["service_file"] = service.service_file
        obj["file_name"] = service.service_file.split("/")[-1]
        obj["service_name"] = service.service_name
        obj["service_img"] = service.service_img
        obj["img_name"] = service.service_img.split("/")[-1]
        obj["id"] = service.id
        result["service"].append(copy.deepcopy(obj))
    result["company_history"] = []
    for history in startup.history_set.all():
        obj = {}
        obj["company_history_year"] = history.company_history_year
        obj["company_history_month"] = history.company_history_month
        obj["company_history_content"] = history.company_history_content
        obj["id"] = history.id
        result["company_history"].append(copy.deepcopy(obj))

    result["revenue_before_year_0"] = startup.revenue_before_year_0
    result["revenue_before_year_1"] = startup.revenue_before_year_1
    result["revenue_before_year_2"] = startup.revenue_before_year_2
    result["revenue_before_0"] = startup.revenue_before_0
    result["revenue_before_1"] = startup.revenue_before_1
    result["revenue_before_2"] = startup.revenue_before_2

    result["export_before_year_0"] = startup.export_before_year_0
    result["export_before_year_1"] = startup.export_before_year_1
    result["export_before_year_2"] = startup.export_before_year_2
    result["export_before_0"] = startup.export_before_0
    result["export_before_1"] = startup.export_before_1
    result["export_before_2"] = startup.export_before_2
    result["export_before_nation_0"] = startup.export_before_nation_0
    result["export_before_nation_1"] = startup.export_before_nation_1
    result["export_before_nation_2"] = startup.export_before_nation_2
    result["attached_cert_file"] = startup.attached_cert_file
    result["attached_ip_file"] = startup.attached_ip_file

    result["invest"] = []

    for invest in startup.companyinvest_set.all():
        obj = {}
        obj["company_invest_year"] = invest.company_invest_year
        obj["company_invest_size"] = invest.company_invest_size
        obj["company_invest_agency"] = invest.company_invest_agency
        result["invest"].append(copy.deepcopy(obj))

    result["news"] = []
    for news in startup.activity_set.order_by("-company_activity_created_at").all():
        obj = {}
        obj["company_activity_created_at"] = news.company_activity_created_at
        obj["company_activity_text"] = news.company_activity_text
        obj["company_activity_img"] = news.company_activity_img
        obj["company_activity_youtube"] = news.company_activity_youtube
        obj["like_num"] = (news.activitylike_set.all()).count()
        obj["rep_num"] = (news.reply_set.all()).count()
        obj["id"] = news.id

        obj["rep"] = []
        for rep in news.reply_set.all():
            temp = {}
            # temp["logo"] = rep.activity.startup.clip_thumbnail
            temp["company_activity_text"] = rep.company_activity_text
            temp["company_activity_created_at"] = rep.company_activity_created_at
            temp["id"] = rep.id
            obj["rep"].append(copy.deepcopy(temp))
        result["news"].append(copy.deepcopy(obj))
    print("end")
    return JsonResponse(result)
vue_get_startup_public_detail()

end
{'sql': 'SELECT `supporting_business_startup`.`id`, `supporting_business_startup`.`user_id`, `supporting_business_startup`.`company_name`, `supporting_business_startup`.`established_date`, `supporting_business_startup`.`logo`, `supporting_business_startup`.`back_img`, `supporting_business_startup`.`company_short_desc`, `supporting_business_startup`.`company_intro`, `supporting_business_startup`.`company_youtube`, `supporting_business_startup`.`company_facebook`, `supporting_business_startup`.`company_instagram`, `supporting_business_startup`.`company_website`, `supporting_business_startup`.`address_0`, `supporting_business_startup`.`address_1`, `supporting_business_startup`.`repre_name`, `supporting_business_startup`.`repre_email`, `supporting_business_startup`.`repre_tel`, `supporting_business_startup`.`mark_name`, `supporting_business_startup`.`mark_email`, `supporting_business_startup`.`mark_tel`, `supporting_business_startup`.`company_keyword`, `supporting_business_startup`.`co

<JsonResponse status_code=200, "application/json">

In [12]:
@my_timer
def vue_home_support_business():

    tag_list =  ["출판","일러스트","스타트업","VR","3년 이내","15명 이하"]
    result={}
    print(tag_list)
    result["data"]=[]
    data=[]
    support_business_set = SupportBusiness.objects.filter(support_business_status=3)#.filter(support_business_apply_end_ymdt__gte=timezone.now())#.exclude(support_business_status=None).exclude(Q(support_business_status=1)|(Q(support_business_status=2)|(Q(support_business_status=6))))
    for filter in tag_list:
        if filter != "" and filter != None:
            if "명 이하" in filter or "명 이상" in filter:
                num = int(re.findall('\d+', filter)[0])
                if num != 0:
                    support_business_set = support_business_set.filter(support_business_employee_condition__lte=num)
                else:
                    pass
            elif filter!="구성원 제한없음":
                support_business_set = support_business_set.filter(selected_support_business_filter_list__filter_name = filter)
    for support_business in support_business_set:
        obj = {}
        obj["tag"] = []
        obj["support_business_name"] = support_business.support_business_name
        obj["id"] = support_business.id
        obj["support_business_poster"] = support_business.support_business_poster
        try:
            obj["is_favored"] = is_in_favor_list("support_business", support_business.id , user_auth_id)
        except:
            obj["is_favored"] = False
        obj["support_business_apply_end_ymdt"] = (support_business.support_business_apply_end_ymdt)
        obj["support_business_short_desc"] = support_business.support_business_short_desc
        obj["favorite"] =  (support_business.additionaluserinfo_set.all()).count()
        obj["comp"]=""


        if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
            number =  str(round((
                Appliance.objects.filter(support_business_id=support_business.id).filter(is_submit=True)).count() / int(
                support_business.support_business_recruit_size), 1))
            if number == "0.0":
                number ="0"
            obj["comp"] = number + " : 1"

        else:
            obj["comp"] = ""

        obj["selected_support_business_filter_list"]=[]
        print(obj["selected_support_business_filter_list"])
        for s in support_business.selected_support_business_filter_list.all():
            obj["selected_support_business_filter_list"].append(s.filter_name)
        obj["rec"]=0

        for f in support_business.selected_support_business_filter_list.all():
            obj["tag"].append(f.filter_name)
            if f.filter_name in tag_list:
                obj["rec"]= obj["rec"]+1


        # if random.randrange(0,10)%2==0:
        #     obj["img"] = img_list[random.randrange(0,9)]

        result["data"].append(copy.deepcopy(obj))
    try:
        if gca_check_session(request) != False:
            user_id = gca_check_session(request)
            user_startup = Startup.objects.get(user = AdditionalUserInfo.objects.get(id=user_id).user)
            result["usr_filter"] = []
            for f in user_startup.selected_company_filter_list.all():
                result["usr_filter"].append(f.filter_name)
            print(result['usr_filter'])
    except:
        pass
    return JsonResponse(result)
vue_home_support_business()


['출판', '일러스트', '스타트업', 'VR', '3년 이내', '15명 이하']
[]
[]
[]
[]
{'sql': "SELECT `supporting_business_supportbusiness`.`id`, `supporting_business_supportbusiness`.`support_business_author_id`, `supporting_business_supportbusiness`.`support_business_created_at_ymdt`, `supporting_business_supportbusiness`.`support_business_name`, `supporting_business_supportbusiness`.`support_business_name_tag`, `supporting_business_supportbusiness`.`support_business_name_sub`, `supporting_business_supportbusiness`.`support_business_poster`, `supporting_business_supportbusiness`.`support_business_relate_support_business_id`, `supporting_business_supportbusiness`.`support_business_short_desc`, `supporting_business_supportbusiness`.`support_business_subject`, `supporting_business_supportbusiness`.`support_business_detail`, `supporting_business_supportbusiness`.`support_business_apply_start_ymd`, `supporting_business_supportbusiness`.`support_business_apply_end_ymdt`, `supporting_business_supportbusiness`.`suppo

<JsonResponse status_code=200, "application/json">

In [78]:
@my_timer
def get_support_business_detail():

    support_business = SupportBusiness.objects.get(id=1)
    result = {}
    result["support_business_name"] = support_business.support_business_name
    result["mng_name"] = support_business.support_business_author.mng_name
    result["mng_email"] = support_business.support_business_author.user.username
    result["mng_tel"] = support_business.support_business_author.mng_tel
    result["mng_id"] = support_business.support_business_author.id
    result["support_business_id"] = support_business.id
    try:
        result["is_favored"] = is_in_favor_list("support_business", support_business.id , user_auth_id)
    except:
        result["is_favored"] = False
    result["kikwan"] = support_business.support_business_author.mng_kikwan

    result["support_business_name_sub"] = support_business.support_business_name_sub

    result["support_business_subject"] = support_business.support_business_subject
    result["support_business_detail"] = support_business.support_business_detail
    result["support_business_poster"] = support_business.support_business_poster
    try:
        with open(support_business.support_business_poster, "rb") as image_file:
            encoded_string = base64.b64encode(image_file.read())
        result["support_business_poster_data_url"] = str(encoded_string)
    except Exception as e:
        print(e)
    result["support_business_status"] = support_business.support_business_status


    result["support_business_short_desc"] = support_business.support_business_short_desc
    result["support_business_name_tag"] = support_business.support_business_name_tag
    result["base_tag"] = []
    result["special_tag"] = []
    result["tag"] = []
    for t in support_business.selected_support_business_filter_list.all():
        result["tag"].append(t.filter_name)
        if t.cat_0 == "기본장르":
            result["base_tag"].append(t.filter_name)
        if t.cat_0 == "영역":
            result["special_tag"].append(t.filter_name)
    if support_business.support_business_employee_condition != None:
        result["tag"].append( str(support_business.support_business_employee_condition) +"명 이하")

    result["support_business_supply_content"] = support_business.support_business_supply_content
    result["support_business_apply_start_ymd"] = support_business.support_business_apply_start_ymd
    result["support_business_apply_end_ymdt"] = support_business.support_business_apply_end_ymdt
    result["support_business_object"] = support_business.support_business_object
    result["support_business_recruit_size"] = support_business.support_business_recruit_size
    result["support_business_prefer"] = support_business.support_business_prefer
    result["support_business_constraint"] = support_business.support_business_constraint
    result["support_business_prefer_chk"] = support_business.support_business_prefer_chk
    result["support_business_constraint_chk"] = support_business.support_business_constraint_chk
    result["support_business_pro_0_choose"] = support_business.support_business_pro_0_choose
    result["support_business_pro_0_start_ymd"] = support_business.support_business_pro_0_start_ymd
    result["support_business_pro_0_end_ymd"] = support_business.support_business_pro_0_end_ymd
    result["support_business_pro_0_open_ymd"] = support_business.support_business_pro_0_open_ymd
    result["support_business_pro_0_criterion"] = support_business.support_business_pro_0_criterion




    result["favorite"] = (support_business.additionaluserinfo_set.all()).count()
    result["comp"]=""
    if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
        try:
            number =  str(round((
                    Appliance.objects.filter(support_business_id=support_business.id).filter(is_submit=True)).count() / int(
                    support_business.support_business_recruit_size), 1))
            if(number =="0.0" ):
                number = "0"
            result["comp"] =  number + " : 1"
        except:
            result["comp"] = ""
    else:
        result["comp"] = ""

    result["support_business_etc_file_title_mng"] = support_business.support_business_etc_file_title_mng
    result["support_business_pro_1_choose"] = support_business.support_business_pro_1_choose
    result["support_business_pro_1_start_ymd"] = support_business.support_business_pro_1_start_ymd
    result["support_business_pro_1_end_ymd"] = support_business.support_business_pro_1_end_ymd
    result["support_business_pro_1_open_ymd"] = support_business.support_business_pro_1_open_ymd
    result["support_business_pro_1_criterion"] = support_business.support_business_pro_1_criterion
    result["support_business_pro_1_check"] = support_business.support_business_pro_1_check

    result["support_business_pro_2_choose"] = support_business.support_business_pro_2_choose
    result["support_business_pro_2_start_ymd"] = support_business.support_business_pro_2_start_ymd
    result["support_business_pro_2_end_ymd"] = support_business.support_business_pro_2_end_ymd
    result["support_business_pro_2_open_ymd"] = support_business.support_business_pro_2_open_ymd
    result["support_business_pro_2_criterion"] = support_business.support_business_pro_2_criterion
    result["support_business_pro_2_check"] = support_business.support_business_pro_2_check

    result["support_business_ceremony_start_ymd"] = support_business.support_business_ceremony_start_ymd
    result["support_business_ceremony_end_ymd"] = support_business.support_business_ceremony_end_ymd

    result["support_business_meta"] = support_business.support_business_meta
    result["support_business_faq"] = support_business.support_business_faq
    result["support_business_additional_faq"] = support_business.support_business_additional_faq
    result["support_business_meta"] = support_business.support_business_meta
    result["support_business_meta_0"] = support_business.support_business_meta_0
    result["mng_support_business_step_6_etc_input_chk"]  = support_business.mng_support_business_step_6_etc_input_chk
    result["support_business_ceremony_chk" ] = support_business.support_business_ceremony_chk
    result["support_business_faq_chk" ] = support_business.support_business_faq_chk
    result["support_business_additional_faq_chk" ] = support_business.support_business_additional_faq_chk
    result["support_business_meta"] = support_business.support_business_meta

    result["mng_support_business_step_3_etc_input_mojipjogun"] = support_business.mng_support_business_step_3_etc_input_mojipjogun
    result["mng_support_business_step_3_etc_input_mojipgenre"] = support_business.mng_support_business_step_3_etc_input_mojipgenre
    result["mng_support_business_step_3_etc_input_mojipjogun_chk"] = support_business.mng_support_business_step_3_etc_input_mojipjogun_chk
    result["mng_support_business_step_3_etc_input_mojipgenre_chk"] = support_business.mng_support_business_step_3_etc_input_mojipgenre_chk

    result["mng_support_business_step_6_etc_input"] = support_business.mng_support_business_step_6_etc_input
    result["support_business_etc_file_title_mng"] = support_business.support_business_etc_file_title_mng
    result["support_business_appliance_form"] = support_business.support_business_appliance_form

    result["object_tag"]=[]
    result["top_support_tag"]=[]
    result["files"]=[]
    for file in support_business.supportbusinessattachedfiles_set.all():
        result["files"].append({"name":file.file_path.split("/")[-1], "path": file.file_path, "id":file.id})

    try:

        if support_business.support_business_status == "4":  # 작성중인 공고문
            result["status"] = "모집종료"
        if support_business.support_business_status == "1":  # 작성중인 공고문
            result["status"] = "작성중"
        if support_business.support_business_status == "2":  # 승인대기중인 공고문
            result["status"] = "승인대기"
        if support_business.support_business_status == "3":
            result["status"] = "공고중"
        if support_business.support_business_apply_end_ymdt < timezone.now() and support_business.support_business_status == "3":  # 모집 종료 된 공고문
            result["status"] = "모집종료"
        if support_business.support_business_status == "5":  # 공고 종료 된 공고문
            result["status"] = "공고종료"
        if support_business.support_business_status == "6":  # 블라인드 공고문
            result["status"] = "블라인드"


    except:
        result["status"] = "작성중"


    result["selected_support_business_filter_list"] = []
    result["local_tag"] = []
    result["kind_tag"] = []
    result["year_tag"] = []
    result["step_tag"] = []
    result["genre_filter"]=[]
    result["conditions_location_filter"] = []
    result["area_creation_filter"] = []
    result["area_it_filter"] = []
    result["area_manufacture_filter"] = []
    result["area_founded_filter"] = [] 
    result["area_newbusiness_filter"] = []
    result["area_etc_filter"] = []
    result["conditions_comtype_filter"] = []
    result["conditions_record_filter"] = []
    result["conditions_stage_filter"] = []
    result["type_cash_filter"] = []
    result["type_invest_filter"] = []
    result["type_edu_filter"] = []
    result["type_market_filter"] = []
    result["type_network_filter"] = []
    result["type_etc_filter"] = []
    result["type_space_filter"] = []
    result["type_pitching_filter"] = []
    for t in support_business.selected_support_business_filter_list.all():
        result["selected_support_business_filter_list"].append(t.filter_name)
    for t in support_business.selected_support_business_filter_list.all():
        if t.cat_1 == "소재지":
            result["local_tag"].append(t.filter_name) 
        if t.cat_1 == "기업형태":
            result["kind_tag"].append(t.filter_name) 
        if t.cat_1 == "업력":
            result["year_tag"].append(t.filter_name)  
        if t.cat_1 == "기업단계":
            result["step_tag"].append(t.filter_name)  
        if t.cat_0 == "지원형태":
            result["top_support_tag"].append(t.filter_name)
        else:
            result["object_tag"].append(t.filter_name)  
    for t in  SupportBusinessFilter.objects.all():
        if t.cat_0 == "기본장르":
            result["genre_filter"].append(t.filter_name)
        if t.cat_1 == "소재지":
            result["conditions_location_filter"].append(t.filter_name)
        if t.cat_1 == "창작":
            result["area_creation_filter"].append(t.filter_name)
        if t.cat_1 == "IT 관련":
            result["area_it_filter"].append(t.filter_name)
        if t.cat_1 == "제조/융합 관련":
            result["area_manufacture_filter"].append(t.filter_name)
        if t.cat_1 == "창업":
            result["area_founded_filter"].append(t.filter_name)
        if t.cat_1 == "신규사업":
            result["area_newbusiness_filter"].append(t.filter_name)
        if t.cat_1 == "기타" and t.cat_0=="영역":
            result["area_etc_filter"].append(t.filter_name)
        if t.cat_1 == "기업형태":
            result["conditions_comtype_filter"].append(t.filter_name)
        if t.cat_1 == "업력":
            result["conditions_record_filter"].append(t.filter_name)
        if t.cat_1 == "기업단계":
            result["conditions_stage_filter"].append(t.filter_name)
        if t.cat_1 == "자금지원":
            result["type_cash_filter"].append(t.filter_name)
        if t.cat_1 == "엑셀러레이팅 투자연계":
            result["type_invest_filter"].append(t.filter_name)
        if t.cat_1 == "교육":
            result["type_edu_filter"].append(t.filter_name)
        if t.cat_1 == "판로":
            result["type_market_filter"].append(t.filter_name)
        if t.cat_1 == "네트워킹":
            result["type_network_filter"].append(t.filter_name)
        if t.cat_1 == "기타지원":
            result["type_etc_filter"].append(t.filter_name)
        if t.cat_1 == "공간지원":
            result["type_space_filter"].append(t.filter_name)
        if t.cat_1 == "피칭":
            result["type_pitching_filter"].append(t.filter_name)

    return JsonResponse(result, safe=False)
get_support_business_detail()

[Errno 2] No such file or directory: 'media/uploads/poster/112926_pl397[W680-].jpg'
{'sql': 'SELECT `supporting_business_supportbusiness`.`id`, `supporting_business_supportbusiness`.`support_business_author_id`, `supporting_business_supportbusiness`.`support_business_created_at_ymdt`, `supporting_business_supportbusiness`.`support_business_name`, `supporting_business_supportbusiness`.`support_business_name_tag`, `supporting_business_supportbusiness`.`support_business_name_sub`, `supporting_business_supportbusiness`.`support_business_poster`, `supporting_business_supportbusiness`.`support_business_relate_support_business_id`, `supporting_business_supportbusiness`.`support_business_short_desc`, `supporting_business_supportbusiness`.`support_business_subject`, `supporting_business_supportbusiness`.`support_business_detail`, `supporting_business_supportbusiness`.`support_business_apply_start_ymd`, `supporting_business_supportbusiness`.`support_business_apply_end_ymdt`, `supporting_business

<JsonResponse status_code=200, "application/json">

In [79]:
@my_timer
def vue_get_filter():
    result={}
    result["genre_filter"] = []
    result["conditions_location_filter"] = []
    result["area_creation_filter"] = []
    result["area_it_filter"] = []
    result["area_manufacture_filter"] = []
    result["area_founded_filter"] = []
    result["area_newbusiness_filter"] = []
    result["area_etc_filter"] = []
    result["conditions_comtype_filter"] = []
    result["conditions_record_filter"] = []
    result["conditions_stage_filter"] = []
    result["type_cash_filter"] = []
    result["type_invest_filter"] = []
    result["type_edu_filter"] = []
    result["type_market_filter"] = []
    result["type_network_filter"] = []
    result["type_etc_filter"] = []
    result["type_space_filter"] = []
    result["type_pitching_filter"] = []
    for t in SupportBusinessFilter.objects.all():
        if t.cat_0 == "기본장르":
            result["genre_filter"].append(t.filter_name)
        if t.cat_1 == "소재지":
            result["conditions_location_filter"].append(t.filter_name)
        if t.cat_1 == "창작":
            result["area_creation_filter"].append(t.filter_name)
        if t.cat_1 == "IT 관련":
            result["area_it_filter"].append(t.filter_name)
        if t.cat_1 == "제조/융합 관련":
            result["area_manufacture_filter"].append(t.filter_name)
        if t.cat_1 == "창업":
            result["area_founded_filter"].append(t.filter_name)
        if t.cat_1 == "신규사업":
            result["area_newbusiness_filter"].append(t.filter_name)
        if t.cat_1 == "기타" and t.cat_0 == "영역":
            result["area_etc_filter"].append(t.filter_name)
        if t.cat_1 == "기업형태":
            result["conditions_comtype_filter"].append(t.filter_name)
        if t.cat_1 == "업력":
            result["conditions_record_filter"].append(t.filter_name)
        if t.cat_1 == "기업단계":
            result["conditions_stage_filter"].append(t.filter_name)
        if t.cat_1 == "자금지원":
            result["type_cash_filter"].append(t.filter_name)
        if t.cat_1 == "엑셀러레이팅 투자연계":
            result["type_invest_filter"].append(t.filter_name)
        if t.cat_1 == "교육":
            result["type_edu_filter"].append(t.filter_name)
        if t.cat_1 == "판로":
            result["type_market_filter"].append(t.filter_name)
        if t.cat_1 == "네트워킹":
            result["type_network_filter"].append(t.filter_name)
        if t.cat_1 == "기타지원":
            result["type_etc_filter"].append(t.filter_name)
        if t.cat_1 == "공간지원":
            result["type_space_filter"].append(t.filter_name)
        if t.cat_1 == "피칭":
            result["type_pitching_filter"].append(t.filter_name)
    return JsonResponse(result, safe=False)
vue_get_filter()

{'sql': 'SELECT `supporting_business_supportbusinessfilter`.`id`, `supporting_business_supportbusinessfilter`.`cat_0`, `supporting_business_supportbusinessfilter`.`cat_1`, `supporting_business_supportbusinessfilter`.`filter_name` FROM `supporting_business_supportbusinessfilter`', 'time': '0.005'}
vue_get_filter
총 쿼리수: 1
실행된 총 시간: 0.005021333694458008 초
db 쿼리 시간 :  0.005 초
쿼리 제외한 연산 시간 :  2.133369445800771e-05 초


<JsonResponse status_code=200, "application/json">

In [76]:
@my_timer
def similar_support_business():
    result={}
    result["data"]=[]
    origin_support_business = SupportBusiness.objects.get(id=1)
    origin_support_business_filter_list = set(list(origin_support_business.selected_support_business_filter_list.values_list("filter_name",flat=True)))
    for support_business in SupportBusiness.objects.filter(support_business_status=3)\
    .filter(support_business_apply_end_ymdt__gte=datetime.now()).exclude(id=1)\
    .prefetch_related("additionaluserinfo_set").prefetch_related("selected_support_business_filter_list")\
    .prefetch_related("appliance_set"):
        obj = {}
        obj["tag"] = []
        obj["support_business_name"] = support_business.support_business_name
        obj["support_business_apply_end_ymdt"] = (support_business.support_business_apply_end_ymdt)
        obj["support_business_apply_start_ymd"] = (support_business.support_business_apply_start_ymd)
        obj["support_business_short_desc"] = support_business.support_business_short_desc
        obj["support_business_poster"] = support_business.support_business_poster
        obj["comp"]=""
        if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
            number =  str(round(support_business.appliance_set.filter(is_submit=True).count() / int(
                support_business.support_business_recruit_size), 1))
            if number =="0.0":
                number ="0"
            obj["comp"] = number + " : 1"

        else:
            obj["comp"] = ""

        obj["favorite"] = str(support_business.additionaluserinfo_set.count())
        try:
            obj["is_favored"] = is_in_favor_list("support_business", support_business.id, request.GET.get("gca_id"))
        except:
            obj["is_favored"] = False
        obj["id"] = support_business.id
        obj["sim"]=0
        obj["selected_support_business_filter_list"]=[]
        for f in support_business.selected_support_business_filter_list.all():
            obj["selected_support_business_filter_list"].append(f.filter_name)
        
        obj["sim"]= len(set(obj["selected_support_business_filter_list"] ) & origin_support_business_filter_list)
        print(obj["sim"])
        # if random.randrange(0,10)%2==0:
        #     obj["img"] = img_list[random.randrange(0,9)]
        result["data"].append(copy.deepcopy(obj))
        sorted(result["data"], key=lambda c:c["sim"])
    return JsonResponse(result)
similar_support_business()

7
7
7
5
5
{'sql': 'SELECT `supporting_business_supportbusiness`.`id`, `supporting_business_supportbusiness`.`support_business_author_id`, `supporting_business_supportbusiness`.`support_business_created_at_ymdt`, `supporting_business_supportbusiness`.`support_business_name`, `supporting_business_supportbusiness`.`support_business_name_tag`, `supporting_business_supportbusiness`.`support_business_name_sub`, `supporting_business_supportbusiness`.`support_business_poster`, `supporting_business_supportbusiness`.`support_business_relate_support_business_id`, `supporting_business_supportbusiness`.`support_business_short_desc`, `supporting_business_supportbusiness`.`support_business_subject`, `supporting_business_supportbusiness`.`support_business_detail`, `supporting_business_supportbusiness`.`support_business_apply_start_ymd`, `supporting_business_supportbusiness`.`support_business_apply_end_ymdt`, `supporting_business_supportbusiness`.`support_business_object`, `supporting_business_supportb

<JsonResponse status_code=200, "application/json">

In [70]:
@my_timer
def similar_support_business():
    result={}
    result["data"]=[]
    origin_support_business = SupportBusiness.objects.get(id=1)
    for support_business in SupportBusiness.objects.filter(support_business_status=3).filter(support_business_apply_end_ymdt__gte=datetime.now()).exclude(id=1):
        obj = {}
        obj["tag"] = []
        obj["support_business_name"] = support_business.support_business_name
        obj["support_business_apply_end_ymdt"] = (support_business.support_business_apply_end_ymdt)
        obj["support_business_apply_start_ymd"] = (support_business.support_business_apply_start_ymd)
        obj["support_business_short_desc"] = support_business.support_business_short_desc
        obj["support_business_poster"] = support_business.support_business_poster
        obj["comp"]=""
        if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
            number =  str(round((
                Appliance.objects.filter(support_business_id=support_business.id).filter(is_submit=True)).count() / int(
                support_business.support_business_recruit_size), 1))
            if number =="0.0":
                number ="0"
            obj["comp"] = number + " : 1"

        else:
            obj["comp"] = ""

        obj["favorite"] = str((AdditionalUserInfo.objects.filter(favorite=support_business)).count())
        try:
            obj["is_favored"] = is_in_favor_list("support_business", support_business.id, request.GET.get("gca_id"))
        except:
            obj["is_favored"] = False
        obj["id"] = support_business.id
        obj["sim"]=0
        obj["selected_support_business_filter_list"]=[]
        for f in support_business.selected_support_business_filter_list.all():
            obj["selected_support_business_filter_list"].append(f.filter_name)
            if f in origin_support_business.selected_support_business_filter_list.all():
                obj["sim"]= obj["sim"]+1

        # if random.randrange(0,10)%2==0:
        #     obj["img"] = img_list[random.randrange(0,9)]
        result["data"].append(copy.deepcopy(obj))
        sorted(result["data"], key=lambda c:c["sim"])
    return JsonResponse(result)
similar_support_business()

{'sql': 'SELECT `supporting_business_supportbusiness`.`id`, `supporting_business_supportbusiness`.`support_business_author_id`, `supporting_business_supportbusiness`.`support_business_created_at_ymdt`, `supporting_business_supportbusiness`.`support_business_name`, `supporting_business_supportbusiness`.`support_business_name_tag`, `supporting_business_supportbusiness`.`support_business_name_sub`, `supporting_business_supportbusiness`.`support_business_poster`, `supporting_business_supportbusiness`.`support_business_relate_support_business_id`, `supporting_business_supportbusiness`.`support_business_short_desc`, `supporting_business_supportbusiness`.`support_business_subject`, `supporting_business_supportbusiness`.`support_business_detail`, `supporting_business_supportbusiness`.`support_business_apply_start_ymd`, `supporting_business_supportbusiness`.`support_business_apply_end_ymdt`, `supporting_business_supportbusiness`.`support_business_object`, `supporting_business_supportbusiness`.`

<JsonResponse status_code=200, "application/json">

In [16]:
@my_timer
def startup_list():

    filter_list = ["출판","일러스트","스타트업","VR","3년 이내","15명 이하"]
    result = Startup.objects.all().exclude(company_name="").exclude(company_name=None)
    for filter in filter_list:
        if filter == "구성원 제한없음":
            pass
        elif "명 이하" in filter or "명 이상" in filter:
            # x 명이 있는 경우에는 구성원을 입력하지 않은 스타트업을 추가해주어야함
            num = int(re.findall('\d+', filter)[0])
            if (num != 0):
                result = copy.deepcopy(result.filter(company_total_employee__lte=num).exclude(company_name="").exclude(
                    company_name=None)) | Startup.objects.all().filter(company_total_employee=None)
        elif filter != None and filter != "":
            result = copy.deepcopy(result.filter(selected_company_filter_list__filter_name=filter))

    result_set = []
    for s in result:
        temp_obj = {}
        temp_obj["company_name"] = s.company_name
        temp_obj["logo"] = s.logo
        temp_obj["company_short_desc"] = s.company_short_desc
        try:
            temp_obj["is_favored"] = is_in_favor_list("startup", s.id, user_auth_id)
        except:
            temp_obj["is_favored"] = False
        temp_obj["filter"] = []
        temp_obj["id"] = s.id
        for t in s.selected_company_filter_list.all():
            if t.filter_name != "" and t.filter_name != None and t.cat_0!="지원형태" and t.cat_1!="기업형태":
                temp_obj["filter"].append(t.filter_name)
        result_set.append(copy.deepcopy(temp_obj))
    return  JsonResponse(list(result_set), safe=False)
startup_list()

{'sql': "SELECT `supporting_business_startup`.`id`, `supporting_business_startup`.`user_id`, `supporting_business_startup`.`company_name`, `supporting_business_startup`.`established_date`, `supporting_business_startup`.`logo`, `supporting_business_startup`.`back_img`, `supporting_business_startup`.`company_short_desc`, `supporting_business_startup`.`company_intro`, `supporting_business_startup`.`company_youtube`, `supporting_business_startup`.`company_facebook`, `supporting_business_startup`.`company_instagram`, `supporting_business_startup`.`company_website`, `supporting_business_startup`.`address_0`, `supporting_business_startup`.`address_1`, `supporting_business_startup`.`repre_name`, `supporting_business_startup`.`repre_email`, `supporting_business_startup`.`repre_tel`, `supporting_business_startup`.`mark_name`, `supporting_business_startup`.`mark_email`, `supporting_business_startup`.`mark_tel`, `supporting_business_startup`.`company_keyword`, `supporting_business_startup`.`compan

<JsonResponse status_code=200, "application/json">

In [17]:
@my_timer
def vue_get_clip():  
    result={}
    clip= Clip.objects.get(id=96)
    result["ip"]=  urllib.request.urlopen('https://api.ipify.org/').read().decode()
    if False:
        print(AdditionalUserInfo.objects.get(id= 74).favorite_clip.all())
        if clip in AdditionalUserInfo.objects.get(id= 74).favorite_clip.all() :
            result["is_favored"] = "true"
        else:
            result["is_favored"] = "false"
    result["clip_title"] = clip.clip_title
    result["clip_youtube"] = clip.clip_youtube
    result["clip_user_id"]= clip.clip_user.id
    result["clip_mov_url"] = clip.clip_mov_url
    try:
        result["is_favored"] = is_in_favor_list( "clip" , clip.id , user_auth_id)
    except:
        result["is_favored"] =False
    result["clip_id"] = clip
    result["clip_object"] = clip.clip_object
    result["clip_info"] = clip.clip_info
    result["clip_play"] = clip.clip_play
    try:
        result["clip_user"] = clip.clip_user.user.startup.mark_name
    except:
        result["clip_user"] = clip.clip_user.mng_name
    result["clip_created_at"] = clip.clip_created_at
    result["clip_thumb"] = clip.clip_thumb
    result["clip_id"] = clip.id
    result["int"] = (clip.additionaluserinfo_set.all()).count()
    result["tag"]=[]
    for  t in clip.clip_filter.all():
        result["tag"].append(t.name)
    result["another_clip"]=[]
    for c in Clip.objects.all().order_by("?")[:4]:
        temp={}
        temp["id"] = c.id
        temp["clip_play"] = c.clip_play
        temp["clip_title"] = c.clip_title
        temp["clip_thumb"] = c.clip_thumb
        print(clip.clip_user)
        try:
            temp["clip_user"] = c.clip_user.user.startup.mark_name
            print(temp["clip_user"])
        except Exception as e:
            print(e)
            temp["clip_user"] = c.clip_user.mng_name
        temp["clip_created_at"] = c.clip_created_at
        temp["clip_youtube"] = c.clip_youtube
        result["another_clip"].append(copy.deepcopy(temp))
    result["another_course"] = []
    for c in Course.objects.all().order_by("?"):
        temp = {}
        temp["id"] = c.id
        temp["course_title"] = c.course_title
        temp["course_total_play"] = c.course_total_play
        temp["course_thumb"] = c.course_thumb
        try:
            temp["course_user"] = c.course_user.user.startup.mark_name
        except:
            temp["course_user"] = c.course_user.mng_name
        temp["course_created_at"] = c.course_created_at
        try:
            temp["entry_point"] = "course/view/"+str(c.id) + "/"+ str(c.course_clips.all().first().id)
        except Exception as e:
            pass
        temp["clip_youtube"] = clip.clip_youtube
        result["another_course"].append(copy.deepcopy(temp))
    return JsonResponse(result)
vue_get_clip()

noknok@startup.com
샘플기업
noknok@startup.com

noknok@startup.com

noknok@startup.com
샘플기업
{'sql': 'SELECT `supporting_business_clip`.`id`, `supporting_business_clip`.`clip_user_id`, `supporting_business_clip`.`clip_title`, `supporting_business_clip`.`clip_youtube`, `supporting_business_clip`.`clip_mov_url`, `supporting_business_clip`.`clip_thumb`, `supporting_business_clip`.`clip_object`, `supporting_business_clip`.`clip_info`, `supporting_business_clip`.`clip_play`, `supporting_business_clip`.`clip_created_at` FROM `supporting_business_clip` WHERE `supporting_business_clip`.`id` = 96', 'time': '0.012'}
{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `suppo

<JsonResponse status_code=200, "application/json">

In [91]:
@my_timer
def vue_get_clip():  
    result={}
    clip= Clip.objects.get(id=96)        
    if False:
        print(AdditionalUserInfo.objects.get(id= 74).favorite_clip.all())
        if clip in AdditionalUserInfo.objects.get(id= 74).favorite_clip.all() :
            result["is_favored"] = "true"
        else:
            result["is_favored"] = "false"
    result["clip_title"] = clip.clip_title
    result["clip_youtube"] = clip.clip_youtube
    result["clip_user_id"]= clip.clip_user.id
    result["clip_mov_url"] = clip.clip_mov_url   
    try:
        result["is_favored"] = is_in_favor_list( "clip" , clip.id , user_auth_id)
    except:
        result["is_favored"] =False
    result["clip_id"] = clip
    result["clip_object"] = clip.clip_object
    result["clip_info"] = clip.clip_info
    result["clip_play"] = clip.clip_play
    try:
        result["clip_user"] = clip.clip_user.user.startup.mark_name
    except:
        result["clip_user"] = clip.clip_user.mng_name
    result["clip_created_at"] = clip.clip_created_at
    result["clip_thumb"] = clip.clip_thumb
    result["clip_id"] = clip.id
    result["int"] = (clip.additionaluserinfo_set.all()).count()
    result["tag"]=[]
 
    for  t in clip.clip_filter.all():
        result["tag"].append(t.name)
   
    result["another_clip"]=[]
    for c in Clip.objects.order_by("?")[:4].prefetch_related("clip_user").prefetch_related("clip_user__own_startup"):      
        temp={}
        temp["id"] = c.id
        temp["clip_play"] = c.clip_play
        temp["clip_title"] = c.clip_title
        temp["clip_thumb"] = c.clip_thumb      
        try:
            temp["clip_user"] = c.clip_user.own_startup.mark_name
            print(temp["clip_user"])
        except Exception as e:
            print(e)
            temp["clip_user"] = c.clip_user.mng_name
        temp["clip_created_at"] = c.clip_created_at
        temp["clip_youtube"] = c.clip_youtube
        result["another_clip"].append(copy.deepcopy(temp))
    result["another_course"] = []
    for c in Course.objects.prefetch_related("course_user").prefetch_related("course_user__own_startup").order_by("?"):
        temp = {}
        temp["id"] = c.id
        temp["course_title"] = c.course_title
        temp["course_total_play"] = c.course_total_play
        temp["course_thumb"] = c.course_thumb
        try:
            temp["course_user"] = c.course_user.own_startup.mark_name
        except:
            temp["course_user"] = c.course_user.mng_name
        temp["course_created_at"] = c.course_created_at
   
        temp["clip_youtube"] = clip.clip_youtube
        result["another_course"].append(copy.deepcopy(temp))

    return JsonResponse(result)
vue_get_clip()

킴킴zla1
남기룡
담당자-수정 테스트-수정2
샘플기업
{'sql': 'SELECT `supporting_business_clip`.`id`, `supporting_business_clip`.`clip_user_id`, `supporting_business_clip`.`clip_title`, `supporting_business_clip`.`clip_youtube`, `supporting_business_clip`.`clip_mov_url`, `supporting_business_clip`.`clip_thumb`, `supporting_business_clip`.`clip_object`, `supporting_business_clip`.`clip_info`, `supporting_business_clip`.`clip_play`, `supporting_business_clip`.`clip_created_at` FROM `supporting_business_clip` WHERE `supporting_business_clip`.`id` = 96', 'time': '0.016'}
{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `support

<JsonResponse status_code=200, "application/json">

In [81]:
@my_timer
def vue_get_course_information():

    result={}
    course = Course.objects.get(id=100)
    result["course_object"] = course.course_object
    result["course_info"] = course.course_info
    result["is_favored"] = ""
    result["course_author_id"] = course.course_user.id
    result["course_title"] = course.course_title
    result["course_rec_dur"] = course.course_rec_dur
    result["course_total_play"] = course.course_total_play
    result["course_created_at"] = course.course_created_at
    result["course_thumb"] = course.course_thumb
    result["course_id"] = course.id

    try:
        result["course_author"] = course.course_user.own_startup.mark_name

    except:
        result["course_author"] = course.course_user.mng_name
    result["course_filter"]=[]
    for filter in course.course_filter.all():
        print(filter)
        result["course_filter"].append(filter.name)

    result["course_clip"]=[]
    for clip in course.course_clips.select_related("clip_user__own_startup"):
        obj = {}
        obj["clip_title"] = clip.clip_title
        obj["clip_created_at"] = clip.clip_created_at
        try:
            obj["clip_author"] = clip.clip_user.own_startup.mark_name
        except:
            obj["clip_author"] = clip.clip_user.mng_name
        obj["clip_thumb"] = clip.clip_thumb
        obj["clip_play"] = clip.clip_play
        obj["clip_id"] = clip.id
        result["course_clip"].append(copy.deepcopy(obj))


    return JsonResponse(result, safe=False)
vue_get_course_information()

EduFilter object
EduFilter object
{'sql': 'SELECT `supporting_business_course`.`id`, `supporting_business_course`.`course_user_id`, `supporting_business_course`.`course_title`, `supporting_business_course`.`course_thumb`, `supporting_business_course`.`course_rec_dur`, `supporting_business_course`.`course_object`, `supporting_business_course`.`course_info`, `supporting_business_course`.`course_total_play`, `supporting_business_course`.`course_created_at` FROM `supporting_business_course` WHERE `supporting_business_course`.`id` = 100', 'time': '0.018'}
{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `su

<JsonResponse status_code=200, "application/json">

In [20]:
@my_timer
def vue_get_clip_all():
    result = []
    for c in Clip.objects.all().order_by("-id"):
        temp={}
        temp["clip_id"] = c.id
        try:
            temp["clip_user"]=c.clip_user.user.startup.mark_name
        except:
            temp["clip_user"] = c.clip_user.mng_name
        temp["clip_thumb"]=c.clip_thumb
        temp["clip_title"]=c.clip_title
        temp["clip_play"]=c.clip_play
        temp["clip_created_at"]=c.clip_created_at
        temp["clip_info"] = c.clip_info
        temp["clip_tag"] =[]
        try:
            temp["is_favored"] = is_in_favor_list( "clip", c.id  , user_auth_id )
        except:
            temp["is_favored"] = False
        temp["clip_entry_point"] ="/channel/clip/view/"+str(c.id)
        # 채널 통계에서 사용되는 레이블과 value
        temp["label"] = c.clip_title
        temp["value"] = c.id

        temp["tag"]=[]
        for t in c.clip_filter.all()  :
            temp["tag"].append(t.name)
        result.append(copy.deepcopy(temp))
    return JsonResponse(result, safe=False)
vue_get_clip_all()

{'sql': 'SELECT `supporting_business_clip`.`id`, `supporting_business_clip`.`clip_user_id`, `supporting_business_clip`.`clip_title`, `supporting_business_clip`.`clip_youtube`, `supporting_business_clip`.`clip_mov_url`, `supporting_business_clip`.`clip_thumb`, `supporting_business_clip`.`clip_object`, `supporting_business_clip`.`clip_info`, `supporting_business_clip`.`clip_play`, `supporting_business_clip`.`clip_created_at` FROM `supporting_business_clip` ORDER BY `supporting_business_clip`.`id` DESC', 'time': '0.016'}
{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluseri

<JsonResponse status_code=200, "application/json">

In [21]:
@my_timer
def vue_get_clip_all():
    result = []
    for c in Clip.objects.select_related("clip_user__own_startup").prefetch_related("clip_filter").order_by("-id"):
        temp={}
        temp["clip_id"] = c.id
        try:
            temp["clip_user"]=c.clip_user.own_startup.mark_name
        except:
            temp["clip_user"] = c.clip_user.mng_name
        temp["clip_thumb"]=c.clip_thumb
        temp["clip_title"]=c.clip_title
        temp["clip_play"]=c.clip_play
        temp["clip_created_at"]=c.clip_created_at
        temp["clip_info"] = c.clip_info
        temp["clip_tag"] =[]
        try:
            temp["is_favored"] = is_in_favor_list( "clip", c.id  , user_auth_id )
        except:
            temp["is_favored"] = False
        temp["clip_entry_point"] ="/channel/clip/view/"+str(c.id)
        # 채널 통계에서 사용되는 레이블과 value
        temp["label"] = c.clip_title
        temp["value"] = c.id

        temp["tag"]=[]
        for t in c.clip_filter.all()  :
            temp["tag"].append(t.name)
        result.append(copy.deepcopy(temp))
    return JsonResponse(result, safe=False)
vue_get_clip_all()

{'sql': 'SELECT `supporting_business_clip`.`id`, `supporting_business_clip`.`clip_user_id`, `supporting_business_clip`.`clip_title`, `supporting_business_clip`.`clip_youtube`, `supporting_business_clip`.`clip_mov_url`, `supporting_business_clip`.`clip_thumb`, `supporting_business_clip`.`clip_object`, `supporting_business_clip`.`clip_info`, `supporting_business_clip`.`clip_play`, `supporting_business_clip`.`clip_created_at`, `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinf

<JsonResponse status_code=200, "application/json">

In [22]:
@my_timer
def get_home_info():

    gr = SupportBusiness.objects.filter(support_business_status=3).filter(support_business_apply_end_ymdt__gte=timezone.now()).order_by("-support_business_update_at_ymdt")[:6] #.filter(  Q(support_business_status=3)|Q(support_business_status=4)|Q(support_business_status=5)).filter(support_business_apply_start_ymd__lte=datetime.now()).order_by("?")[:6]
    result={}
    result["support_business_set"] = []
    for g in gr:
        team={}
        team["support_business_name"] = g.support_business_name
        team["support_business_apply_end_ymdt"] = g.support_business_apply_end_ymdt
        team["support_business_short_desc"] = g.support_business_short_desc
        team["selected_support_business_filter_list"]=[]
        for f in g.selected_support_business_filter_list.all():
            team["selected_support_business_filter_list"].append(f.filter_name)
        team["support_business_poster"]= g.support_business_poster
        try:
            team["is_favored"] = is_in_favor_list("support_business",g.id, user_auth_id)
        except Exception as e :
            print(e)
            team["is_favored"] = ""
        team["id"] = g.id
        result["support_business_set"].append(copy.deepcopy(team))
    result["startup_set"] = []
    startup = Startup.objects.exclude(company_name="").exclude(company_name=None).order_by("?")[:3]
    for s in startup:
        temp_obj = {}
        temp_obj["company_name"] = s.company_name
        temp_obj["company_short_desc"] = s.company_short_desc
        temp_obj["logo"] = s.logo
        try:
            temp_obj["is_favored"] = is_in_favor_list("startup", s.id, user_auth_id)
        except:
            temp_obj["is_favored"] = False
        temp_obj["tag"] = []
        temp_obj["id"] = s.id
        temp_obj["filter"] = []
        temp_obj["filter"] = []
        for t in s.selected_company_filter_list.all():
            if t.cat_0 != "지원형태" and t.cat_1 != "기업형태":
                temp_obj["filter"].append(t.filter_name)
        result["startup_set"].append(copy.deepcopy(temp_obj))
    result["clip"] = []
    for c in Clip.objects.all().order_by("-id")[:3]:
        temp={}
        temp["clip_id"] = c.id
        try:
            temp["clip_user"]=c.clip_user.user.startup.mark_name
        except:
            temp["clip_user"] = c.clip_user.mng_name
        temp["clip_thumb"]=c.clip_thumb
        temp["clip_title"]=c.clip_title
        temp["clip_play"]=c.clip_play
        temp["clip_created_at"]=c.clip_created_at
        temp["clip_info"] = c.clip_info
        temp["clip_tag"] =[]
        try:
            temp["is_favored"] = is_in_favor_list( "clip", c.id  , user_auth_id )
        except:
            temp["is_favored"] = False
        temp["clip_entry_point"] ="/channel/clip/view/"+str(c.id)
        # 채널 통계에서 사용되는 레이블과 value
        temp["label"] = c.clip_title
        temp["value"] = c.id
        temp["tag"]=[]
        for t in c.clip_filter.all()  :
            temp["tag"].append(t.name)
        result["clip"].append(copy.deepcopy(temp))
    result["course"]=[]
    for c in Course.objects.all().order_by("-id")[:3]:
        temp = {}
        temp["id"] = c.id
        try:
            print(0)
            temp["course_entry_point"] = "/channel/course/view/" + str(c.id) + "/" + str(
                c.course_clips.all().first().id)
        except Exception as e:
            print(e)
            print(c.course_clips.all())
            print(c.course_clips.all().first())
            temp["course_entry_point"] = ""
        try:
            temp["course_user"] = c.course_user.user.startup.mark_name
        except:
            temp["course_user"] = c.course_user.mng_name
        temp["course_thumb"] = c.course_thumb
        temp["course_id"] = c.id
        temp["label"] = c.course_title
        temp["value"] = c.id
        try:
            temp["is_favored"] = is_in_favor_list("course", c.id, user_auth_id)
        except:
            temp["is_favored"] = False
        temp["course_title"] = c.course_title
        temp["course_rec_dur"] = c.course_rec_dur
        temp["course_created_at"] = c.course_created_at
        temp["course_info"] = c.course_info
        temp["course_tag"] = []
        temp["course_total_play"] = c.course_total_play
        for t in c.course_filter.all():
            temp["course_tag"].append(t.name)
        result["course"].append(copy.deepcopy(temp))
    result["path"] = []
    for c in Path.objects.all().order_by("-id"):
        temp = {}
        temp["id"] = c.id
        try:
            temp["path_entry_point"] = "/channel/path/view/" + str(c.id) + "/" + str(
                c.path_course.all().first().id) + "/" + str(c.path_course.first().course_clips.all().first().id)
        except Exception as e:
            print(e)
            temp["path_entry_point"] = ""
        try:
            temp["path_user"] = c.path_user.user.startup.mark_name
        except:
            temp["path_user"] = c.path_user.mng_name
        temp["path_thumb"] = c.path_thumb
        temp["path_title"] = c.path_title
        temp["path_rec_dur"] = c.path_rec_dur
        temp["label"] = c.path_title
        temp["value"] = c.id
        try:
            temp["is_favored"] = is_in_favor_list("path", c.id, user_auth_id)
        except:
            temp["is_favored"] = False
        temp["path_total_play"] = c.path_total_play
        temp["path_id"] = c.id
        temp["path_created_at"] = c.path_created_at
        temp["path_info"] = c.path_info
        temp["path_tag"] = []
        for t in c.path_filter.all():
            temp["path_tag"].append(t.name)
        result["path"].append(copy.deepcopy(temp))



    return JsonResponse(result)
get_home_info()

name 'is_in_favor_list' is not defined
name 'is_in_favor_list' is not defined
name 'is_in_favor_list' is not defined
name 'is_in_favor_list' is not defined
name 'is_in_favor_list' is not defined
0
'NoneType' object has no attribute 'id'
<QuerySet []>
None
0
'NoneType' object has no attribute 'id'
<QuerySet []>
None
0
'NoneType' object has no attribute 'id'
<QuerySet []>
None
'NoneType' object has no attribute 'id'
'NoneType' object has no attribute 'id'
'NoneType' object has no attribute 'id'
'NoneType' object has no attribute 'id'
'NoneType' object has no attribute 'id'
'NoneType' object has no attribute 'id'
'NoneType' object has no attribute 'id'
'NoneType' object has no attribute 'id'
'NoneType' object has no attribute 'id'
'NoneType' object has no attribute 'id'
'NoneType' object has no attribute 'id'
'NoneType' object has no attribute 'id'
'NoneType' object has no attribute 'id'
'NoneType' object has no attribute 'id'
'NoneType' object has no attribute 'id'
{'sql': "SELECT `suppo

<JsonResponse status_code=200, "application/json">

In [23]:
@my_timer
def similar_filter_support_business():
    filter_string_list = ["출판","일러스트","스타트업","VR","3년 이내","15명 이하"]
    filter_list = []
    result={}
    result["data"]=[]
    for f in filter_string_list:
        try:
            filter_list.append(SupportBusinessFilter.objects.get(filter_name=f))
        except:
            pass
    support_business_list = SupportBusiness.objects.filter(selected_support_business_filter_list__in=filter_list)\
        .exclude(support_business_status__in=[1,2,4,5,6,"1","2","4","5","6"]).filter(support_business_apply_end_ymdt__gte= timezone.now()).values("id").order_by("support_business_apply_end_ymdt")
    sb_list=[]

    for su in support_business_list:
        supportbusiness = SupportBusiness.objects.get(id=su["id"])
        if supportbusiness not in sb_list:
            sb_list.append(supportbusiness)

    for support_business in sb_list:
        obj = {}
        obj["tag"] = []
        obj["support_business_name"] = support_business.support_business_name
        obj["support_business_apply_end_ymdt"] = (support_business.support_business_apply_end_ymdt)
        obj["support_business_apply_start_ymd"] = (support_business.support_business_apply_start_ymd)
        obj["support_business_short_desc"] = support_business.support_business_short_desc
        obj["support_business_poster"] = support_business.support_business_poster
        try:
            obj["is_favored"] = is_in_favor_list("support_business", support_business.id, user_auth_id)
        except:
            obj["is_favored"] = False
        obj["id"] = support_business.id
        obj["sim"] = 0
        obj["selected_support_business_filter_list"] = []
        for f in support_business.selected_support_business_filter_list.all():
            obj["selected_support_business_filter_list"].append(f.filter_name)
            if f in filter_list:
                obj["sim"] = obj["sim"] + 1
        result["data"].append(copy.deepcopy(obj))
    return JsonResponse({"result":(result)},safe=False)
similar_filter_support_business()

{'sql': "SELECT `supporting_business_supportbusinessfilter`.`id`, `supporting_business_supportbusinessfilter`.`cat_0`, `supporting_business_supportbusinessfilter`.`cat_1`, `supporting_business_supportbusinessfilter`.`filter_name` FROM `supporting_business_supportbusinessfilter` WHERE `supporting_business_supportbusinessfilter`.`filter_name` = '출판'", 'time': '0.000'}
{'sql': "SELECT `supporting_business_supportbusinessfilter`.`id`, `supporting_business_supportbusinessfilter`.`cat_0`, `supporting_business_supportbusinessfilter`.`cat_1`, `supporting_business_supportbusinessfilter`.`filter_name` FROM `supporting_business_supportbusinessfilter` WHERE `supporting_business_supportbusinessfilter`.`filter_name` = '일러스트'", 'time': '0.016'}
{'sql': "SELECT `supporting_business_supportbusinessfilter`.`id`, `supporting_business_supportbusinessfilter`.`cat_0`, `supporting_business_supportbusinessfilter`.`cat_1`, `supporting_business_supportbusinessfilter`.`filter_name` FROM `supporting_business_supp

<JsonResponse status_code=200, "application/json">

In [67]:
@my_timer
def similar_filter_support_business():
    filter_string_list = ["출판","일러스트","스타트업","VR","3년 이내","15명 이하"]
    filter_list = []
    result={}
    result["data"]=[]
    for f in filter_string_list:
        try:
            filter_list.append(SupportBusinessFilter.objects.get(filter_name=f))
        except:
            pass
    support_business_list = SupportBusiness.objects.filter(selected_support_business_filter_list__in=filter_list)\
        .exclude(support_business_status__in=[1,2,4,5,6,"1","2","4","5","6"])\
        .filter(support_business_apply_end_ymdt__gte= timezone.now())\
        .prefetch_related("selected_support_business_filter_list")\
        .order_by("support_business_apply_end_ymdt")

    for support_business in support_business_list:
        obj = {}
        obj["tag"] = []
        obj["support_business_name"] = support_business.support_business_name
        obj["support_business_apply_end_ymdt"] = (support_business.support_business_apply_end_ymdt)
        obj["support_business_apply_start_ymd"] = (support_business.support_business_apply_start_ymd)
        obj["support_business_short_desc"] = support_business.support_business_short_desc
        obj["support_business_poster"] = support_business.support_business_poster
        try:
            obj["is_favored"] = is_in_favor_list("support_business", support_business.id, user_auth_id)
        except:
            obj["is_favored"] = False
        obj["id"] = support_business.id
        obj["sim"] = 0
        obj["selected_support_business_filter_list"] = []
        for f in support_business.selected_support_business_filter_list.all():
            obj["selected_support_business_filter_list"].append(f.filter_name)
            if f in filter_list:
                obj["sim"] = obj["sim"] + 1
        result["data"].append(copy.deepcopy(obj))
    return JsonResponse({"result":(result)},safe=False)
similar_filter_support_business()

{'sql': "SELECT `supporting_business_supportbusinessfilter`.`id`, `supporting_business_supportbusinessfilter`.`cat_0`, `supporting_business_supportbusinessfilter`.`cat_1`, `supporting_business_supportbusinessfilter`.`filter_name` FROM `supporting_business_supportbusinessfilter` WHERE `supporting_business_supportbusinessfilter`.`filter_name` = '출판'", 'time': '0.016'}
{'sql': "SELECT `supporting_business_supportbusinessfilter`.`id`, `supporting_business_supportbusinessfilter`.`cat_0`, `supporting_business_supportbusinessfilter`.`cat_1`, `supporting_business_supportbusinessfilter`.`filter_name` FROM `supporting_business_supportbusinessfilter` WHERE `supporting_business_supportbusinessfilter`.`filter_name` = '일러스트'", 'time': '0.017'}
{'sql': "SELECT `supporting_business_supportbusinessfilter`.`id`, `supporting_business_supportbusinessfilter`.`cat_0`, `supporting_business_supportbusinessfilter`.`cat_1`, `supporting_business_supportbusinessfilter`.`filter_name` FROM `supporting_business_supp

<JsonResponse status_code=200, "application/json">

In [24]:
@my_timer
def vue_home_support_business_new():

    tag_list = ["출판","일러스트","스타트업","VR","3년 이내","15명 이하"]
    result={}
    result["data"]=[]
    data=[]
    support_business_set = SupportBusiness.objects.filter(support_business_status=3)#.filter(support_business_apply_end_ymdt__gte=timezone.now())#.exclude(support_business_status=None).exclude(Q(support_business_status=1)|(Q(support_business_status=2)|(Q(support_business_status=6))))
    for filter in tag_list:
        if filter != "" and filter != None:
            if "명 이하" in filter or "명 이상" in filter:
                num = int(re.findall('\d+', filter)[0])
                if num != 0:
                    support_business_set = support_business_set.filter(support_business_employee_condition__lte=num)
                else:
                    pass
            elif filter!="구성원 제한없음":
                support_business_set = support_business_set.filter(support_business_raw_filter_text__contains=filter)
    for support_business in support_business_set:
        obj = {}
        obj["tag"] = []
        obj["support_business_name"] = support_business.support_business_name
        obj["id"] = support_business.id
        obj["support_business_poster"] = support_business.support_business_poster
        try:
            obj["is_favored"] = is_in_favor_list("support_business", support_business.id , user_auth_id)
        except:
            obj["is_favored"] = False
        obj["support_business_apply_end_ymdt"] = (support_business.support_business_apply_end_ymdt)
        obj["support_business_short_desc"] = support_business.support_business_short_desc
        obj["favorite"] =  (support_business.additionaluserinfo_set.all()).count()
        obj["comp"]=""


        if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
            number =  str(round((
                Appliance.objects.filter(support_business_id=support_business.id).filter(is_submit=True)).count() / int(
                support_business.support_business_recruit_size), 1))
            if number == "0.0":
                number ="0"
            obj["comp"] = number + " : 1"

        else:
            obj["comp"] = ""

        obj["selected_support_business_filter_list"]=[]
        print(obj["selected_support_business_filter_list"])
        for s in support_business.selected_support_business_filter_list.all():
            obj["selected_support_business_filter_list"].append(s.filter_name)
        obj["rec"]=0

        for f in support_business.selected_support_business_filter_list.all():
            obj["tag"].append(f.filter_name)
            if f.filter_name in tag_list:
                obj["rec"]= obj["rec"]+1


        # if random.randrange(0,10)%2==0:
        #     obj["img"] = img_list[random.randrange(0,9)]

        result["data"].append(copy.deepcopy(obj))
    try:
        if gca_check_session(request) != False:
            user_id = gca_check_session(request)
            user_startup = Startup.objects.get(user = AdditionalUserInfo.objects.get(id=user_id).user)
            result["usr_filter"] = []
            for f in user_startup.selected_company_filter_list.all():
                result["usr_filter"].append(f.filter_name)
            print(result['usr_filter'])
    except:
        pass
    return JsonResponse(result)
vue_home_support_business_new()

[]
[]
{'sql': "SELECT `supporting_business_supportbusiness`.`id`, `supporting_business_supportbusiness`.`support_business_author_id`, `supporting_business_supportbusiness`.`support_business_created_at_ymdt`, `supporting_business_supportbusiness`.`support_business_name`, `supporting_business_supportbusiness`.`support_business_name_tag`, `supporting_business_supportbusiness`.`support_business_name_sub`, `supporting_business_supportbusiness`.`support_business_poster`, `supporting_business_supportbusiness`.`support_business_relate_support_business_id`, `supporting_business_supportbusiness`.`support_business_short_desc`, `supporting_business_supportbusiness`.`support_business_subject`, `supporting_business_supportbusiness`.`support_business_detail`, `supporting_business_supportbusiness`.`support_business_apply_start_ymd`, `supporting_business_supportbusiness`.`support_business_apply_end_ymdt`, `supporting_business_supportbusiness`.`support_business_object`, `supporting_business_supportbusin

<JsonResponse status_code=200, "application/json">

In [25]:
@my_timer
def get_channel_content():
    result={}
    result["clip"]=[]
    result["course"]=[]
    result["path"]=[]
    for c in Clip.objects.all().order_by("-id"):
        temp = {}
        temp["clip_id"] = c.id
        try:
            temp["clip_user"] = c.clip_user.user.startup.mark_name
        except:
            temp["clip_user"] = c.clip_user.mng_name
        temp["clip_thumb"] = c.clip_thumb
        temp["clip_title"] = c.clip_title
        temp["clip_play"] = c.clip_play
        temp["clip_created_at"] = c.clip_created_at
        temp["clip_info"] = c.clip_info
        temp["clip_tag"] = []
        
        #temp["is_favored"] = is_in_favor_list("clip", c.id, user_auth_id)
        temp["clip_entry_point"] = "/channel/clip/view/" + str(c.id)
        # 채널 통계에서 사용되는 레이블과 value
        temp["label"] = c.clip_title
        temp["value"] = c.id
        temp["tag"] = []
        for t in c.clip_filter.all():
            temp["tag"].append(t.name)
        result["clip"].append(copy.deepcopy(temp))
    for c in Course.objects.all().order_by("-id"):
        temp = {}
        temp["id"] = c.id
        try:
            temp["course_entry_point"] = "/channel/course/view/" + str(c.id) + "/" + str(
                c.course_clips.all().first().id)
        except Exception as e:
            temp["course_entry_point"] = ""
        try:
            temp["course_user"] = c.course_user.user.startup.mark_name
        except:
            temp["course_user"] = c.course_user.mng_name
        temp["course_thumb"] = c.course_thumb
        temp["course_id"] = c.id
        temp["label"] = c.course_title
        temp["value"] = c.id
        #temp["is_favored"] = is_in_favor_list("course", c.id, user_auth_id)
        temp["course_title"] = c.course_title
        temp["course_rec_dur"] = c.course_rec_dur
        temp["course_created_at"] = c.course_created_at
        temp["course_info"] = c.course_info
        temp["course_tag"] = []
        temp["course_total_play"] = c.course_total_play
        for t in c.course_filter.all():
            temp["course_tag"].append(t.name)
        result["course"].append(copy.deepcopy(temp))

    for c in Path.objects.all().order_by("-id"):
        temp = {}
        temp["id"] = c.id
        try:
            temp["path_entry_point"] = "/channel/path/view/" + str(c.id) + "/" + str(
                c.path_course.all().first().id) + "/" + str(c.path_course.first().course_clips.all().first().id)
        except Exception as e:
            temp["path_entry_point"] = ""
        try:
            temp["path_user"] = c.path_user.user.startup.mark_name
        except:
            temp["path_user"] = c.path_user.mng_name
        temp["path_thumb"] = c.path_thumb
        temp["path_title"] = c.path_title
        temp["path_rec_dur"] = c.path_rec_dur
        temp["label"] = c.path_title
        temp["value"] = c.id
        #temp["is_favored"] = is_in_favor_list("path", c.id, user_auth_id)
        temp["path_total_play"] = c.path_total_play
        temp["path_id"] = c.id
        temp["path_created_at"] = c.path_created_at
        temp["path_info"] = c.path_info
        temp["path_tag"] = []
        for t in c.path_filter.all():
            temp["path_tag"].append(t.name)
        result["path"].append(copy.deepcopy(temp))
    return JsonResponse(result, safe=False)
get_channel_content()

{'sql': 'SELECT `supporting_business_clip`.`id`, `supporting_business_clip`.`clip_user_id`, `supporting_business_clip`.`clip_title`, `supporting_business_clip`.`clip_youtube`, `supporting_business_clip`.`clip_mov_url`, `supporting_business_clip`.`clip_thumb`, `supporting_business_clip`.`clip_object`, `supporting_business_clip`.`clip_info`, `supporting_business_clip`.`clip_play`, `supporting_business_clip`.`clip_created_at` FROM `supporting_business_clip` ORDER BY `supporting_business_clip`.`id` DESC', 'time': '0.000'}
{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluseri

<JsonResponse status_code=200, "application/json">

In [82]:
@my_timer
def get_channel_content():

    result={}
    result["clip"]=[]
    result["course"]=[]
    result["path"]=[]
    for c in Clip.objects.select_related("clip_user__own_startup").prefetch_related("clip_filter").order_by("-id"):
        temp = {}
        temp["clip_id"] = c.id
        try:
            temp["clip_user"] = c.clip_user.own_startup.mark_name
        except:
            temp["clip_user"] = c.clip_user.mng_name
        temp["clip_thumb"] = c.clip_thumb
        temp["clip_title"] = c.clip_title
        temp["clip_play"] = c.clip_play
        temp["clip_created_at"] = c.clip_created_at
        temp["clip_info"] = c.clip_info
        temp["clip_tag"] = []
        
        #temp["is_favored"] = is_in_favor_list("clip", c.id, user_auth_id)
        # 채널 통계에서 사용되는 레이블과 value
        temp["label"] = c.clip_title
        temp["value"] = c.id
        temp["tag"] = []
        for t in c.clip_filter.all():
            temp["tag"].append(t.name)
        result["clip"].append(copy.deepcopy(temp))
    for c in Course.objects.select_related("course_user__own_startup").prefetch_related("course_filter").prefetch_related("course_clips").order_by("-id"):
        temp = {}
        temp["id"] = c.id
        try:
            temp["course_user"] = c.course_user.own_startup.mark_name
        except:
            temp["course_user"] = c.course_user.mng_name
        temp["course_thumb"] = c.course_thumb
        temp["course_id"] = c.id
        temp["label"] = c.course_title
        temp["value"] = c.id
        #temp["is_favored"] = is_in_favor_list("course", c.id, user_auth_id)
        temp["course_title"] = c.course_title
        temp["course_rec_dur"] = c.course_rec_dur
        temp["course_created_at"] = c.course_created_at
        temp["course_info"] = c.course_info
        temp["course_tag"] = []
        temp["course_total_play"] = c.course_total_play
        for t in c.course_filter.all():
            temp["course_tag"].append(t.name)
        result["course"].append(copy.deepcopy(temp))

    for c in Path.objects.select_related("path_user__own_startup").prefetch_related("path_filter").prefetch_related("path_course").order_by("-id"):
        temp = {}
        temp["id"] = c.id
        try:
            temp["path_user"] = c.path_user.own_startup.mark_name
        except:
            temp["path_user"] = c.path_user.mng_name
        temp["path_thumb"] = c.path_thumb
        temp["path_title"] = c.path_title
        temp["path_rec_dur"] = c.path_rec_dur
        temp["label"] = c.path_title
        temp["value"] = c.id
        #temp["is_favored"] = is_in_favor_list("path", c.id, user_auth_id)
        temp["path_total_play"] = c.path_total_play
        temp["path_id"] = c.id
        temp["path_created_at"] = c.path_created_at
        temp["path_info"] = c.path_info
        temp["path_tag"] = []
        for t in c.path_filter.all():
            temp["path_tag"].append(t.name)
        result["path"].append(copy.deepcopy(temp))
    return JsonResponse(result, safe=False)
get_channel_content()

{'sql': 'SELECT `supporting_business_clip`.`id`, `supporting_business_clip`.`clip_user_id`, `supporting_business_clip`.`clip_title`, `supporting_business_clip`.`clip_youtube`, `supporting_business_clip`.`clip_mov_url`, `supporting_business_clip`.`clip_thumb`, `supporting_business_clip`.`clip_object`, `supporting_business_clip`.`clip_info`, `supporting_business_clip`.`clip_play`, `supporting_business_clip`.`clip_created_at`, `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinf

<JsonResponse status_code=200, "application/json">

In [27]:
@my_timer
def vue_get_application():
  
    startup = Startup.objects.get(id=99)
    support_business = SupportBusiness.objects.get(id=308)
    app, created = Appliance.objects.get_or_create(startup_id=99, support_business_id=308)
    result = {}

    if created == True:
        print("생성되었습니다.")
        result["id"] = app.id
        result["st_id"]= startup.id
        app.st_id = startup.id
        result["support_business_id"] = support_business.id
        app.support_business_id = support_business.id
        result["support_business_appliance_form"] = support_business.support_business_appliance_form
        result["support_business_meta"] = support_business.support_business_meta
        result["address_0"] = startup.address_0
        app.address_0 = startup.address_0
        result["address_1"] = startup.address_1
        app.address_1 = startup.address_1
        result["company_name"] = startup.company_name
        app.company_name = startup.company_name
        result["established_date"] = startup.established_date
        app.established_date = startup.established_date

        result["repre_name"] = startup.repre_name
        app.repre_name = startup.repre_name
        result["repre_tel"] = startup.repre_tel
        app.repre_tel = startup.repre_tel
        result["repre_email"] = startup.repre_email
        app.repre_email = startup.repre_email

        result["mark_name"] = startup.mark_name
        app.mark_name = startup.mark_name
        result["mark_email"] = startup.mark_email
        app.mark_email = startup.mark_email
        result["mark_tel"] = startup.mark_tel
        app.mark_tel = startup.mark_tel

        result["company_website"] = startup.company_website
        app.company_website = startup.company_website
        result["company_youtube"] = startup.company_youtube
        app.company_youtube = startup.company_youtube
        result["company_instagram"] = startup.company_instagram
        app.company_instagram = startup.company_instagram
        result["company_facebook"] = startup.company_facebook
        app.company_facebook=startup.company_facebook
        result["company_kind"] = startup.company_kind
        app.company_kind= startup.company_kind


        result["company_keyword"] = startup.company_keyword
        app.company_keyword = startup.company_keyword
        result["attached_ir_file"] = startup.attached_ir_file
        app.attached_ir_file=startup.attached_ir_file
        result["attached_cert_file"] = startup.attached_cert_file
        app.attached_cert_file = startup.attached_cert_file
        result["attached_tax_file"] = startup.attached_tax_file
        app.attached_tax_file = startup.attached_tax_file
        result["attached_fund_file"] = startup.attached_fund_file
        app.attached_fund_file=startup.attached_fund_file
        result["attached_ppt_file"] = startup.attached_ppt_file
        app.attached_ppt_file = startup.attached_ppt_file
        result["attached_etc_file"] = ""
        result["attached_ip_file"] = startup.attached_ip_file
        app.attached_ip_file = startup.attached_ip_file
        result["company_total_employee"] = 0
        app.company_total_employee = 0
        result["company_hold_employee"] = 0
        app.company_hold_employee =0
        result["company_assurance_employee"] = 0
        app.company_assurance_employee = 0
        result["revenue_before_0"] = startup.revenue_before_0
        app.revenue_before_0=startup.revenue_before_0
        result["revenue_before_1"] = startup.revenue_before_1
        app.revenue_before_1=startup.revenue_before_1
        result["revenue_before_2"] = startup.revenue_before_2
        app.revenue_before_2 = startup.revenue_before_2
        result[ "revenue_before_year_0"] = 2017
        app.revenue_before_year_0 = 2017
        result["revenue_before_year_1"] = 2016
        app.revenue_before_year_1 =2016
        result[ "revenue_before_year_2"] = 2015
        app.revenue_before_year_2 = 2015
        result["export_before_0"] = startup.export_before_0 if app.export_before_0 == "None" or app.export_before_0 == "" else app.export_before_0
        app.export_before_0 = startup.export_before_0
        result["export_before_1"] = startup.export_before_1 if app.export_before_1 == "None" or app.export_before_1 == "" else app.export_before_1
        app.export_before_1 = startup.export_before_1
        result["export_before_2"] = startup.export_before_2 if app.export_before_2 == "None" or app.export_before_2 == "" else app.export_before_2
        app.export_before_2 = startup.export_before_2
        result[ "export_before_year_0"] = 2017
        app.export_before_year_0 = 2017
        result["export_before_year_1"] = 2016
        app.export_before_year_1 = 2016
        result[ "export_before_year_2"] = 2015
        app.export_before_year_2 = 2015
        result["export_before_nation_0"] = startup.export_before_nation_0 if app.export_before_nation_0 == "None" or app.export_before_nation_0 == "" else app.export_before_nation_0
        app.export_before_nation_0 = startup.export_before_nation_0
        result["export_before_nation_1"] = startup.export_before_nation_1 if app.export_before_nation_1 == "None" or app.export_before_nation_1 == "" else app.export_before_nation_1
        app.export_before_nation_1=startup.export_before_nation_1
        result[ "export_before_nation_2"] = startup.export_before_nation_2 if app.export_before_nation_2 == "None" or app.export_before_nation_2 == "" else app.export_before_nation_2
        app.export_before_nation_2 = startup.export_before_nation_2
        result["company_intro"] = startup.company_intro if app.company_intro==None or app.company_intro=="" else app.company_intro
        app.company_intro = startup.company_intro
        result["company_history"] = []
        app.save()
        for t in startup.history_set.all():
            his = ApplianceHistory()
            his.appliance = app
            his.company_history_year=t.company_history_year
            his.company_history_content=t.company_history_content
            his.save()
            result["company_history"].append({
                "company_history_year": t.company_history_year,
                "company_history_content": t.company_history_content,
                "id": his.id,
            })

        result["invest"] = []
        print(app.applianceinvest_set)
        for inv in startup.companyinvest_set.all():
            appinv =  ApplianceInvest()
            appinv.applicance = app
            appinv.company_invest_year= inv.company_invest_year
            appinv.company_invest_size= inv.company_invest_size
            appinv.company_invest_agency= inv.company_invest_agency
            appinv.save()
            result["invest"].append({
                "id":appinv.id,
                "company_invest_year":inv.company_invest_year,
                "company_invest_size": inv.company_invest_size,
                "company_invest_agency": inv.company_invest_agency,
            })
        result["tag"]=[]
        result["base_filter"] = []
        result["special_filter"] = []
        area_filter=[]
        for t in startup.selected_company_filter_list.all():
            app.selected_company_filter_list.add(t)

        for t in startup.selected_company_filter_list.all():
            if t.cat_0 == "기본장르" or t.cat_0=="영역":
                area_filter.append(t.filter_name)
        for t in startup.selected_company_filter_list.all():
            if t.cat_0 =="기본장르":
                result["base_filter"].append(t.filter_name)
            elif t.cat_0 =="영역":
                result["special_filter"].append(t.filter_name)
        print()
        result["is_submit"] = False
        result["service"] = []
        for s in startup.service_set.all():
            app_ser = ApplianceService()
            app_ser.appliance = app
            app_ser.service_name=s.service_name
            app_ser.service_intro=s.service_intro
            app_ser.startup = startup
            app_ser.save()
            result["service"].append({"service_name":s.service_name,"":s.service_intro ,"id":app_ser.id})
        result["created"] = True
    else:
        result["id"] = app.id
        result["st_id"] = startup.id
        result["created"] = False
        result["support_business_id"] = support_business.id
        result["support_business_appliance_form"] = support_business.support_business_appliance_form
        result["support_business_meta"] = support_business.support_business_meta
        result["address_0"] =  app.address_0
        result["address_1"] =  app.address_1

        result["company_name"] = startup.company_name
        result["established_date"] = startup.established_date
        result["company_kind"] = startup.company_kind

        result["repre_name"] =  app.repre_name
        result["repre_tel"] =  app.repre_tel
        result["repre_email"] = app.repre_email
        result["mark_name"] =  app.mark_name
        result["mark_email"] =  app.mark_email
        result["mark_tel"] = app.mark_tel
        result[ "company_website"] = app.company_website
        result["company_youtube"] =  app.company_youtube
        result["company_instagram"] =  app.company_instagram
        result["company_facebook"] = app.company_facebook

        result["company_keyword"] =  app.company_keyword
        result["attached_ir_file"] =  app.attached_ir_file
        result["attached_cert_file"] =  app.attached_cert_file
        result["attached_tax_file"] =   app.attached_tax_file
        result["attached_fund_file"] =  app.attached_fund_file
        result["attached_ppt_file"] =  app.attached_ppt_file
        result["attached_etc_file"] =  app.attached_etc_file
        result["attached_ip_file"] = app.attached_ip_file
        result["company_total_employee"] = app.company_total_employee
        result["company_hold_employee"] = app.company_hold_employee
        result["company_assurance_employee"] =  app.company_assurance_employee
        result["revenue_before_0"] = app.revenue_before_0
        result["revenue_before_1"] = app.revenue_before_1
        result["revenue_before_2"] = app.revenue_before_2
        result["revenue_before_year_0"] = 2017
        result["revenue_before_year_1"] = 2016
        result["revenue_before_year_2"] = 2015
        result["export_before_0"] = app.export_before_0
        result["export_before_1"] = app.export_before_1
        result["export_before_2"] =  app.export_before_2
        result["export_before_year_0"] = 2017
        result["export_before_year_1"] = 2016
        result["export_before_year_2"] = 2015
        result["export_before_nation_0"] =  app.export_before_nation_0
        result["export_before_nation_1"] =  app.export_before_nation_1
        result["export_before_nation_2"] = app.export_before_nation_2
        result["company_intro"] =  app.company_intro
        result["company_history"] = []
        for t in app.appliancehistory_set.all():
            result["company_history"].append({
                "company_history_year": t.company_history_year,
                "company_history_content": t.company_history_content,
                "id": t.id,
            })
        result["invest"] = []
        for inv in app.applianceinvest_set.all():
            result["invest"].append({
                "id":inv.id,
                "company_invest_year": inv.company_invest_year,
                "company_invest_size": inv.company_invest_size,
                "company_invest_agency": inv.company_invest_agency,
            })
        result["tag"] = []
        result["base_filter"] = []
        result["special_filter"] = []
        area_filter = []
        for t in app.selected_company_filter_list.all():
            if t.cat_0 == "기본장르" or t.cat_0 == "영역":
                area_filter.append(t.filter_name)
        for t in app.selected_company_filter_list.all():
            if t.cat_0 == "기본장르":
                result["base_filter"].append(t.filter_name)
            elif t.cat_0 == "영역":
                result["special_filter"].append(t.filter_name)
        result["service"] = []
        for s in app.applianceservice_set.all():
            result["service"].append({"service_name": s.service_name, "service_intro": s.service_intro, "id": s.id})
        result["is_submit"]=app.is_submit
        result["is_applied_to_company_info"] = app.is_applied_to_company_info


    return JsonResponse(result, )
vue_get_application()

{'sql': 'SELECT `supporting_business_startup`.`id`, `supporting_business_startup`.`user_id`, `supporting_business_startup`.`company_name`, `supporting_business_startup`.`established_date`, `supporting_business_startup`.`logo`, `supporting_business_startup`.`back_img`, `supporting_business_startup`.`company_short_desc`, `supporting_business_startup`.`company_intro`, `supporting_business_startup`.`company_youtube`, `supporting_business_startup`.`company_facebook`, `supporting_business_startup`.`company_instagram`, `supporting_business_startup`.`company_website`, `supporting_business_startup`.`address_0`, `supporting_business_startup`.`address_1`, `supporting_business_startup`.`repre_name`, `supporting_business_startup`.`repre_email`, `supporting_business_startup`.`repre_tel`, `supporting_business_startup`.`mark_name`, `supporting_business_startup`.`mark_email`, `supporting_business_startup`.`mark_tel`, `supporting_business_startup`.`company_keyword`, `supporting_business_startup`.`compan

<JsonResponse status_code=200, "application/json">

In [28]:
@my_timer
def vue_get_course():

    result={}
    clip= Clip.objects.get(id=134)
    course = Course.objects.get(id=100 )
 
    result["course_title"] = Course.objects.get(id=100).course_title
    result["clip_title"] = clip.clip_title
    result["course_play"] = course.course_total_play
    result["course_youtube"] = clip.clip_youtube
    result["course_mov_url"] = clip.clip_mov_url
    result["course_object"] = clip.clip_object
    result["course_info"] = clip.clip_info
    result["course_info"] = clip.clip_info
    #result["is_favored"] = is_in_favor_list( "course", course.id , user_auth_id)
    try:
        result["course_user"] = clip.clip_user.user.startup.mark_name
    except:
        result["course_user"] = clip.clip_user.mng_name
    result["course_created_at"] = clip.clip_created_at
    result["int"] = (clip.additionaluserinfo_set.all()).count()
    result["course_id"] = course.id
    result["tag"] = []
    for t in clip.clip_filter.all():
        result["tag"].append(t.name)
    result["another_clip"]=[]
    k=1
    url_list = []
    prefix = "/channel/course/view/"
    for c in Course.objects.get(id=100).course_clips.all():
        temp={}
        url_list.append(prefix + str(course.id)+"/"+ str(c.id) )
        temp["index"] = k
        k=k+1
        temp["id"] = c.id
        temp["clip_play"] = c.clip_play
        temp["clip_created_at"] = c.clip_created_at
        try:
            temp["clip_user"] = c.clip_user.user.startup.mark_name
        except:
            temp["clip_user"] = c.clip_user.mng_name
        temp["clip_title"] = c.clip_title
        result["another_clip"].append(copy.deepcopy(temp))

    result["another_course"] = []
    for c in Course.objects.all().order_by("?")[:2]:
        temp = {}
        temp["id"] = c.id
        temp["course_title"] = c.course_title
        temp["course_total_play"] = c.course_total_play
        temp["course_thumb"] = c.course_thumb
        try:
            temp["course_user"] = c.course_user.user.startup.mark_name
        except:
            temp["course_user"] = c.course_user.mng_name

        temp["course_created_at"] = c.course_created_at
        try:
            temp["course_entry_point"] = "/channel/course/view/"+str(c.id)+"/"+str(c.course_clips.first().id)+"/"
        except:
            pass
        result["another_course"].append(copy.deepcopy(temp))
    present = url_list.index("/channel/course/view/"+ str(course.id) +"/"+str(clip.id) )
    if present == 0:
        prev=""
    else:
        prev = url_list[present - 1]
    if present == len(url_list)-1:
        next= ""
    else:
        next = url_list[present+1]
    result["prev_url"]= prev
    result["next_url"] = next
    return JsonResponse(result)
vue_get_course()

{'sql': 'SELECT `supporting_business_clip`.`id`, `supporting_business_clip`.`clip_user_id`, `supporting_business_clip`.`clip_title`, `supporting_business_clip`.`clip_youtube`, `supporting_business_clip`.`clip_mov_url`, `supporting_business_clip`.`clip_thumb`, `supporting_business_clip`.`clip_object`, `supporting_business_clip`.`clip_info`, `supporting_business_clip`.`clip_play`, `supporting_business_clip`.`clip_created_at` FROM `supporting_business_clip` WHERE `supporting_business_clip`.`id` = 134', 'time': '0.016'}
{'sql': 'SELECT `supporting_business_course`.`id`, `supporting_business_course`.`course_user_id`, `supporting_business_course`.`course_title`, `supporting_business_course`.`course_thumb`, `supporting_business_course`.`course_rec_dur`, `supporting_business_course`.`course_object`, `supporting_business_course`.`course_info`, `supporting_business_course`.`course_total_play`, `supporting_business_course`.`course_created_at` FROM `supporting_business_course` WHERE `supporting_bu

<JsonResponse status_code=200, "application/json">

In [102]:
@my_timer
def vue_get_course():

    result={}
    clip= Clip.objects.get(id=134)
    course = Course.objects.get(id=100 ) 
    result["course_title"] = Course.objects.get(id=100).course_title
    result["clip_title"] = clip.clip_title
    result["course_play"] = course.course_total_play
    result["course_youtube"] = clip.clip_youtube
    result["course_mov_url"] = clip.clip_mov_url
    result["course_object"] = clip.clip_object
    result["course_info"] = clip.clip_info
    result["course_info"] = clip.clip_info
    #result["is_favored"] = is_in_favor_list( "course", course.id , user_auth_id)
    try:
        result["course_user"] = clip.clip_user.own_startup.mark_name
    except:
        result["course_user"] = clip.clip_user.mng_name
    result["course_created_at"] = clip.clip_created_at
    result["int"] = (clip.additionaluserinfo_set.all()).count()
    result["course_id"] = course.id
    result["tag"] = []
    for t in clip.clip_filter.all():
        result["tag"].append(t.name)
    result["another_clip"]=[]
    k=1
    url_list = []
    prefix = "/channel/course/view/"
    for c in Course.objects.get(id=100).course_clips.select_related("clip_user__own_startup"):
        temp={}
        url_list.append(prefix + str(course.id)+"/"+ str(c.id) )
        temp["index"] = k
        k=k+1
        temp["id"] = c.id
        temp["clip_play"] = c.clip_play
        temp["clip_created_at"] = c.clip_created_at
        try:
            temp["clip_user"] = c.clip_user.own_startup.mark_name
        except:
            temp["clip_user"] = c.clip_user.mng_name
        temp["clip_title"] = c.clip_title
        result["another_clip"].append(copy.deepcopy(temp))

    result["another_course"] = []
    for c in Course.objects.select_related("course_user__own_startup").prefetch_related("course_clips").order_by("?")[:2]:
        temp = {}
        temp["id"] = c.id
        temp["course_title"] = c.course_title
        temp["course_total_play"] = c.course_total_play
        temp["course_thumb"] = c.course_thumb
        try:
            temp["course_user"] = c.course_user.own_startup.mark_name
        except:
            temp["course_user"] = c.course_user.mng_name

        temp["course_created_at"] = c.course_created_at
        try:
            temp["course_entry_point"] = "/channel/course/view/"+str(c.id)+"/"+str(c.course_clips.first().id)+"/"
        except:
            pass
        result["another_course"].append(copy.deepcopy(temp))
    present = url_list.index("/channel/course/view/"+ str(course.id) +"/"+str(clip.id) )
    if present == 0:
        prev=""
    else:
        prev = url_list[present - 1]
    if present == len(url_list)-1:
        next= ""
    else:
        next = url_list[present+1]
    result["prev_url"]= prev
    result["next_url"] = next
    return JsonResponse(result)
vue_get_course()

{'sql': 'SELECT `supporting_business_clip`.`id`, `supporting_business_clip`.`clip_user_id`, `supporting_business_clip`.`clip_title`, `supporting_business_clip`.`clip_youtube`, `supporting_business_clip`.`clip_mov_url`, `supporting_business_clip`.`clip_thumb`, `supporting_business_clip`.`clip_object`, `supporting_business_clip`.`clip_info`, `supporting_business_clip`.`clip_play`, `supporting_business_clip`.`clip_created_at` FROM `supporting_business_clip` WHERE `supporting_business_clip`.`id` = 134', 'time': '0.023'}
{'sql': 'SELECT `supporting_business_course`.`id`, `supporting_business_course`.`course_user_id`, `supporting_business_course`.`course_title`, `supporting_business_course`.`course_thumb`, `supporting_business_course`.`course_rec_dur`, `supporting_business_course`.`course_object`, `supporting_business_course`.`course_info`, `supporting_business_course`.`course_total_play`, `supporting_business_course`.`course_created_at` FROM `supporting_business_course` WHERE `supporting_bu

<JsonResponse status_code=200, "application/json">

In [29]:
@my_timer
def vue_get_path():
 
    result={}
    path_url_list = []
    try:
        clip= Clip.objects.get(id=134)
        result["clip_title"] = clip.clip_title
        result["clip_youtube"] = clip.clip_youtube
        result["clip_mov_url"] = clip.clip_mov_url
        result["object"] = clip.clip_object
        result["course_info"] = clip.course_info
        result["tag"] = []
        for t in clip.clip_filter.all():
            result["tag"].append(t.name)
        result["clip_id"] = clip.id
        result["int"] = (clip.additionaluserinfo_set.all()).count()
        result["clip_play"] = clip.clip_play
        result["user"] = clip.user.name
        result["created"] = clip.created_at

    except Exception as e:
        print(e)

    p = Path.objects.get(id=32)
    result["path_filter"] = []
    try:
        result["user"] = p.path_user.user.startup.mark_name
    except:
        result["user"] = p.path_user.mng_name
    for t in p.path_filter.all():
        result["path_filter"].append(t.name)
    result["path_title"] = p.path_title
    result["path_rec_dur"] = p.path_rec_dur
    result["path_id"] = p.id
    result["path_info"] = p.path_info
    result["path_object"] = p.path_object
    result["path_created_at"] = p.path_created_at
    result["is_favored"]=""
    try:
        if p in AdditionalUserInfo.objects.get(id=user_auth_id).favorite_path.all():
            result["is_favored"] = "true"
        else:
            result["is_favored"] = "false"
    except:
        result["is_favored"] = "false"
    result["total_play"] = p.path_total_play
    result["course"]=[]
    result["another_course"] = []

    k = 1
    a = 1
    # 패스 => 코스 항목
    for c in Path.objects.get(id=32).path_course.all():
            temp = {}
            temp["index"] = a
            a = a + 1
            k = 1
            temp["id"] = c.id
            temp["course_title"] = c.course_title
            try:
                temp["author"] = c.course_user.user.startup.mark_name
            except:
                temp["author"] = c.course_user.mng_name
            temp["course_created_at"] = c.course_created_at
            temp["course_info"] = c.course_info
            temp["course_object"] = c.course_object
            temp["course_rec_dur"] = c.course_rec_dur
            temp["course_total_play"] = c.course_total_play

            temp["course_filter"] = []
            for f in c.course_filter.all():
                temp["course_filter"].append(f.name)

            temp["clips"] = []
            # 코스 항목 => 강좌 항목 //
            for clip in c.course_clips.all():
                ttem = {}
                ttem["index"] = k
                k = k + 1
                ttem["id"] = clip.id
                try:
                    ttem["clip_user"] = clip.clip_user.user.startup.mark_name
                except:
                    ttem["clip_user"] = clip.clip_user.mng_name
                ttem["clip_play"] = clip.clip_play
                ttem["clip_title"] = clip.clip_title
                ttem["clip_created_at"] = clip.clip_created_at
                ttem["clip_info"] = clip.clip_info
                ttem["clip_object"] = clip.clip_object
                temp["clips"].append(copy.deepcopy(ttem))
                path_url_list.append(str(p.id)+"/"+str(c.id)+"/"+str(clip.id))

            result["course"].append(copy.deepcopy(temp))
            result["another_course"].append(copy.deepcopy(temp))

#     path_index = path_url_list.index(str(p.id)+"/"+request.POST.get('course') + "/" +request.POST.get("clip"))
#     if path_index-1 >= 0:
#         prev_url = path_url_list[path_index-1]
#     else:
#         prev_url = ""
#     if path_index < len(path_url_list)-1:
#         next_url = path_url_list[path_index+1]
#     else :
#         next_url = ""
#     result["prev_url"] = prev_url
#     result["next_url"] = next_url

    temp= JsonResponse(result)
#    temp_content= temp.content // json string
#    //  update stat_table set json_data= temp_content where  stat_id=1;
    return temp
vue_get_path()

'Clip' object has no attribute 'course_info'
{'sql': 'SELECT `supporting_business_clip`.`id`, `supporting_business_clip`.`clip_user_id`, `supporting_business_clip`.`clip_title`, `supporting_business_clip`.`clip_youtube`, `supporting_business_clip`.`clip_mov_url`, `supporting_business_clip`.`clip_thumb`, `supporting_business_clip`.`clip_object`, `supporting_business_clip`.`clip_info`, `supporting_business_clip`.`clip_play`, `supporting_business_clip`.`clip_created_at` FROM `supporting_business_clip` WHERE `supporting_business_clip`.`id` = 134', 'time': '0.000'}
{'sql': 'SELECT `supporting_business_path`.`id`, `supporting_business_path`.`path_user_id`, `supporting_business_path`.`path_title`, `supporting_business_path`.`path_thumb`, `supporting_business_path`.`path_rec_dur`, `supporting_business_path`.`path_object`, `supporting_business_path`.`path_info`, `supporting_business_path`.`path_total_play`, `supporting_business_path`.`path_created_at` FROM `supporting_business_path` WHERE `supp

<JsonResponse status_code=200, "application/json">

In [30]:
@my_timer
def get_startup_application():

    startup = Startup.objects.get(id=74)
    result={}
    #작성중인 지원서
    result["writing"]=[]

    for ap in Appliance.objects.filter(startup=startup).filter(is_submit=False):
        try:
            temp = {}
            temp["support_business_name"] = ap.support_business.support_business_name
            temp["favorite"] = (ap.support_business.additionaluserinfo_set.all()).count()
            temp["support_business_id"] = ap.support_business.id
            temp["support_business_kikwan"] = ap.support_business.support_business_author.mng_kikwan
            temp["support_business_poster"] = ap.support_business.support_business_poster
            temp["support_business_apply_start_ymd"] = ap.support_business.support_business_apply_start_ymd
            temp["support_business_apply_end_ymdt"] = ap.support_business.support_business_apply_end_ymdt
            temp["updated"] = ap.appliance_update_at_ymdt

            if ap.support_business.support_business_recruit_size == "" or ap.support_business.support_business_recruit_size == None or  ap.support_business.support_business_recruit_size== "0" :
                temp["comp"] =  str((Appliance.objects.filter(support_business=ap.support_business).filter(is_submit=True)).count()) +" : 1"
            else:
                #temp["comp"] = len(Appliance.objects.filter(support_business=ap.support_business)) / int(ap.support_business.recruit_size)
                number = str(round( ((Appliance.objects.filter(support_business=ap.support_business).filter(is_submit=True).count()))/int(ap.support_business.support_business_recruit_size ),1 ) )
                if number == "0.0":
                    number ="0"
                temp["comp"] = ""
            try:
                if ap.support_business.support_business_status == "4":  # 작성중인 공고문
                    temp["status"] = "모집종료"
                if ap.support_business.support_business_status == "1":  # 작성중인 공고문
                    temp["status"] = "작성중"
                if ap.support_business.support_business_status == "2":  # 승인대기중인 공고문
                    temp["status"]= "승인대기"
                if ap.support_business.support_business_status == "3":
                    temp["status"] = "공고중"
                if ap.support_business.support_business_apply_end_ymdt < timezone.now() and ap.support_business.support_business_status == "3":  # 모집 종료 된 공고문
                    temp["status"] = "모집종료"
                if ap.support_business.support_business_status == "5":  # 공고 종료 된 공고문
                    temp["status"] = "공고종료"
                if ap.support_business.support_business_status == "6":  # 블라인드 공고문
                    temp["status"]= "블라인드"
            except Exception as e:
                print(e)
                temp["status"] = "작성중"

            temp["date"] = str(ap.support_business.support_business_pro_0_end_ymd).split(" ")[0]
            temp["start"] = str(ap.support_business.support_business_apply_start_ymd).split(" ")[0]
            temp["id"] = ap.id
            result["writing"].append(copy.deepcopy(temp))
                # 지원완료 지원서
        except Exception as e:
            print(e)
    result["comp"] = []
    for ap in Appliance.objects.filter(startup=startup).filter(is_submit=True):
        temp = {}
        temp["support_business_name"] = ap.support_business.support_business_name
        temp["favorite"] = (ap.support_business.additionaluserinfo_set.all()).count()
        temp["updated"] = ap.appliance_update_at_ymdt
        if ap.support_business.support_business_recruit_size == "" or  ap.support_business.support_business_recruit_size == None  or ap.support_business.support_business_recruit_size == "0":
            temp["comp"] = ""
        else:


            # temp["comp"] = len(Appliance.objects.filter(support_business=ap.support_business)) / int(ap.support_business.recruit_size)
            number = str( round(((Appliance.objects.filter(support_business=ap.support_business).filter(
                is_submit=True).count())) / int(ap.support_business.support_business_recruit_size ), 1) )
            if number == "0.0":
                number ="0"
            temp["comp"] = str(number) +" : 1"
        temp["date"] = str(ap.support_business.support_business_pro_0_end_ymd).split(" ")[0]
        temp["start"] = str(ap.support_business.support_business_pro_0_start_ymd).split(" ")[0]
        temp["support_business_kikwan"] = ap.support_business.support_business_author.mng_kikwan
        temp["support_business_apply_start_ymd"] = ap.support_business.support_business_apply_start_ymd
        temp["support_business_poster"] = ap.support_business.support_business_poster
        temp["support_business_apply_end_ymdt"] = ap.support_business.support_business_apply_end_ymdt
        temp["id"] = ap.id
        temp["support_business_id"]=ap.support_business.id
        award_num = (Award.objects.filter(support_business=ap.support_business).filter(startup=startup)).count()
        is_award=False
        if award_num !=0 :
            is_award = True
        temp["is_awarded"]= is_award


        try:
            if ap.support_business.support_business_status == "4":  # 작성중인 공고문
                temp["status"] = "모집종료"
            if ap.support_business.support_business_status == "1":  # 작성중인 공고문
                temp["status"] = "작성중"
            if ap.support_business.support_business_status == "2":  # 승인대기중인 공고문
                temp["status"] = "승인대기"
            if ap.support_business.support_business_status == "3":
                temp["status"] = "공고중"
            if ap.support_business.support_business_apply_end_ymdt < timezone.now() and ap.support_business.support_business_status == "3":  # 모집 종료 된 공고문
                temp["status"] = "모집종료"
            if ap.support_business.support_business_status == "5":  # 공고 종료 된 공고문
                temp["status"] = "공고종료"
            if ap.support_business.support_business_status == "6":  # 블라인드 공고문
                temp["status"] = "블라인드"
        except Exception as e:
            print(e)
            temp["status"] = "작성중"
        result["comp"].append(copy.deepcopy(temp))

    result["end"] = []
    for ap in Appliance.objects.filter(startup=startup).filter(is_submit=True).filter(Q(support_business__support_business_status="5")):

        temp = {}
        temp["support_business_name"] = ap.support_business.support_business_name
        temp["favorite"] = (ap.support_business.additionaluserinfo_set.all()).count()
        if ap.support_business.support_business_recruit_size == ""or  ap.support_business.support_business_recruit_size == None  or ap.support_business.support_business_recruit_size == "0":
            temp["comp"] = ""
        else:
            # temp["comp"] = len(Appliance.objects.filter(support_business=ap.support_business)) / int(ap.support_business.recruit_size)
            number = str( round(((Appliance.objects.filter(support_business=ap.support_business).filter(
                is_submit=True).count())) / int(ap.support_business.support_business_recruit_size ), 1) )
            if number == "0.0":
                number ="0"
            temp["comp"] = number + " : 1"
        temp["date"] = str(ap.support_business.support_business_pro_0_end_ymd).split(" ")[0]
        temp["start"] = str(ap.support_business.support_business_pro_0_start_ymd).split(" ")[0]
        temp["support_business_apply_start_ymd"] = ap.support_business.support_business_apply_start_ymd
        temp["support_business_poster"] = ap.support_business.support_business_poster
        temp["support_business_apply_end_ymdt"] = ap.support_business.support_business_apply_end_ymdt
        temp["id"] = ap.id
        temp["support_business_id"]=ap.support_business.id
        temp["updated"] = ap.appliance_update_at_ymdt
        award_num = (Award.objects.filter(support_business=ap.support_business).filter(startup=startup)).count()
        is_award=False
        if award_num !=0 :
            is_award = True
        temp["is_awarded"]= is_award


        try:
            if ap.support_business.support_business_status == "4":  # 작성중인 공고문
                temp["status"] = "모집종료"
            if ap.support_business.support_business_status == "1":  # 작성중인 공고문
                temp["status"] = "작성중"
            if ap.support_business.support_business_status == "2":  # 승인대기중인 공고문
                temp["status"] = "승인대기"
            if ap.support_business.support_business_status == "3":
                temp["status"] = "공고중"
            if ap.support_business.support_business_apply_end_ymdt < timezone.now() and ap.support_business.support_business_status == "3":  # 모집 종료 된 공고문
                temp["status"] = "모집종료"
            if ap.support_business.support_business_status == "5":  # 공고 종료 된 공고문
                temp["status"] = "공고종료"
            if ap.support_business.support_business_status == "6":  # 블라인드 공고문
                temp["status"] = "블라인드"
        except Exception as e:
            print(e)
            temp["status"] = "작성중"
        result["end"].append(copy.deepcopy(temp))


    return JsonResponse(result)
get_startup_application()

{'sql': 'SELECT `supporting_business_startup`.`id`, `supporting_business_startup`.`user_id`, `supporting_business_startup`.`company_name`, `supporting_business_startup`.`established_date`, `supporting_business_startup`.`logo`, `supporting_business_startup`.`back_img`, `supporting_business_startup`.`company_short_desc`, `supporting_business_startup`.`company_intro`, `supporting_business_startup`.`company_youtube`, `supporting_business_startup`.`company_facebook`, `supporting_business_startup`.`company_instagram`, `supporting_business_startup`.`company_website`, `supporting_business_startup`.`address_0`, `supporting_business_startup`.`address_1`, `supporting_business_startup`.`repre_name`, `supporting_business_startup`.`repre_email`, `supporting_business_startup`.`repre_tel`, `supporting_business_startup`.`mark_name`, `supporting_business_startup`.`mark_email`, `supporting_business_startup`.`mark_tel`, `supporting_business_startup`.`company_keyword`, `supporting_business_startup`.`compan

<JsonResponse status_code=200, "application/json">

In [31]:
@my_timer
def vue_get_startup_detail_base():
    print("hello")

    startup = AdditionalUserInfo.objects.get(id=74).user.startup
    result = {}
    result["back_img"] = startup.back_img
    result["logo"] = startup.logo
    result["company_website"] = startup.company_website
    result["company_youtube"] = startup.company_youtube
    result["company_instagram"] = startup.company_instagram
    result["company_facebook"] = startup.company_facebook
    result["established_date"]= str(startup.established_date).split("T")[0]
    result["select_tag"]= ""
    result["repre_tel"] =startup.repre_tel
    result["repre_email"] = startup.user.username
    result["mark_tel"] = startup.mark_tel
    result["mark_email"] = startup.mark_email
    result["mark_name"] = startup.mark_name
    result["startup_id"] = startup.id
    result["company_name"] = startup.company_name

    result["company_keyword"] = startup.company_keyword
    result["company_kind"] = startup.company_kind

    result["address_0"] = startup.address_0
    result["address_1"] = startup.address_1
    result["company_intro"] = startup.company_intro
    result["information"] = {}
    result["information"]["id"] = startup.id
    result["information"]["tag"] = []
    result['information']["company_website"] = startup.company_website
    result['information']["mark_email"] = startup.mark_email
    try:
        result["location"] = startup.address_0 + startup.address_1
    except:
        pass
    result["service"] = []
    result["tag"] = []
    result["intro_tag"] = []
    result["select_tag"] = []
    for f in startup.selected_company_filter_list.all():
        result['information']["tag"].append(f.filter_name)
        if f.cat_0 == "기본장르" or f.cat_0 == "영역" or f.cat_0 == "조건":
            print("필터를 넣습니다.")
            result["intro_tag"].append(f.filter_name)
            result["select_tag"].append(f.filter_name)
    result["company_history"] = []
    print(startup.company_total_employee)
    if startup.company_total_employee != "":
        print("hrer")
        print(  result["intro_tag"])

        result["intro_tag"].append(startup.company_total_employee+" 명 이하")
    for history in startup.history_set.all():
        obj={}
        obj["company_history_year"] = history.company_history_year

        obj["company_history_month"] = history.company_history_month
        obj["company_history_content"] = history.company_history_content
        obj["id"] = history.id
        result["company_history"].append(copy.deepcopy(obj))


    return JsonResponse(result)
vue_get_startup_detail_base()

hello
필터를 넣습니다.
필터를 넣습니다.
필터를 넣습니다.
필터를 넣습니다.
필터를 넣습니다.
필터를 넣습니다.
필터를 넣습니다.
필터를 넣습니다.
필터를 넣습니다.
필터를 넣습니다.
필터를 넣습니다.
필터를 넣습니다.
0
hrer
['출판', '만화', '음악', '게임', '영화', '애니메이션', '방송', '전문디자인', '경기도 기업 이용 기업', '상품/상용화', '캐릭터', '법인사업자']
{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `suppor

<JsonResponse status_code=200, "application/json">

In [32]:
@my_timer
def get_vue_mng_dashboard():
 
    result = {}
    support_business_author_id = 11
    end=""
    end_support_business = SupportBusiness.objects.filter(support_business_apply_end_ymdt__lt=datetime.now()).filter(
        Q(support_business_status="4") | Q(support_business_status="3")).filter(
        support_business_author_id=support_business_author_id)
    result = []
    end = end_support_business.count()

    if(True):
    # 모집 마감된 공고문
        end_support_business = SupportBusiness.objects.filter(support_business_apply_end_ymdt__lt=datetime.now()).filter(
            Q(support_business_status="4") | Q(support_business_status="3")).filter(
            support_business_author_id=support_business_author_id)
        result = []
        end = end_support_business.count()
        for support_business in end_support_business:
            result_end = {}
            result_end["id"] = support_business.id
            result_end["author_id"] = support_business.support_business_author.id
            result_end["support_business_award_date_ymd"] = support_business.support_business_pro_0_open_ymd
            result_end['support_business_name'] = support_business.support_business_name
            result_end['support_business_poster'] = support_business.support_business_poster

            result_end["support_business_apply_start_ymd"] = support_business.support_business_apply_start_ymd
            result_end["support_business_apply_end_ymdt"] = support_business.support_business_apply_end_ymdt
            result_end["apply_num"] = (
            Appliance.objects.filter(support_business_id=support_business.id).filter(is_submit=True)).count()
            try:
                if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
                    number = str(round((Appliance.objects.filter(support_business_id=support_business.id).filter(
                        is_submit=True)).count() / int(support_business.support_business_recruit_size), 1))
                    if (number == "0.0"):
                        number = "0"
                    result_end["comp"] = number + " : 1"
                else:
                    result_end["comp"] = ""
            except:
                result_end["comp"] = ""
            result.append(copy.deepcopy(result_end))
    blind=""
    blind_support_business = SupportBusiness.objects.filter(support_business_status="6").filter(
        support_business_author_id=support_business_author_id)
    blind = blind_support_business.count()
    if True:
        blind_support_business = SupportBusiness.objects.filter(support_business_status="6").filter(
            support_business_author_id=support_business_author_id)
        blind= blind_support_business.count()
        blind_set = []
        result=[]
        for support_business in blind_support_business:
            result_end = {}
            result_end["id"] = support_business.id
            result_end["support_business_award_date_ymd"] = support_business.support_business_pro_0_open_ymd
            result_end['support_business_name'] = support_business.support_business_name
            result_end["support_business_apply_start_ymd"] = support_business.support_business_apply_start_ymd
            result_end["support_business_apply_end_ymdt"] = support_business.support_business_apply_end_ymdt
            result_end['support_business_poster'] = support_business.support_business_poster
            result_end["apply_num"] = (
            Appliance.objects.filter(support_business_id=support_business.id).filter(is_submit=True)).count()
            try:
                if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
                    number = str(round((
                                           Appliance.objects.filter(support_business_id=support_business.id).filter(
                                               is_submit=True)).count() / int(
                        support_business.support_business_recruit_size), 1))
                    if number == "0.0":
                        number = "0"
                    result_end["comp"] = number + " : 1"
                    pass
                else:
                    result_end["comp"] = ""
            except:
                result_end["comp"] = ""
            result.append(copy.deepcopy(result_end))
    writing=""
    writing_support_business = SupportBusiness.objects.filter(support_business_status="1").filter(
        support_business_author_id=support_business_author_id)
    writing = writing_support_business.count()
    if True:

        writing_support_business = SupportBusiness.objects.filter(support_business_status="1").filter(
            support_business_author_id=support_business_author_id)
        writing = writing_support_business.count()
        writing_set = []
        result=[]
        for support_business in writing_support_business:
            result_end = {}
            result_end["id"] = support_business.id
            result_end["support_business_award_date_ymd"] = \
            str(support_business.support_business_update_at_ymdt).split(" ")[0]
            result_end['support_business_name'] = support_business.support_business_name
            result_end['support_business_poster'] = support_business.support_business_poster
            result_end["support_business_apply_start_ymd"] = support_business.support_business_apply_start_ymd
            result_end["support_business_apply_end_ymdt"] = support_business.support_business_apply_end_ymdt
            result_end["apply_num"] = (
            Appliance.objects.filter(support_business_id=support_business.id).filter(is_submit=True)).count()
            result_end["comp"] = ""
            try:
                if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
                    number = str(round((
                                           Appliance.objects.filter(support_business_id=support_business.id).filter(
                                               is_submit=True)).count() / int(
                        support_business.support_business_recruit_size), 1))
                    if number == "0.0":
                        number = "0"
                    result_end["comp"] = number + " : 1"
                    pass
                else:
                    result_end["comp"] = ""
            except:
                result_end["comp"] = ""
            result.append(copy.deepcopy(result_end))
    ing=""
    ing_support_business = SupportBusiness.objects.filter(support_business_status="3").filter(
        support_business_author_id=support_business_author_id).filter(
        support_business_apply_end_ymdt__gt=timezone.now())
    ing_set = []
    ing = ing_support_business.count()
    if True:
        ing_support_business = SupportBusiness.objects.filter(support_business_status="3").filter(
            support_business_author_id=support_business_author_id).filter(
            support_business_apply_end_ymdt__gt=timezone.now())
        ing_set = []
        ing=ing_support_business.count()
        for support_business in ing_support_business:

            result_end = {}
            result_end["id"] = support_business.id
            result_end["support_business_award_date_ymd"] = support_business.support_business_pro_0_open_ymd
            result_end["author_id"] = support_business.support_business_author.id
            result_end['support_business_name'] = support_business.support_business_name
            result_end['support_business_poster'] = support_business.support_business_poster
            result_end["support_business_apply_start_ymd"] = support_business.support_business_apply_start_ymd
            result_end["support_business_apply_end_ymdt"] = support_business.support_business_apply_end_ymdt
            result_end["apply_num"] = (
            Appliance.objects.filter(support_business_id=support_business.id).filter(is_submit=True)).count()
            result_end["comp"] = ""
            try:
                if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
                    number = str(round((
                                           Appliance.objects.filter(support_business_id=support_business.id).filter(
                                               is_submit=True)).count() / int(
                        support_business.support_business_recruit_size), 1))
                    if number == "0.0":
                        number = "0"
                    result_end["comp"] = number + " : 1"

                else:
                    result_end["comp"] = ""
            except:
                result_end["comp"] = ""
            result.append(copy.deepcopy(result_end))
    return JsonResponse({"result_set":result,"set_num":{"ing": ing, "blind":blind ,"writing":writing, "end":end }}, safe=False)
get_vue_mng_dashboard()

{'sql': "SELECT COUNT(*) AS `__count` FROM `supporting_business_supportbusiness` WHERE (`supporting_business_supportbusiness`.`support_business_apply_end_ymdt` < '2018-12-13 19:46:18.541976' AND (`supporting_business_supportbusiness`.`support_business_status` = '4' OR `supporting_business_supportbusiness`.`support_business_status` = '3') AND `supporting_business_supportbusiness`.`support_business_author_id` = 11)", 'time': '0.000'}
{'sql': "SELECT COUNT(*) AS `__count` FROM `supporting_business_supportbusiness` WHERE (`supporting_business_supportbusiness`.`support_business_apply_end_ymdt` < '2018-12-13 19:46:18.541976' AND (`supporting_business_supportbusiness`.`support_business_status` = '4' OR `supporting_business_supportbusiness`.`support_business_status` = '3') AND `supporting_business_supportbusiness`.`support_business_author_id` = 11)", 'time': '0.016'}
{'sql': "SELECT `supporting_business_supportbusiness`.`id`, `supporting_business_supportbusiness`.`support_business_author_id`, 

<JsonResponse status_code=200, "application/json">

In [160]:
@my_timer
def get_vue_mng_dashboard():
 
    result = {}
    support_business_author_id = 11
    end=""
    end_support_business = SupportBusiness.objects.filter(support_business_apply_end_ymdt__lt=datetime.now()).filter(
        Q(support_business_status="4") | Q(support_business_status="3")).filter(
        support_business_author_id=support_business_author_id)
    result = []
    end = end_support_business.count()

    if(True):
    # 모집 마감된 공고문
        
        end_support_business = SupportBusiness.objects.filter(support_business_apply_end_ymdt__lt=datetime.now()).filter(
            Q(support_business_status="4") | Q(support_business_status="3")).filter(
            support_business_author_id=support_business_author_id).prefetch_related("support_business_author")\
        .prefetch_related("appliance_set").annotate(apply_num=(
         Sum(Case(
            When(supportbusiness__appliance__is_submit=True, then=1),
            default=0,
            output_field=models.IntegerField(),
          ))
        ))
        result = []       
        for support_business in end_support_business:
            result_end = {}
            result_end["id"] = support_business.id
            result_end["author_id"] = support_business.support_business_author.id
            result_end["support_business_award_date_ymd"] = support_business.support_business_pro_0_open_ymd
            result_end['support_business_name'] = support_business.support_business_name
            result_end['support_business_poster'] = support_business.support_business_poster
            result_end["support_business_apply_start_ymd"] = support_business.support_business_apply_start_ymd
            result_end["support_business_apply_end_ymdt"] = support_business.support_business_apply_end_ymdt
#             result_end["apply_num"] =  support_business.appliance_set.filter(is_submit=True).count()
            
            print("annotate:"+str(support_business.apply_num))
#             print(result_end["apply_num"])
#             if((support_business.apply_num) != result_end["apply_num"] ):
#                 print(support_business.id)
            try:
                if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
                    number = str(round( result_end["apply_num"] / int(support_business.support_business_recruit_size), 1))
                    if (number == "0.0"):
                        number = "0"
                    result_end["comp"] = number + " : 1"
                else:
                    result_end["comp"] = ""
            except:
                result_end["comp"] = ""
            result.append(copy.deepcopy(result_end))
#     blind=""
#     blind_support_business = SupportBusiness.objects.filter(support_business_status="6").filter(
#         support_business_author_id=support_business_author_id)
#     blind = blind_support_business.count()
#     if True:
#         blind_support_business = SupportBusiness.objects.filter(support_business_status="6").filter(
#             support_business_author_id=support_business_author_id)\
#         .prefetch_related("appliance_set")
     
#         blind_set = []
#         result=[]
#         for support_business in blind_support_business:
#             result_end = {}
#             result_end["id"] = support_business.id
#             result_end["support_business_award_date_ymd"] = support_business.support_business_pro_0_open_ymd
#             result_end['support_business_name'] = support_business.support_business_name
#             result_end["support_business_apply_start_ymd"] = support_business.support_business_apply_start_ymd
#             result_end["support_business_apply_end_ymdt"] = support_business.support_business_apply_end_ymdt
#             result_end['support_business_poster'] = support_business.support_business_poster
#             result_end["apply_num"] = support_business.appliance_set.filter(is_submit=True).count()
#             try:
#                 if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
#                     number = str(round( result_end["apply_num"]  / int(
#                         support_business.support_business_recruit_size), 1))
#                     if number == "0.0":
#                         number = "0"
#                     result_end["comp"] = number + " : 1"
#                     pass
#                 else:
#                     result_end["comp"] = ""
#             except:
#                 result_end["comp"] = ""
#             result.append(copy.deepcopy(result_end))
#     writing=""
#     writing_support_business = SupportBusiness.objects.filter(support_business_status="1").filter(
#         support_business_author_id=support_business_author_id)
#     writing = writing_support_business.count()
#     if True:
#         writing_support_business = SupportBusiness.objects.filter(support_business_status="1").filter(
#             support_business_author_id=support_business_author_id)\
#         .prefetch_related("appliance_set")
     
#         result=[]
#         for support_business in writing_support_business:
#             result_end = {}
#             result_end["id"] = support_business.id
#             result_end["support_business_award_date_ymd"] = \
#             str(support_business.support_business_update_at_ymdt).split(" ")[0]
#             result_end['support_business_name'] = support_business.support_business_name
#             result_end['support_business_poster'] = support_business.support_business_poster
#             result_end["support_business_apply_start_ymd"] = support_business.support_business_apply_start_ymd
#             result_end["support_business_apply_end_ymdt"] = support_business.support_business_apply_end_ymdt
#             result_end["apply_num"] =support_business.appliance_set.filter(is_submit=True).count()
#             result_end["comp"] = ""
#             try:
#                 if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
#                     number = str(round(result_end["apply_num"] / int(
#                         support_business.support_business_recruit_size), 1))
#                     if number == "0.0":
#                         number = "0"
#                     result_end["comp"] = number + " : 1"
#                     pass
#                 else:
#                     result_end["comp"] = ""
#             except:
#                 result_end["comp"] = ""
#             result.append(copy.deepcopy(result_end))
#     ing=""
#     ing_support_business = SupportBusiness.objects.filter(support_business_status="3").filter(
#         support_business_author_id=support_business_author_id).filter(
#         support_business_apply_end_ymdt__gt=timezone.now())
#     ing_set = []
#     ing = ing_support_business.count()
#     if True:
#         ing_support_business = SupportBusiness.objects.filter(support_business_status="3").filter(
#             support_business_author_id=support_business_author_id).filter(
#             support_business_apply_end_ymdt__gt=timezone.now())\
#         .prefetch_related("appliance_set").prefetch_related("support_business_author")
             
#         for support_business in ing_support_business:

#             result_end = {}
#             result_end["id"] = support_business.id
#             result_end["support_business_award_date_ymd"] = support_business.support_business_pro_0_open_ymd
#             result_end["author_id"] = support_business.support_business_author.id
#             result_end['support_business_name'] = support_business.support_business_name
#             result_end['support_business_poster'] = support_business.support_business_poster
#             result_end["support_business_apply_start_ymd"] = support_business.support_business_apply_start_ymd
#             result_end["support_business_apply_end_ymdt"] = support_business.support_business_apply_end_ymdt
#             result_end["apply_num"] = len(support_business.appliance_set.filter(is_submit=True))
#             result_end["comp"] = ""
#             try:
#                 if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
#                     number = str(round(result_end["apply_num"] / int(
#                         support_business.support_business_recruit_size), 1))
#                     if number == "0.0":
#                         number = "0"
#                     result_end["comp"] = number + " : 1"

#                 else:
#                     result_end["comp"] = ""
#             except:
#                 result_end["comp"] = ""
#             result.append(copy.deepcopy(result_end))
#     return JsonResponse({"result_set":result,"set_num":{"ing": ing, "blind":blind ,"writing":writing, "end":end }}, safe=False)
get_vue_mng_dashboard()

annotate:0
annotate:0
annotate:0
annotate:0
annotate:0
annotate:0
annotate:0
annotate:0
annotate:0
annotate:0
annotate:0
annotate:0
annotate:0
annotate:0
annotate:0
annotate:0
annotate:0
annotate:0
annotate:0
{'sql': "SELECT COUNT(*) AS `__count` FROM `supporting_business_supportbusiness` WHERE (`supporting_business_supportbusiness`.`support_business_apply_end_ymdt` < '2018-12-13 23:33:18.397120' AND (`supporting_business_supportbusiness`.`support_business_status` = '4' OR `supporting_business_supportbusiness`.`support_business_status` = '3') AND `supporting_business_supportbusiness`.`support_business_author_id` = 11)", 'time': '0.011'}
{'sql': "SELECT `supporting_business_supportbusiness`.`id`, `supporting_business_supportbusiness`.`support_business_author_id`, `supporting_business_supportbusiness`.`support_business_created_at_ymdt`, `supporting_business_supportbusiness`.`support_business_name`, `supporting_business_supportbusiness`.`support_business_name_tag`, `supporting_business_su

In [146]:
sp = SupportBusiness.objects.get(id=302).appliance_set.all()
print(sp.filter(is_submit=True).count())
print(sp.count())

3
4


In [34]:
@my_timer
def vue_get_support_business_select_name_by_kikwan_2():

    support_business_list=[]
    for sp in SupportBusiness.objects.filter(support_business_apply_end_ymdt__lte=timezone.now() ).filter( Q(support_business_status="3") |  Q(support_business_status="5") | Q(support_business_status="4") ):
        support_business_list.append({
            "author":sp.support_business_author.mng_name,
            "author_id": sp.support_business_author.id,
            "name":sp.support_business_name,
            "support_business_id":sp.id,
            "support_business_status":sp.support_business_status
            })

    return JsonResponse(support_business_list, safe=False)
vue_get_support_business_select_name_by_kikwan_2()

{'sql': "SELECT `supporting_business_supportbusiness`.`id`, `supporting_business_supportbusiness`.`support_business_author_id`, `supporting_business_supportbusiness`.`support_business_created_at_ymdt`, `supporting_business_supportbusiness`.`support_business_name`, `supporting_business_supportbusiness`.`support_business_name_tag`, `supporting_business_supportbusiness`.`support_business_name_sub`, `supporting_business_supportbusiness`.`support_business_poster`, `supporting_business_supportbusiness`.`support_business_relate_support_business_id`, `supporting_business_supportbusiness`.`support_business_short_desc`, `supporting_business_supportbusiness`.`support_business_subject`, `supporting_business_supportbusiness`.`support_business_detail`, `supporting_business_supportbusiness`.`support_business_apply_start_ymd`, `supporting_business_supportbusiness`.`support_business_apply_end_ymdt`, `supporting_business_supportbusiness`.`support_business_object`, `supporting_business_supportbusiness`.`

<JsonResponse status_code=200, "application/json">

In [35]:
@my_timer
def vue_get_support_business_select_name_by_kikwan_2():

    support_business_list=[]
    for sp in SupportBusiness.objects.filter(support_business_apply_end_ymdt__lte=timezone.now() ).filter( Q(support_business_status="3") |  Q(support_business_status="5") | Q(support_business_status="4") ).select_related("support_business_author"):
        support_business_list.append({
            "author":sp.support_business_author.mng_name,
            "author_id": sp.support_business_author.id,
            "name":sp.support_business_name,
            "support_business_id":sp.id,
            "support_business_status":sp.support_business_status
            })

    return JsonResponse(support_business_list, safe=False)
vue_get_support_business_select_name_by_kikwan_2()

{'sql': "SELECT `supporting_business_supportbusiness`.`id`, `supporting_business_supportbusiness`.`support_business_author_id`, `supporting_business_supportbusiness`.`support_business_created_at_ymdt`, `supporting_business_supportbusiness`.`support_business_name`, `supporting_business_supportbusiness`.`support_business_name_tag`, `supporting_business_supportbusiness`.`support_business_name_sub`, `supporting_business_supportbusiness`.`support_business_poster`, `supporting_business_supportbusiness`.`support_business_relate_support_business_id`, `supporting_business_supportbusiness`.`support_business_short_desc`, `supporting_business_supportbusiness`.`support_business_subject`, `supporting_business_supportbusiness`.`support_business_detail`, `supporting_business_supportbusiness`.`support_business_apply_start_ymd`, `supporting_business_supportbusiness`.`support_business_apply_end_ymdt`, `supporting_business_supportbusiness`.`support_business_object`, `supporting_business_supportbusiness`.`

<JsonResponse status_code=200, "application/json">

In [36]:
@my_timer
def vue_get_support_business_select_name_1():
    mng = AdditionalUserInfo.objects.get(id=11)
    support_business_list = []
    for sp in SupportBusiness.objects.filter(support_business_author=mng).filter(support_business_status__in=["3"]).filter(support_business_apply_end_ymdt__gte=timezone.now()):#.filter(support_business_apply_end_ymdt__gte=timezone.now()):
        support_business_list.append({
            "author": sp.support_business_author.mng_name,
            "name":sp.support_business_name,
            "support_business_id":sp.id,
            "support_business_status": sp.support_business_status
        })
    return JsonResponse(support_business_list, safe=False)
vue_get_support_business_select_name_1()

{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busine

<JsonResponse status_code=200, "application/json">

In [115]:

@my_timer
def mng_vue_get_startup_account():

    startup= Startup.objects.all()
    result = []
    if True:
        k=1
        startup_set=[]
        for s in startup :
            temp={}
            temp["mng_index"]=k
            k=k+1
            temp["mng_company_name"] = s.company_name
            temp["mng_id"] = s.user.username
            temp["mng_startup_id"] = s.id
            temp["mng_mark_name"] = s.mark_name
            temp["mng_mark_tel"] = s.mark_tel
            temp["mng_mark_email"] = s.mark_email
            tag_list=[]
            for t in s.selected_company_filter_list.all():
                tag_list.append(t.filter_name)
            temp["mng_tag"] = tag_list
            try:
                if "경기" in s.address_0:
                    local = "경기"
                elif "서울" in s.address_0:
                    local = "서울"
                elif "인천" in s.address_0:
                    local = "인천"
                else :
                    local = "기타"
            except:
                local="기타"
            temp["mng_local"] = local
            temp["mng_employ_num"] = int(s.company_total_employee) if s.company_total_employee else 0
            temp["mng_apply_num"] = (Appliance.objects.filter(startup=s)).count()
            temp["mng_award_num"] = (Award.objects.filter(startup=s)).count()
            temp["mng_join"] = s.user.date_joined
            temp["mng_tag"]=[]
            for t in s.selected_company_filter_list.all():
                temp["mng_tag"].append(t.filter_name)
            startup_set.append(copy.deepcopy(temp))
        result = startup_set
    if True:
        user_ad = AdditionalUserInfo.objects.exclude(auth=4).exclude(auth=5)
        user_set = []
        p=1
        for u in user_ad:
            try:
                user = {}
                user["mng_id"] = u.user.username
                user["mng_startup_id"] = Startup.objects.get(user=u.user).id
                user["mng_mark_name"] = Startup.objects.get(user=u.user).mark_name
                user["mng_mark_tel"] = Startup.objects.get(user=u.user).mark_tel
                user["mng_facebook"] = Startup.objects.get(user=u.user).company_facebook
                user["mng_joined"] = u.user.date_joined
                user["mng_index"]=p
                p=p+1
                user_set.append(copy.deepcopy(user))
            except Exception as e:
                pass
        result = user_set
    if True:
        ## 사업 참여 기업
        aw_startup_set = Appliance.objects.all().values("startup").distinct()
        k=1
        ap_set = []
        for s in aw_startup_set:
            aw_st={}
            startup = Startup.objects.get(id=s["startup"])
            aw_st["mng_index"] = k
            k=k+1
            aw_st["mng_company_name"] = startup.company_name
            aw_st["mng_mark_name"] = startup.mark_name
            aw_st["mng_startup_id"] = startup.id
            aw_st["mng_mark_tel"] = startup.mark_tel
            tag_list = []
            for t in startup.selected_company_filter_list.all():
                tag_list.append(t.filter_name)
            aw_st["mng_tag"] = tag_list
            try:
                if "경기" in startup.address_0:
                    local = "경기"
                elif "서울" in startup.address_0:
                    local = "서울"
                elif "인천" in startup.address_0:
                    local = "인천"
                else:
                    local = "기타"
            except:
                local="기타"
            aw_st["mng_local"] = local
            aw_st["mng_support_business_name"] = Appliance.objects.filter(startup=startup).last().support_business.support_business_name
            if (Award.objects.filter(support_business=Appliance.objects.filter(startup=startup).last().support_business).filter(startup=startup)).count() == 0 :
                aw_st["mng_awarded"] = "N"
            else:
                aw_st["mng_awarded"] = "Y"
            aw_st["mng_end_date"] = str(Appliance.objects.filter(startup=startup).last().support_business.support_business_apply_end_ymdt).split(" ")[0]
            ap_set.append(copy.deepcopy(aw_st))
        result = ap_set
  
    return JsonResponse({"result":result})

mng_vue_get_startup_account()

{'sql': 'SELECT `supporting_business_startup`.`id`, `supporting_business_startup`.`user_id`, `supporting_business_startup`.`company_name`, `supporting_business_startup`.`established_date`, `supporting_business_startup`.`logo`, `supporting_business_startup`.`back_img`, `supporting_business_startup`.`company_short_desc`, `supporting_business_startup`.`company_intro`, `supporting_business_startup`.`company_youtube`, `supporting_business_startup`.`company_facebook`, `supporting_business_startup`.`company_instagram`, `supporting_business_startup`.`company_website`, `supporting_business_startup`.`address_0`, `supporting_business_startup`.`address_1`, `supporting_business_startup`.`repre_name`, `supporting_business_startup`.`repre_email`, `supporting_business_startup`.`repre_tel`, `supporting_business_startup`.`mark_name`, `supporting_business_startup`.`mark_email`, `supporting_business_startup`.`mark_tel`, `supporting_business_startup`.`company_keyword`, `supporting_business_startup`.`compan

<JsonResponse status_code=200, "application/json">

In [127]:

@my_timer
def mng_vue_get_startup_account():
    startup= Startup.objects.select_related("user").prefetch_related("appliance_set").prefetch_related("award_set")\
    .prefetch_related("selected_company_filter_list")
    result = []
    if True:
        k=1
        startup_set=[]
        for s in startup :
            temp={}
            temp["mng_index"]=k
            k=k+1
            temp["mng_company_name"] = s.company_name
            temp["mng_id"] = s.user.username
            temp["mng_startup_id"] = s.id
            temp["mng_mark_name"] = s.mark_name
            temp["mng_mark_tel"] = s.mark_tel
            temp["mng_mark_email"] = s.mark_email
            temp["mng_tag"]=[]
            for f in s.selected_company_filter_list.all():
                temp["mng_tag"].append(f.filter_name)             
            try:
                if "경기" in s.address_0:
                    local = "경기"
                elif "서울" in s.address_0:
                    local = "서울"
                elif "인천" in s.address_0:
                    local = "인천"
                else :
                    local = "기타"
            except:
                local="기타"
            temp["mng_local"] = local
            temp["mng_employ_num"] = int(s.company_total_employee) if s.company_total_employee else 0
            temp["mng_apply_num"] =  s.appliance_set.count() #  (Appliance.objects.filter(startup=s)).count()
            temp["mng_award_num"] = s.award_set.count() # (Award.objects.filter(startup=s)).count()          
            temp["mng_join"] = s.user.date_joined
            startup_set.append(copy.deepcopy(temp))
        result = startup_set
    if True:
        user_ad = AdditionalUserInfo.objects.filter(auth="USR").prefetch_related("user").prefetch_related("own_startup")
        user_set = []
        p=1
        for u in user_ad:
            try:
                user = {}
                user["mng_id"] = u.user.username
                user["mng_startup_id"] = u.own_startup.id                 
                user["mng_mark_name"] = u.own_startup.mark_name
                user["mng_mark_tel"] = u.own_startup.mark_tel
                user["mng_facebook"] = u.own_startup.company_facebook
                user["mng_joined"] = u.user.date_joined
                user["mng_index"]=p
                p=p+1
                user_set.append(copy.deepcopy(user))
            except Exception as e:
                pass
        result = user_set
    if True:
        ## 사업 참여 기업               
        aw_startup_set = Appliance.objects.values_list("startup", flat=True).distinct()
        k=1
        ap_set = []        
        for startup in Startup.objects.filter(id__in=aw_startup_set).prefetch_related("appliance_set__support_business")\
        .prefetch_related("selected_company_filter_list").prefetch_related("award_set"):
            aw_st={}
            aw_st["mng_index"] = k
            k=k+1
            aw_st["mng_company_name"] = startup.company_name
            aw_st["mng_mark_name"] = startup.mark_name
            aw_st["mng_startup_id"] = startup.id
            aw_st["mng_mark_tel"] = startup.mark_tel
            tag_list = []
            for t in startup.selected_company_filter_list.all():
                tag_list.append(t.filter_name)
            aw_st["mng_tag"] = tag_list
            try:
                if "경기" in startup.address_0:
                    local = "경기"
                elif "서울" in startup.address_0:
                    local = "서울"
                elif "인천" in startup.address_0:
                    local = "인천"
                else:
                    local = "기타"
            except:
                local="기타"
            aw_st["mng_local"] = local
            last_appliance =  startup.appliance_set.order_by("-appliance_update_at_ymdt")[0].support_business
            aw_st["mng_support_business_name"] =last_appliance.support_business_name # Appliance.objects.filter(startup=startup).last().support_business.support_business_name
            if(startup.award_set.filter(support_business = last_appliance)):           
                aw_st["mng_awarded"] = "N"
            else:
                aw_st["mng_awarded"] = "Y"
            aw_st["mng_end_date"] = str(last_appliance.support_business_apply_end_ymdt).split(" ")[0]
            ap_set.append(copy.deepcopy(aw_st))
        result = ap_set  
    return JsonResponse({"result":result})
mng_vue_get_startup_account()

{'sql': 'SELECT `supporting_business_startup`.`id`, `supporting_business_startup`.`user_id`, `supporting_business_startup`.`company_name`, `supporting_business_startup`.`established_date`, `supporting_business_startup`.`logo`, `supporting_business_startup`.`back_img`, `supporting_business_startup`.`company_short_desc`, `supporting_business_startup`.`company_intro`, `supporting_business_startup`.`company_youtube`, `supporting_business_startup`.`company_facebook`, `supporting_business_startup`.`company_instagram`, `supporting_business_startup`.`company_website`, `supporting_business_startup`.`address_0`, `supporting_business_startup`.`address_1`, `supporting_business_startup`.`repre_name`, `supporting_business_startup`.`repre_email`, `supporting_business_startup`.`repre_tel`, `supporting_business_startup`.`mark_name`, `supporting_business_startup`.`mark_email`, `supporting_business_startup`.`mark_tel`, `supporting_business_startup`.`company_keyword`, `supporting_business_startup`.`compan

<JsonResponse status_code=200, "application/json">

In [39]:
for ad in AdditionalUserInfo.objects.all():
    try:
        ad.own_startup = ad.user.startup
        ad.save()
    except Exception as e:
        print(e)
        

User has no startup.
User has no startup.


C:\Users\sehyun\AppData\Local\Programs\Python\Python36\lib\site-packages\django\db\backends\mysql\base.py:112: Warning: (1048, "Column 'mng_date_joined_ymd' cannot be null")
  return self.cursor.execute(query, args)


User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.
User has no startup.


In [40]:
@my_timer
def vue_get_support_business_select_name_2():

    mng = AdditionalUserInfo.objects.get(id=11)
    support_business_list = []

    for sp in SupportBusiness.objects.filter(support_business_author=mng).filter(Q(support_business_status="4")|Q(support_business_status="5")|Q(support_business_status="3")).filter(support_business_apply_end_ymdt__lte=timezone.now()):
        print(sp.support_business_name)
        support_business_list.append({
            "author": sp.support_business_author.mng_name,
            "name":sp.support_business_name,
            "support_business_id":sp.id,
            "support_business_status": sp.support_business_status
            })

    return JsonResponse(support_business_list, safe=False)
vue_get_support_business_select_name_2()

테스트 지원사업
ㄴㅇㄹㄴㅇㄹ
234
새로고침 테스트 지원사업
테스트 지원사업명
아이디 클래스로 변경후 테스트하는 공고문 
기업 참여 공고문
테스트 공고문
지원서 양식테스트
123
슈퍼끼어로 시즌5 참가자 모집
테스트입니다.
공고종료 테스트입니다.
공고종료 테스트123
테스트입니다.
테스트
2018년 경기도 다양성영화 국제영화제 참가지원
구석구석 움직이는 경기공방‘ 메이커스 분야 모집
연도/회차/기수‘사업명’모집/지원/참여
아침테스트
첨부서류 테스트 공고문
2018 인기가요
ㅊㅍㅊㅊㅊㅊ
2018년 2차 글로벌 게임센터 입주 모집
2018 피땀눈물
cafe 501
당신은 참 나에게 참
테스트트트
{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supportin

<JsonResponse status_code=200, "application/json">

In [41]:
@my_timer
def vue_get_support_business_select_name_2():

    mng = AdditionalUserInfo.objects.get(id=11)
    support_business_list = []

    for sp in SupportBusiness.objects.filter(support_business_author=mng).filter(Q(support_business_status="4")|Q(support_business_status="5")|Q(support_business_status="3"))\
    .filter(support_business_apply_end_ymdt__lte=timezone.now())\
    .select_related("support_business_author"):
        print(sp.support_business_name)
        support_business_list.append({
            "author": sp.support_business_author.mng_name,
            "name":sp.support_business_name,
            "support_business_id":sp.id,
            "support_business_status": sp.support_business_status
            })

    return JsonResponse(support_business_list, safe=False)
vue_get_support_business_select_name_2()

테스트 지원사업
ㄴㅇㄹㄴㅇㄹ
234
새로고침 테스트 지원사업
테스트 지원사업명
아이디 클래스로 변경후 테스트하는 공고문 
기업 참여 공고문
테스트 공고문
지원서 양식테스트
123
슈퍼끼어로 시즌5 참가자 모집
테스트입니다.
공고종료 테스트입니다.
공고종료 테스트123
테스트입니다.
테스트
2018년 경기도 다양성영화 국제영화제 참가지원
구석구석 움직이는 경기공방‘ 메이커스 분야 모집
연도/회차/기수‘사업명’모집/지원/참여
아침테스트
첨부서류 테스트 공고문
2018 인기가요
ㅊㅍㅊㅊㅊㅊ
2018년 2차 글로벌 게임센터 입주 모집
2018 피땀눈물
cafe 501
당신은 참 나에게 참
테스트트트
{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supportin

<JsonResponse status_code=200, "application/json">

In [42]:
@my_timer
def vue_get_support_business_select_name_3():

    mng = AdditionalUserInfo.objects.get(id=11)
    support_business_list = []
    for sp in SupportBusiness.objects.exclude(support_business_author=mng).filter( Q(support_business_status="3"))\
    .filter(support_business_apply_end_ymdt__gte=timezone.now()):
        support_business_list.append({
            "name":sp.support_business_name,
            "author": sp.support_business_author.mng_name,
            "support_business_id":sp.id,
            "support_business_status": sp.support_business_status
        })
    return JsonResponse(support_business_list, safe=False)
vue_get_support_business_select_name_3()

{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busine

<JsonResponse status_code=200, "application/json">

In [43]:
@my_timer
def vue_get_support_business_select_name_3():

    mng = AdditionalUserInfo.objects.get(id=11)
    support_business_list = []
    for sp in SupportBusiness.objects.exclude(support_business_author=mng).filter( Q(support_business_status="3"))\
    .filter(support_business_apply_end_ymdt__gte=timezone.now())\
    .select_related("support_business_author") :
        support_business_list.append({
            "name":sp.support_business_name,
            "author": sp.support_business_author.mng_name,
            "support_business_id":sp.id,
            "support_business_status": sp.support_business_status
        })
    return JsonResponse(support_business_list, safe=False)
vue_get_support_business_select_name_3()

{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busine

<JsonResponse status_code=200, "application/json">

In [44]:
@my_timer
def vue_get_support_business_select_name_4():
  
    support_business_list = []
    mng = AdditionalUserInfo.objects.get(id=11)
    for sp in SupportBusiness.objects.exclude(support_business_author = mng).filter(Q(support_business_status="4")|Q(support_business_status="5")|Q(support_business_status="3")).filter(support_business_apply_end_ymdt__lte=timezone.now()):
        support_business_list.append({
            "name":sp.support_business_name,
            "author": sp.support_business_author.mng_name,
            "support_business_id":sp.id,
            "support_business_status": sp.support_business_status
        })

    return JsonResponse(support_business_list, safe=False)
vue_get_support_business_select_name_4()


{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busine

<JsonResponse status_code=200, "application/json">

In [45]:
@my_timer
def vue_get_support_business_select_name_4():
  
    support_business_list = []
    mng = AdditionalUserInfo.objects.get(id=11)
    for sp in SupportBusiness.objects.exclude(support_business_author = mng).filter(Q(support_business_status="4")|Q(support_business_status="5")|Q(support_business_status="3")).filter(support_business_apply_end_ymdt__lte=timezone.now()).select_related("support_business_author"):
        support_business_list.append({
            "name":sp.support_business_name,
            "author": sp.support_business_author.mng_name,
            "support_business_id":sp.id,
            "support_business_status": sp.support_business_status
        })

    return JsonResponse(support_business_list, safe=False)
vue_get_support_business_select_name_4()

{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busine

<JsonResponse status_code=200, "application/json">

In [46]:
@my_timer
def vue_get_course_all():
    
    for c in Course.objects.all().order_by("-id"):
        result=[]
        temp={}
        temp["id"] = c.id
        try:
            temp["course_entry_point"] = "/channel/course/view/"+ str(c.id)+"/" + str(c.course_clips.all().first().id)
        except Exception as e:         
            temp["course_entry_point"]=""
        try:
            temp["course_user"]=c.course_user.user.startup.mark_name
        except:
            temp["course_user"] = c.course_user.mng_name
        temp["course_thumb"]=c.course_thumb
        temp["course_id"] = c.id
        temp["label"] = c.course_title
        temp["value"] = c.id
        #temp["is_favored"] = is_in_favor_list("course", c.id, user_auth_id)

        temp["course_title"]=c.course_title
        temp["course_rec_dur"]=c.course_rec_dur
        temp["course_created_at"]=c.course_created_at
        temp["course_info"] = c.course_info
        temp["course_tag"] =[]
        temp["course_total_play"] = c.course_total_play
        for t in c.course_filter.all():
            temp["course_tag"].append(t.name)
        result.append(copy.deepcopy(temp))
    return JsonResponse(result, safe=False)
vue_get_course_all()

{'sql': 'SELECT `supporting_business_course`.`id`, `supporting_business_course`.`course_user_id`, `supporting_business_course`.`course_title`, `supporting_business_course`.`course_thumb`, `supporting_business_course`.`course_rec_dur`, `supporting_business_course`.`course_object`, `supporting_business_course`.`course_info`, `supporting_business_course`.`course_total_play`, `supporting_business_course`.`course_created_at` FROM `supporting_business_course` ORDER BY `supporting_business_course`.`id` DESC', 'time': '0.022'}
{'sql': 'SELECT `supporting_business_clip`.`id`, `supporting_business_clip`.`clip_user_id`, `supporting_business_clip`.`clip_title`, `supporting_business_clip`.`clip_youtube`, `supporting_business_clip`.`clip_mov_url`, `supporting_business_clip`.`clip_thumb`, `supporting_business_clip`.`clip_object`, `supporting_business_clip`.`clip_info`, `supporting_business_clip`.`clip_play`, `supporting_business_clip`.`clip_created_at` FROM `supporting_business_clip` INNER JOIN `supp

<JsonResponse status_code=200, "application/json">

In [83]:
@my_timer
def vue_get_course_all():
    obj =  Course.objects.order_by("-id").prefetch_related("course_user").select_related("course_user__own_startup").prefetch_related("course_filter").prefetch_related("course_clips")
    for c in obj:
        result=[]
        temp={}
        temp["id"] = c.id
        try:
            temp["course_user"]=c.course_user.own_startup.mark_name
        except:
            temp["course_user"] = c.course_user.mng_name
        temp["course_thumb"]=c.course_thumb
        temp["course_id"] = c.id
        temp["label"] = c.course_title
        temp["value"] = c.id
        #temp["is_favored"] = is_in_favor_list("course", c.id, user_auth_id)

        temp["course_title"]=c.course_title
        temp["course_rec_dur"]=c.course_rec_dur
        temp["course_created_at"]=c.course_created_at
        temp["course_info"] = c.course_info
        temp["course_tag"] =[]
        temp["course_total_play"] = c.course_total_play
        for t in c.course_filter.all():
            temp["course_tag"].append(t.name)
        result.append(copy.deepcopy(temp))
    return JsonResponse(result, safe=False)
vue_get_course_all()

{'sql': 'SELECT `supporting_business_course`.`id`, `supporting_business_course`.`course_user_id`, `supporting_business_course`.`course_title`, `supporting_business_course`.`course_thumb`, `supporting_business_course`.`course_rec_dur`, `supporting_business_course`.`course_object`, `supporting_business_course`.`course_info`, `supporting_business_course`.`course_total_play`, `supporting_business_course`.`course_created_at`, `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.

<JsonResponse status_code=200, "application/json">

In [86]:
@my_timer
def vue_get_path_all():
    result = []
    for c in Path.objects.all().select_related("path_user__own_startup").prefetch_related("path_filter").order_by("-id"):
        temp={}
        temp["id"] = c.id

        try:
            temp["path_user"]=c.path_user.own_startup.mark_name
        except:
            temp["path_user"] = c.path_user.mng_name
        temp["path_thumb"]=c.path_thumb
        temp["path_title"]=c.path_title
        temp["path_rec_dur"]=c.path_rec_dur
        temp["label"] = c.path_title
        temp["value"] = c.id
        #temp["is_favored"] = is_in_favor_list("path", c.id, user_auth_id)
        temp["path_total_play"] = c.path_total_play
        temp["path_id"] = c.id
        temp["path_created_at"]=c.path_created_at
        temp["path_info"] = c.path_info
        temp["path_tag"] =[]
        for t in c.path_filter.all():
            temp["path_tag"].append(t.name)
        result.append(copy.deepcopy(temp))
    return JsonResponse(result, safe=False)
vue_get_path_all()

{'sql': 'SELECT `supporting_business_path`.`id`, `supporting_business_path`.`path_user_id`, `supporting_business_path`.`path_title`, `supporting_business_path`.`path_thumb`, `supporting_business_path`.`path_rec_dur`, `supporting_business_path`.`path_object`, `supporting_business_path`.`path_info`, `supporting_business_path`.`path_total_play`, `supporting_business_path`.`path_created_at`, `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_a

<JsonResponse status_code=200, "application/json">

In [85]:
@my_timer
def vue_get_path_all():
    result = []
    obj = Path.objects.order_by("-id").select_related("path_user__own_startup").prefetch_related("path_filter")
    for c in obj:
        temp={}
        temp["id"] = c.id     
        try:
            temp["path_user"]=c.path_user.own_startup.mark_name
        except:
            temp["path_user"] = c.path_user.mng_name
        temp["path_thumb"]=c.path_thumb
        temp["path_title"]=c.path_title
        temp["path_rec_dur"]=c.path_rec_dur
        temp["label"] = c.path_title
        temp["value"] = c.id
        #temp["is_favored"] = is_in_favor_list("path", c.id, user_auth_id)
        temp["path_total_play"] = c.path_total_play
        temp["path_id"] = c.id
        temp["path_created_at"]=c.path_created_at
        temp["path_info"] = c.path_info
        temp["path_tag"] =[]
        for t in c.path_filter.all():
            temp["path_tag"].append(t.name)
        result.append(copy.deepcopy(temp))
    return JsonResponse(result, safe=False)
vue_get_path_all()

{'sql': 'SELECT `supporting_business_path`.`id`, `supporting_business_path`.`path_user_id`, `supporting_business_path`.`path_title`, `supporting_business_path`.`path_thumb`, `supporting_business_path`.`path_rec_dur`, `supporting_business_path`.`path_object`, `supporting_business_path`.`path_info`, `supporting_business_path`.`path_total_play`, `supporting_business_path`.`path_created_at`, `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_a

<JsonResponse status_code=200, "application/json">

In [50]:
@my_timer
def vue_get_path_information():

    result = {}
    path = Path.objects.get(id=65)
    result["path_object"] = path.path_object
    result["path_info"] = path.path_info
    result["path_title"] = path.path_title
    result["path_rec_dur"] = path.path_rec_dur
    result["path_total_play"] = path.path_total_play
    result["path_created_at"] = path.path_created_at
    #result["is_favored"] = is_in_favor_list("path", path.id ,user_auth_id)
    result["path_author_id"] = path.path_user.id
    result["path_thumb"] = path.path_thumb
    result["path_id"] = path.id
    try:
        result["path_author"] = path.path_user.user.startup.mark_name
    except:
        result["path_author"] = path.path_user.mng_name
    result["path_filter"] = []

    for filter in path.path_filter.all():      
        result["path_filter"].append(filter.name)

    result["path_course"]=[]
    for course in path.path_course.all():
        obj_c={}
        obj_c["course_id"] = course.id
        obj_c["course_object"] = course.course_object
        obj_c["course_info"] = course.course_info
        obj_c["course_title"] = course.course_title
        obj_c["course_rec_dur"] = course.course_rec_dur
        obj_c["course_total_play"] = course.course_total_play
        obj_c["course_created_at"] = course.course_created_at
        obj_c["course_thumb"] = course.course_thumb
        try:
            obj_c["course_author"] = course.course_user.own_startup.mark_name
        except:
            obj_c["course_author"] = course.course_user.mng_name
        obj_c["course_entry_point"] = ""
        obj_c["course_filter"]=[]
        for filter in course.course_filter.all():
            print(filter)
            obj_c["course_filter"].append(filter.name)

        obj_c["course_clip"]=[]
        for clip in course.course_clips.all():
            obj = {}
            obj["clip_title"] = clip.clip_title
            obj["clip_created_at"] = clip.clip_created_at
            try:
                obj["clip_author"] = clip.clip_user.user.startup.mark_name
            except:
                obj["clip_author"] = clip.clip_user.mng_name
            obj["clip_thumb"] = clip.clip_thumb
            obj["clip_play"] = clip.clip_play
            obj["clip_id"] = clip.id
            obj_c["course_clip"].append(copy.deepcopy(obj))
        result["path_course"].append(copy.deepcopy(obj_c))

    print(result)
    return JsonResponse(result, safe=False)
vue_get_path_information()

EduFilter object
EduFilter object
EduFilter object
{'path_object': '456', 'path_info': '45', 'path_title': '5645', 'path_rec_dur': '456', 'path_total_play': 2088, 'path_created_at': datetime.date(2018, 11, 6), 'path_author_id': 139, 'path_thumb': 'media/uploads/user/139/company/movie/97487465-rocket-icon-start-up-business-concept.jpg', 'path_id': 65, 'path_author': '담당자-수정 테스트-수정2', 'path_filter': ['디자인 강의', '개발', '기획 실무'], 'path_course': [{'course_id': 92, 'course_object': '234', 'course_info': '234', 'course_title': '56756', 'course_rec_dur': '234', 'course_total_play': 1044, 'course_created_at': datetime.date(2018, 11, 6), 'course_thumb': 'media/uploads/user/139/company/movie/1.JPG', 'course_author': '담당자-수정 테스트-수정2', 'course_entry_point': '', 'course_filter': ['디자인 강의', '개발', '기획 실무'], 'course_clip': [{'clip_title': '234', 'clip_created_at': datetime.date(2018, 11, 2), 'clip_author': '담당자-수정 테스트-수정2', 'clip_thumb': 'https://img.youtube.com/vi/TdJEXTX51xQ/0.jpg', 'clip_play': 522, '

<JsonResponse status_code=200, "application/json">

In [51]:
@my_timer
def vue_get_path_information():

    result = {}
    path = Path.objects.get(id=65)
    result["path_object"] = path.path_object
    result["path_info"] = path.path_info
    result["path_title"] = path.path_title
    result["path_rec_dur"] = path.path_rec_dur
    result["path_total_play"] = path.path_total_play
    result["path_created_at"] = path.path_created_at
    #result["is_favored"] = is_in_favor_list("path", path.id ,user_auth_id)
    result["path_author_id"] = path.path_user.id
    result["path_thumb"] = path.path_thumb
    result["path_id"] = path.id
    try:
        result["path_author"] = path.path_user.user.startup.mark_name
    except:
        result["path_author"] = path.path_user.mng_name
    result["path_filter"] = []

    for filter in path.path_filter.all():      
        result["path_filter"].append(filter.name)

    result["path_course"]=[]
    for course in path.path_course.select_related("course_user").prefetch_related("course_filter").prefetch_related("course_clips"):
        obj_c={}
        obj_c["course_id"] = course.id
        obj_c["course_object"] = course.course_object
        obj_c["course_info"] = course.course_info
        obj_c["course_title"] = course.course_title
        obj_c["course_rec_dur"] = course.course_rec_dur
        obj_c["course_total_play"] = course.course_total_play
        obj_c["course_created_at"] = course.course_created_at
        obj_c["course_thumb"] = course.course_thumb
        try:
            obj_c["course_author"] = course.course_user.own_startup.mark_name
        except:
            obj_c["course_author"] = course.course_user.mng_name
        obj_c["course_entry_point"] = ""
        obj_c["course_filter"]=[]
        for filter in course.course_filter.all():    
            obj_c["course_filter"].append(filter.name)

        obj_c["course_clip"]=[]
        for clip in course.course_clips.select_related("clip_user"):
            obj = {}
            obj["clip_title"] = clip.clip_title
            obj["clip_created_at"] = clip.clip_created_at
            try:
                obj["clip_author"] = clip.clip_user.own_startup.mark_name
            except:
                obj["clip_author"] = clip.clip_user.mng_name
            obj["clip_thumb"] = clip.clip_thumb
            obj["clip_play"] = clip.clip_play
            obj["clip_id"] = clip.id
            obj_c["course_clip"].append(copy.deepcopy(obj))
        result["path_course"].append(copy.deepcopy(obj_c))

    print(result)
    return JsonResponse(result, safe=False)
vue_get_path_information()

{'path_object': '456', 'path_info': '45', 'path_title': '5645', 'path_rec_dur': '456', 'path_total_play': 2088, 'path_created_at': datetime.date(2018, 11, 6), 'path_author_id': 139, 'path_thumb': 'media/uploads/user/139/company/movie/97487465-rocket-icon-start-up-business-concept.jpg', 'path_id': 65, 'path_author': '담당자-수정 테스트-수정2', 'path_filter': ['디자인 강의', '개발', '기획 실무'], 'path_course': [{'course_id': 92, 'course_object': '234', 'course_info': '234', 'course_title': '56756', 'course_rec_dur': '234', 'course_total_play': 1044, 'course_created_at': datetime.date(2018, 11, 6), 'course_thumb': 'media/uploads/user/139/company/movie/1.JPG', 'course_author': '담당자-수정 테스트-수정2', 'course_entry_point': '', 'course_filter': ['디자인 강의', '개발', '기획 실무'], 'course_clip': [{'clip_title': '234', 'clip_created_at': datetime.date(2018, 11, 2), 'clip_author': '담당자-수정 테스트-수정2', 'clip_thumb': 'https://img.youtube.com/vi/TdJEXTX51xQ/0.jpg', 'clip_play': 522, 'clip_id': 131}]}, {'course_id': 93, 'course_object'

<JsonResponse status_code=200, "application/json">

In [52]:
@my_timer
def vue_get_registerd_channel():
 
    result={}
    result["path_list"]=[]
    result["course_list"] =[]
    result["clip_list"]=[]
    for ch in RegisteredChannel.objects.filter(channel_user=AdditionalUserInfo.objects.get(id=74)):
        if ch.path != None:
            p = ch.path
            t = {}
            t["path_title"] = p.path_title
            t["id"] = p.id
            t["path_created_at"] = p.path_created_at

            try:
                t["path_user"] = p.path_user.user.startup.mark_name
            except:
                t["path_user"] = p.path_user.mng_name
            t["path_total_play"] = p.path_total_play
            t["path_thumb"] = p.path_thumb
            t["path_percent"] = 0
            origin_length = int(p.path_total_play)
            view_num = (WatchHistory.objects.filter(
                watch_user=AdditionalUserInfo.objects.get(id=74)) \
                           .filter(watch_path=p)).count() * 6
            try:
                per = round(view_num * 100 / origin_length,2)
                if(per > 100):
                    per = 100
            except:
                per=0
            t["path_percent"] = per
            t["path_entry_point"] = ""
            result["path_list"].append(copy.deepcopy(t))
        if ch.course != None:
            p=ch.course
            t = {}
            t["course_title"] = p.course_title
            t["id"] = p.id
            t["course_created_at"] = p.course_created_at
            try:
                t["course_user"] = p.course_user.user.startup.mark_name
            except:
                t["course_user"] = p.course_user.mng_name
            t["course_total_play"] = p.course_total_play
            t["course_thumb"] = p.course_thumb

            origin_length = int(p.course_total_play)
            view_num = (WatchHistory.objects.filter(
                watch_user=AdditionalUserInfo.objects.get(id=74)) \
                           .filter(watch_course=p)).count() * 6
            try:
                per = round(view_num * 100 / origin_length,2)
                if (per > 100):
                    per = 100
                t["course_percent"] = per
            except:
                t["course_percent"]=""
            try:
                t["course_entry_point"] = ""
            except:
                pass
            result["course_list"].append(copy.deepcopy(t))
        if ch.clip != None:
            p = ch.clip
            t = {}
            t["clip_title"] = p.clip_title
            t["id"] = p.id
            t["clip_created_at"] = p.clip_created_at

            try:
                t["clip_user"] = p.clip_user.user.startup.mark_name
            except:
                t["clip_user"] = p.clip_user.mng_name

            t["clip_play"] = p.clip_play
            t["clip_thumb"] = p.clip_thumb

            origin_length = int(p.clip_play)
            view_num = (WatchHistory.objects.filter(
                watch_user=AdditionalUserInfo.objects.get(id=74)) \
                           .filter(watch_clip=p)).count() * 6
            per = round(view_num * 100 / origin_length,2)
            if (per > 100):
                per = 100
            t["clip_percent"] = per
            try:
                t["clip_entry_point"] =""
            except:
                pass
            result["clip_list"].append(copy.deepcopy(t))

    return  JsonResponse(result, safe = False)
vue_get_registerd_channel()

{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busine

<JsonResponse status_code=200, "application/json">

In [53]:
@my_timer
def vue_get_registerd_channel(): 
    result={}
    result["path_list"]=[]
    result["course_list"] =[]
    result["clip_list"]=[]
    for ch in RegisteredChannel.objects.filter(channel_user=AdditionalUserInfo.objects.get(id=74))\
    .select_related("path__path_user").select_related("course__course_user").select_related("clip__clip_user"):
        if ch.path != None:
            p = ch.path
            t = {}
            t["path_title"] = p.path_title
            t["id"] = p.id
            t["path_created_at"] = p.path_created_at
            try:
                t["path_user"] = p.path_user.own_startup.mark_name
            except:
                t["path_user"] = p.path_user.mng_name
            t["path_total_play"] = p.path_total_play
            t["path_thumb"] = p.path_thumb
            t["path_percent"] = 0
            origin_length = int(p.path_total_play)
            view_num = (WatchHistory.objects.filter(
                watch_user=AdditionalUserInfo.objects.get(id=74)) \
                           .filter(watch_path=p)).count() * 6
            try:
                per = round(view_num * 100 / origin_length,2)
                if(per > 100):
                    per = 100
            except:
                per=0
            t["path_percent"] = per
            t["path_entry_point"] = ""
            result["path_list"].append(copy.deepcopy(t))
        if ch.course != None:
            p=ch.course
            t = {}
            t["course_title"] = p.course_title
            t["id"] = p.id
            t["course_created_at"] = p.course_created_at
            try:
                t["course_user"] = p.course_user.own_startup.mark_name
            except:
                t["course_user"] = p.course_user.mng_name
            t["course_total_play"] = p.course_total_play
            t["course_thumb"] = p.course_thumb

            origin_length = int(p.course_total_play)
            view_num = (WatchHistory.objects.filter(
                watch_user=AdditionalUserInfo.objects.get(id=74)) \
                           .filter(watch_course=p)).count() * 6
            try:
                per = round(view_num * 100 / origin_length,2)
                if (per > 100):
                    per = 100
                t["course_percent"] = per
            except:
                t["course_percent"]=""
            try:
                t["course_entry_point"] = ""
            except:
                pass
            result["course_list"].append(copy.deepcopy(t))
        if ch.clip != None:
            p = ch.clip
            t = {}
            t["clip_title"] = p.clip_title
            t["id"] = p.id
            t["clip_created_at"] = p.clip_created_at

            try:
                t["clip_user"] = p.clip_user.own_startup.mark_name
            except:
                t["clip_user"] = p.clip_user.mng_name

            t["clip_play"] = p.clip_play
            t["clip_thumb"] = p.clip_thumb

            origin_length = int(p.clip_play)
            view_num = (WatchHistory.objects.filter(
                watch_user=AdditionalUserInfo.objects.get(id=74)) \
                           .filter(watch_clip=p)).count() * 6
            per = round(view_num * 100 / origin_length,2)
            if (per > 100):
                per = 100
            t["clip_percent"] = per
            try:
                t["clip_entry_point"] =""
            except:
                pass
            result["clip_list"].append(copy.deepcopy(t))

    return  JsonResponse(result, safe = False)
vue_get_registerd_channel()

{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busine

<JsonResponse status_code=200, "application/json">

In [54]:
@my_timer
def startup_list():
    filter_list = ["출판","일러스트","스타트업","VR","3년 이내","15명 이하"]
    result = Startup.objects.all().exclude(company_name="").exclude(company_name=None)
    for filter in filter_list:
        if filter == "구성원 제한없음":
            pass
        elif "명 이하" in filter or "명 이상" in filter:
            # x 명이 있는 경우에는 구성원을 입력하지 않은 스타트업을 추가해주어야함
            num = int(re.findall('\d+', filter)[0])
            if (num != 0):
                result = copy.deepcopy(result.filter(company_total_employee__lte=num).exclude(company_name="").exclude(
                    company_name=None)) | Startup.objects.all().filter(company_total_employee=None)
        elif filter != None and filter != "":
            result = copy.deepcopy(result.filter(selected_company_filter_list__filter_name=filter))

    result_set = []
    for s in result:
        temp_obj = {}
        temp_obj["company_name"] = s.company_name
        temp_obj["logo"] = s.logo
        temp_obj["company_short_desc"] = s.company_short_desc
        try:
            temp_obj["is_favored"] = is_in_favor_list("startup", s.id, user_auth_id)
        except:
            temp_obj["is_favored"] = False
        temp_obj["filter"] = []
        temp_obj["id"] = s.id
        for t in s.selected_company_filter_list.all():
            if t.filter_name != "" and t.filter_name != None and t.cat_0!="지원형태" and t.cat_1!="기업형태":
                temp_obj["filter"].append(t.filter_name)
        result_set.append(copy.deepcopy(temp_obj))
    return  JsonResponse(list(result_set), safe=False)
startup_list()

{'sql': "SELECT `supporting_business_startup`.`id`, `supporting_business_startup`.`user_id`, `supporting_business_startup`.`company_name`, `supporting_business_startup`.`established_date`, `supporting_business_startup`.`logo`, `supporting_business_startup`.`back_img`, `supporting_business_startup`.`company_short_desc`, `supporting_business_startup`.`company_intro`, `supporting_business_startup`.`company_youtube`, `supporting_business_startup`.`company_facebook`, `supporting_business_startup`.`company_instagram`, `supporting_business_startup`.`company_website`, `supporting_business_startup`.`address_0`, `supporting_business_startup`.`address_1`, `supporting_business_startup`.`repre_name`, `supporting_business_startup`.`repre_email`, `supporting_business_startup`.`repre_tel`, `supporting_business_startup`.`mark_name`, `supporting_business_startup`.`mark_email`, `supporting_business_startup`.`mark_tel`, `supporting_business_startup`.`company_keyword`, `supporting_business_startup`.`compan

<JsonResponse status_code=200, "application/json">

In [55]:

@my_timer
def vue_get_opr_dashboard():
 
    mng_list = []

    for a in AdditionalUserInfo.objects.get(id=7).additionaluserinfo_set.all():
        mng_list.append(a.id)
    result = []
    # 모집 마감된 공고

    end = SupportBusiness.objects.filter(support_business_apply_end_ymdt__lt=datetime.now()).filter(
            Q(support_business_status="4") | Q(support_business_status="3")).filter(
            support_business_author_id__in=mng_list).count()

    if(True):
        end_support_business = SupportBusiness.objects.filter(support_business_apply_end_ymdt__lt=datetime.now()).filter(
            Q(support_business_status="4") | Q(support_business_status="3")).filter(
            support_business_author_id__in=mng_list)
        end_set = []
        for support_business in end_support_business:
            result_end = {}
            result_end["opr_support_business_award_date_ymd"] = support_business.support_business_pro_0_open_ymd
            result_end['opr_support_business_name'] = support_business.support_business_name
            result_end["opr_support_business_apply_start_ymd"] = support_business.support_business_apply_start_ymd
            result_end["opr_support_business_apply_end_ymdt"] = support_business.support_business_apply_end_ymdt
            result_end["opr_id"] = support_business.id
            result_end["opr_support_business_author_id"] = support_business.support_business_author.id
            result_end["opr_support_business_poster"] = support_business.support_business_poster
            result_end["opr_apply_num"] = (
            Appliance.objects.filter(support_business_id=support_business.id).filter(is_submit=True)).count()
            result_end["opr_favorite"] = (AdditionalUserInfo.objects.filter(favorite=support_business)).count()
            if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
                try:
                    number = str(round((
                                           Appliance.objects.filter(support_business_id=support_business.id).filter(
                                               is_submit=True)).count() / int(
                        support_business.support_business_recruit_size), 1))
                    if number == "0.0":
                        number = "0"
                    result_end["opr_comp"] = number + " : 1"
                except:
                    result_end["opr_comp"] = str((
                                                     Appliance.objects.filter(
                                                         support_business_id=support_business.id).filter(
                                                         is_submit=True)).count()) + " : 1"
            else:
                result_end["opr_comp"] = str((Appliance.objects.filter(support_business_id=support_business.id).filter(
                    is_submit=True)).count()) + " : 1"
            result.append(copy.deepcopy(result_end))


    wating =  waiting_support_business = SupportBusiness.objects.filter(support_business_status="2").filter(
            support_business_author_id__in=mng_list).count()
    if(True) :
        # 승인 요청중인 공고
        waiting_support_business = SupportBusiness.objects.filter(support_business_status="2").filter(
            support_business_author_id__in=mng_list)
        waiting_set = []
        for support_business in waiting_support_business:
            result_end = {}
            result_end["opr_id"] = support_business.id
            result_end["opr_support_business_award_date_ymd"] = \
            str(support_business.support_business_update_at_ymdt).split(" ")[0]
            result_end['opr_support_business_name'] = support_business.support_business_name
            result_end["opr_support_business_apply_start_ymd"] = support_business.support_business_apply_start_ymd
            result_end["opr_support_business_apply_end_ymdt"] = support_business.support_business_apply_end_ymdt
            result_end["opr_support_business_update_at_ymdt"] = support_business.support_business_update_at_ymdt
            result_end["opr_support_business_poster"] = support_business.support_business_poster
            result_end["opr_apply_num"] = (
            Appliance.objects.filter(support_business_id=support_business.id).filter(is_submit=True)).count()
            result_end["opr_favorite"] = (AdditionalUserInfo.objects.filter(favorite=support_business)).count()
            result_end["opr_comp"] = "0 : 1"
            result.append(copy.deepcopy(result_end))
    ing =  SupportBusiness.objects.filter(support_business_status="3").filter(
            support_business_apply_end_ymdt__gte=timezone.now()).filter(support_business_author_id__in=mng_list).count()
    if(True):
        # 공고중인 공고
        ing_support_business = SupportBusiness.objects.filter(support_business_status="3").filter(
            support_business_apply_end_ymdt__gte=timezone.now()).filter(support_business_author_id__in=mng_list)
        ing_set = []
        for support_business in ing_support_business:
            result_end = {}
            result_end["opr_id"] = support_business.id
            result_end["opr_support_business_award_date_ymd"] = support_business.support_business_pro_0_open_ymd
            result_end['opr_support_business_name'] = support_business.support_business_name
            result_end["opr_support_business_apply_start_ymd"] = support_business.support_business_apply_start_ymd
            result_end["opr_support_business_apply_end_ymdt"] = support_business.support_business_apply_end_ymdt
            result_end["opr_support_business_poster"] = support_business.support_business_poster
            result_end["opr_apply_num"] = (
            Appliance.objects.filter(support_business_id=support_business.id).filter(is_submit=True)).count()
            result_end["opr_favorite"] = (AdditionalUserInfo.objects.filter(favorite=support_business)).count()
            result_end["opr_support_business_author_id"] = support_business.support_business_author.id
            result_end["opr_open_date"] = (support_business.support_business_created_at_ymdt)
            if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
                try:
                    number = str(round((
                                           Appliance.objects.filter(support_business_id=support_business.id).filter(
                                               is_submit=True)).count() / int(
                        support_business.support_business_recruit_size), 1))
                    if number == "0.0":
                        number = "0"
                    result_end["opr_comp"] = number + " : 1"
                except:
                    result_end["opr_comp"] = str((
                                                     Appliance.objects.filter(
                                                         support_business_id=support_business.id).filter(
                                                         is_submit=True)).count()) + " : 1"
            else:
                result_end["opr_comp"] = ""
            result_end["opr_favorite"] = (AdditionalUserInfo.objects.filter(favorite=support_business)).count()
            result.append(copy.deepcopy(result_end))
    return JsonResponse({ "result_set" : result, "set_num":{"end":end, "ing":ing, "waiting" : wating,} }, safe=False)
vue_get_opr_dashboard()

{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busine

<JsonResponse status_code=200, "application/json">

In [56]:

@my_timer
def vue_get_opr_dashboard():
 
    mng_list = []

    for a in AdditionalUserInfo.objects.get(id=7).additionaluserinfo_set.all():
        mng_list.append(a.id)
    result = []
    # 모집 마감된 공고

    end = SupportBusiness.objects.filter(support_business_apply_end_ymdt__lt=datetime.now()).filter(
            Q(support_business_status="4") | Q(support_business_status="3")).filter(
            support_business_author_id__in=mng_list).count()

    if(True):
        end_support_business = SupportBusiness.objects.filter(support_business_apply_end_ymdt__lt=datetime.now()).filter(
            Q(support_business_status="4") | Q(support_business_status="3")).filter(
            support_business_author_id__in=mng_list).prefetch_related("appliance_set").prefetch_related("additionaluserinfo_set").select_related("support_business_author")
        end_set = []
        for support_business in end_support_business:
            result_end = {}
            result_end["opr_support_business_award_date_ymd"] = support_business.support_business_pro_0_open_ymd
            result_end['opr_support_business_name'] = support_business.support_business_name
            result_end["opr_support_business_apply_start_ymd"] = support_business.support_business_apply_start_ymd
            result_end["opr_support_business_apply_end_ymdt"] = support_business.support_business_apply_end_ymdt
            result_end["opr_id"] = support_business.id
            result_end["opr_support_business_author_id"] = support_business.support_business_author.id
            result_end["opr_support_business_poster"] = support_business.support_business_poster
            result_end["opr_apply_num"] = (support_business.appliance_set.filter(is_submit=True)).count()
            result_end["opr_favorite"] = (support_business.additionaluserinfo_set).count()
            if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
                try:
                    number = str(round((
                                          result_end["opr_apply_num"] / int(
                        support_business.support_business_recruit_size), 1)))
                    if number == "0.0":
                        number = "0"
                    result_end["opr_comp"] = number + " : 1"
                except:
                    result_end["opr_comp"] = str(result_end["opr_apply_num"] )+ " : 1"
            else:
                result_end["opr_comp"] = str(result_end["opr_apply_num"]) + " : 1"
            result.append(copy.deepcopy(result_end))

    wating =  waiting_support_business = SupportBusiness.objects.filter(support_business_status="2").filter(
            support_business_author_id__in=mng_list).count()
    if(True) :
        # 승인 요청중인 공고
        waiting_support_business = SupportBusiness.objects.filter(support_business_status="2").filter(
            support_business_author_id__in=mng_list).prefetch_related("appliance_set").prefetch_related("additionaluserinfo_set").select_related("support_business_author")
        waiting_set = []
        for support_business in waiting_support_business:
            result_end = {}
            result_end["opr_id"] = support_business.id
            result_end["opr_support_business_award_date_ymd"] = \
            str(support_business.support_business_update_at_ymdt).split(" ")[0]
            result_end['opr_support_business_name'] = support_business.support_business_name
            result_end["opr_support_business_apply_start_ymd"] = support_business.support_business_apply_start_ymd
            result_end["opr_support_business_apply_end_ymdt"] = support_business.support_business_apply_end_ymdt
            result_end["opr_support_business_update_at_ymdt"] = support_business.support_business_update_at_ymdt
            result_end["opr_support_business_poster"] = support_business.support_business_poster
            result_end["opr_apply_num"] = (support_business.appliance_set.filter(is_submit=True)).count()
            result_end["opr_favorite"] =(support_business.additionaluserinfo_set).count()
            if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
                try:
                    number = str(round(( result_end["opr_apply_num"] / int(
                        support_business.support_business_recruit_size), 1)))
                    if number == "0.0":
                        number = "0"
                    result_end["opr_comp"] = number + " : 1"
                except:
                    result_end["opr_comp"] = str(result_end["opr_apply_num"] )+ " : 1"
            else:
                result_end["opr_comp"] = str(result_end["opr_apply_num"]) + " : 1"
            result.append(copy.deepcopy(result_end))
    ing =  SupportBusiness.objects.filter(support_business_status="3").filter(
            support_business_apply_end_ymdt__gte=timezone.now()).filter(support_business_author_id__in=mng_list).count()
    if(True):
        # 공고중인 공고
        ing_support_business = SupportBusiness.objects.filter(support_business_status="3").filter(
            support_business_apply_end_ymdt__gte=timezone.now()).filter(support_business_author_id__in=mng_list)\
        .prefetch_related("appliance_set").prefetch_related("additionaluserinfo_set").select_related("support_business_author")
        ing_set = []
        for support_business in ing_support_business:
            result_end = {}
            result_end["opr_id"] = support_business.id
            result_end["opr_support_business_award_date_ymd"] = support_business.support_business_pro_0_open_ymd
            result_end['opr_support_business_name'] = support_business.support_business_name
            result_end["opr_support_business_apply_start_ymd"] = support_business.support_business_apply_start_ymd
            result_end["opr_support_business_apply_end_ymdt"] = support_business.support_business_apply_end_ymdt
            result_end["opr_support_business_poster"] = support_business.support_business_poster
            result_end["opr_apply_num"] = (support_business.appliance_set.filter(is_submit=True)).count()
            result_end["opr_favorite"] =(support_business.additionaluserinfo_set).count()
            result_end["opr_support_business_author_id"] = support_business.support_business_author.id
            result_end["opr_open_date"] = (support_business.support_business_created_at_ymdt)
            if support_business.support_business_recruit_size != "" and support_business.support_business_recruit_size != 0 and support_business.support_business_recruit_size != None:
                try:
                    number = str(round( result_end["opr_apply_num"] / int(support_business.support_business_recruit_size), 1))
                    if number == "0.0" :
                        number = "0"
                    result_end["opr_comp"] = number + " : 1"
                except:
                    result_end["opr_comp"] = str( result_end["opr_apply_num"]) + " : 1"
            else:
                result_end["opr_comp"] = ""
           
            result.append(copy.deepcopy(result_end))
    return JsonResponse({ "result_set" : result, "set_num":{"end":end, "ing":ing, "waiting" : wating,} }, safe=False)
vue_get_opr_dashboard()

{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busine

<JsonResponse status_code=200, "application/json">

In [57]:
@my_timer
def vue_get_opr_acc():

    id = 11
    mng_acc = AdditionalUserInfo.objects.get(id=id)
    temp={}
    temp["opr_additional_user_id"] = mng_acc.id
    temp["opr_id"] = mng_acc.user.username
    temp["opr_name"] = mng_acc.mng_name
    temp["opr_kikwan"] = mng_acc.mng_kikwan
    temp["opr_bonbu"] = mng_acc.mng_bonbu
    temp["opr_team"] = mng_acc.mng_team
    temp["opr_position"] = mng_acc.mng_position
    temp["opr_tel"] = mng_acc.mng_tel
    temp["opr_phone"] = mng_acc.mng_phone
    temp["opr_email"] = mng_acc.mng_email
    temp["opr_website"] = mng_acc.mng_website
    print(connection.queries)
    return JsonResponse((temp), safe = False)
vue_get_opr_acc()

[{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busin

<JsonResponse status_code=200, "application/json">

In [58]:
@my_timer
def opr_vue_get_kikwan_account():

    opr_account_set = []
    k=1
    opr_all_account_set=[]
    for ac in  AdditionalUserInfo.objects.filter(mng_boss_id=11).order_by("-id"):
        temp={}
        temp["opr_index"] = k
        k=k+1
        temp["opr_id"] = ac.user.username
        temp["opr_mng_name"] = ac.mng_name
        temp["opr_mng_position"] = ac.mng_position
        temp["opr_mng_bonbu"] = ac.mng_bonbu
        temp["opr_mng_kikwan"] = ac.mng_kikwan
        temp["opr_mng_team"] = ac.mng_team
        temp["opr_mng_tel"] = ac.mng_tel
        temp["opr_mng_phone"] = ac.mng_phone
        temp["opr_mng_email"] = ac.mng_email
        temp["opr_mng_date_joined_ymd"] = ac.mng_date_joined_ymd
        opr_account_set.append(copy.deepcopy(temp))
    k=1
    for ac in AdditionalUserInfo.objects.filter(Q(auth="MNG")|Q(auth="OPR")|Q(auth="4")).order_by("-id"):
        temp = {}
        temp["opr_index"] = k
        k = k + 1
        temp["opr_id"] = ac.user.username
        temp["opr_mng_name"] = ac.mng_name
        temp["opr_mng_position"] = ac.mng_position
        temp["opr_mng_bonbu"] = ac.mng_bonbu
        temp["opr_mng_kikwan"] = ac.mng_kikwan
        temp["opr_mng_team"] = ac.mng_team
        try:
            temp["opr_mng_sangsa"] = ac.mng_boss.mng_name
        except:
            temp["opr_mng_sangsa"] = ""
        temp["opr_mng_tel"] = ac.mng_tel
        temp["opr_mng_phone"] = ac.mng_phone
        temp["opr_mng_email"] = ac.mng_email
        temp["opr_mng_date_joined_ymd"] = ac.mng_date_joined_ymd
        opr_all_account_set.append(copy.deepcopy(temp))
    result={}
    result["opr_account_set"] = opr_account_set
    result["opr_all_account_set"] = opr_all_account_set

    return  JsonResponse(result, safe=False)
opr_vue_get_kikwan_account()

{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busine

<JsonResponse status_code=200, "application/json">

In [59]:
@my_timer
def opr_vue_get_kikwan_account():

    opr_account_set = []
    k=1
    opr_all_account_set=[]
    for ac in  AdditionalUserInfo.objects.filter(mng_boss_id=11).order_by("-id").prefetch_related("user"):
        temp={}
        temp["opr_index"] = k
        k=k+1
        temp["opr_id"] = ac.user.username
        temp["opr_mng_name"] = ac.mng_name
        temp["opr_mng_position"] = ac.mng_position
        temp["opr_mng_bonbu"] = ac.mng_bonbu
        temp["opr_mng_kikwan"] = ac.mng_kikwan
        temp["opr_mng_team"] = ac.mng_team
        temp["opr_mng_tel"] = ac.mng_tel
        temp["opr_mng_phone"] = ac.mng_phone
        temp["opr_mng_email"] = ac.mng_email
        temp["opr_mng_date_joined_ymd"] = ac.mng_date_joined_ymd
        opr_account_set.append(copy.deepcopy(temp))
    k=1
    for ac in AdditionalUserInfo.objects.filter(Q(auth="MNG")|Q(auth="OPR")|Q(auth="4")).order_by("-id").select_related("user")\
    .select_related("mng_boss"):
        temp = {}
        temp["opr_index"] = k
        k = k + 1
        temp["opr_id"] = ac.user.username
        temp["opr_mng_name"] = ac.mng_name
        temp["opr_mng_position"] = ac.mng_position
        temp["opr_mng_bonbu"] = ac.mng_bonbu
        temp["opr_mng_kikwan"] = ac.mng_kikwan
        temp["opr_mng_team"] = ac.mng_team
        try:
            temp["opr_mng_sangsa"] = ac.mng_boss.mng_name
        except:
            temp["opr_mng_sangsa"] = ""
        temp["opr_mng_tel"] = ac.mng_tel
        temp["opr_mng_phone"] = ac.mng_phone
        temp["opr_mng_email"] = ac.mng_email
        temp["opr_mng_date_joined_ymd"] = ac.mng_date_joined_ymd
        opr_all_account_set.append(copy.deepcopy(temp))
    result={}
    result["opr_account_set"] = opr_account_set
    result["opr_all_account_set"] = opr_all_account_set

    return  JsonResponse(result, safe=False)
opr_vue_get_kikwan_account()

{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busine

<JsonResponse status_code=200, "application/json">

In [60]:
@my_timer
def vue_get_mng_list():
    id = 7
    mngs = AdditionalUserInfo.objects.get(id=id).additionaluserinfo_set.all()
    m_list= []
    for m in mngs:
        temp={}
        temp["id"] = m.id
        temp["mng_name"] = m.mng_name
        temp["support_business"] =[]
        for s in SupportBusiness.objects.filter(support_business_author=m):
            ttem={}
            ttem["support_business_name"] = s.support_business_name
            ttem["id"] = s.id
            temp["support_business"].append(copy.deepcopy(ttem))
        m_list.append(copy.deepcopy(temp))
    return JsonResponse(m_list, safe = False)
vue_get_mng_list()

{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busine

<JsonResponse status_code=200, "application/json">

In [113]:
@my_timer
def vue_get_mng_list():
    id = 7
    mngs = AdditionalUserInfo.objects.get(id=id).additionaluserinfo_set.prefetch_related("supportbusiness_set")
    m_list= []
    for m in mngs:
        temp={}
        temp["id"] = m.id
        temp["mng_name"] = m.mng_name
        temp["support_business"] =[]
        for s in m.supportbusiness_set.all():
            ttem={}
            ttem["support_business_name"] = s.support_business_name
            ttem["id"] = s.id
            temp["support_business"].append(copy.deepcopy(ttem))
        m_list.append(copy.deepcopy(temp))
    return JsonResponse(m_list, safe = False)
vue_get_mng_list()

{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busine

<JsonResponse status_code=200, "application/json">

In [112]:
mng = AdditionalUserInfo.objects.get(id=11) # 11 번 매니저
for su in mng.supportbusiness_set.all():
    print(su.support_business_name)
    print(su.support_business_author_id)

테스트 지원사업
11
ㄴㅇㄹㄴㅇㄹ
11
234
11
새로고침 테스트 지원사업
11
테스트 지원사업명
11
아이디 클래스로 변경후 테스트하는 공고문 
11
기업 참여 공고문
11
테스트 공고문
11
지원서 양식테스트
11
123
11
슈퍼끼어로 시즌5 참가자 모집
11
234
11
테스트입니다.
11
테스트입니다.
11
지원서 양식테스트
11
공고종료 테스트입니다.
11
공고종료 테스트123
11
2017 충주 고구마 축제
11
111222333777
11
바텀 컨트롤 이벤트 제거지원사업 공고문 등록
11
123_123
11
131_131
11
테스트입니다.
11
fefgsfg
11
테스트
11
138번 사업
11
1022테스트
11
테스트 넥스트 지원사업
11
1030
11
1101테스트입니다.
11
123
11
2018년 제2차 경기글로벌게임센터 신규 입주기업 모집
11
구석구석 움직이는 경기공방 참여자(단체/기관) 모집계획
11
첨부서류 오류 테스트
11
파일 첨부 테스트 다시 사용
11
포스터가 없는 공고
11
2018년 경기도 다양성영화 국제영화제 참가지원
11
구석구석 움직이는 경기공방‘ 메이커스 분야 모집
11
파일 여러개 업로드 테스트
11
연도/회차/기수‘사업명’모집/지원/참여
11
제 1회 테스트 
11
ㅇㄹㄹㄹ
11
아침테스트
11
첨부서류 테스트 공고문
11
2018 인기가요
11
ㅊㅍㅊㅊㅊㅊ
11
2018년 경기도 다양성영화 국제영화제 참가지원
11
2018년 2차 글로벌 게임센터 입주 모집
11
2018 피땀눈물
11
cafe 501
11
당신은 참 나에게 참
11
테스트트트
11
일러스트 레이터의 속마음
11
구석구석 움직이는 경기공방‘ 메이커스 분야 모집 
11
구석구석 움직이는 경기공방‘ 메이커스 분야 모집 
11
2018/12/10
11


In [62]:
@my_timer
def mng_vue_get_kikwan_account():
  
    opr_account_set = []
    k = 1
    opr_all_account_set = []
    result={}
    boss_id = AdditionalUserInfo.objects.get(id =11).mng_boss_id

    for ac in AdditionalUserInfo.objects.filter(mng_boss_id=boss_id).order_by("-id"):
        temp = {}
        temp["mng_index"] = k
        k = k + 1
        temp["mng_id"] = ac.user.username
        temp["mng_mng_name"] = ac.mng_name
        temp["mng_mng_position"] = ac.mng_position
        temp["mng_mng_bonbu"] = ac.mng_bonbu
        temp["mng_mng_kikwan"] = ac.mng_kikwan
        temp["mng_mng_team"] = ac.mng_team
        temp["mng_mng_tel"] = ac.mng_tel
        temp["mng_mng_phone"] = ac.mng_phone
        temp["mng_mng_email"] = ac.mng_email
        temp["mng_mng_date_joined_ymd"] = ac.mng_date_joined_ymd
        opr_account_set.append(copy.deepcopy(temp))
    k = 1

    result["opr_account_set"] = opr_account_set

    return JsonResponse(result, safe=False)
mng_vue_get_kikwan_account()

{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busine

<JsonResponse status_code=200, "application/json">

In [63]:
 @my_timer
def mng_vue_get_kikwan_account():
  
    opr_account_set = []
    k = 1
    opr_all_account_set = []
    result={}
    boss_id = AdditionalUserInfo.objects.get(id =11).mng_boss_id

    for ac in AdditionalUserInfo.objects.filter(mng_boss_id=boss_id).order_by("-id").select_related("user"):
        temp = {}
        temp["mng_index"] = k
        k = k + 1
        temp["mng_id"] = ac.user.username
        temp["mng_mng_name"] = ac.mng_name
        temp["mng_mng_position"] = ac.mng_position
        temp["mng_mng_bonbu"] = ac.mng_bonbu
        temp["mng_mng_kikwan"] = ac.mng_kikwan
        temp["mng_mng_team"] = ac.mng_team
        temp["mng_mng_tel"] = ac.mng_tel
        temp["mng_mng_phone"] = ac.mng_phone
        temp["mng_mng_email"] = ac.mng_email
        temp["mng_mng_date_joined_ymd"] = ac.mng_date_joined_ymd
        opr_account_set.append(copy.deepcopy(temp))
    k = 1

    result["opr_account_set"] = opr_account_set

    return JsonResponse(result, safe=False)
mng_vue_get_kikwan_account()

{'sql': 'SELECT `supporting_business_additionaluserinfo`.`id`, `supporting_business_additionaluserinfo`.`user_id`, `supporting_business_additionaluserinfo`.`auth`, `supporting_business_additionaluserinfo`.`is_superuser`, `supporting_business_additionaluserinfo`.`avatar`, `supporting_business_additionaluserinfo`.`own_startup_id`, `supporting_business_additionaluserinfo`.`agreement`, `supporting_business_additionaluserinfo`.`repre_name`, `supporting_business_additionaluserinfo`.`repre_tel`, `supporting_business_additionaluserinfo`.`repre_email`, `supporting_business_additionaluserinfo`.`mng_name`, `supporting_business_additionaluserinfo`.`mng_tel`, `supporting_business_additionaluserinfo`.`mng_phone`, `supporting_business_additionaluserinfo`.`mng_email`, `supporting_business_additionaluserinfo`.`mng_position`, `supporting_business_additionaluserinfo`.`mng_bonbu`, `supporting_business_additionaluserinfo`.`mng_kikwan`, `supporting_business_additionaluserinfo`.`mng_team`, `supporting_busine

<JsonResponse status_code=200, "application/json">